In [95]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import xgboost as xgb
import lightgbm as lgb
import statsmodels.api as sm
import warnings
import shap
from sklearn.model_selection import KFold
from sklearn.model_selection import cross_validate
from sklearn.ensemble import VotingClassifier
from sklearn.ensemble import VotingRegressor
from sklearn.preprocessing import StandardScaler
from sklearn.preprocessing import RobustScaler
from sklearn.preprocessing import MinMaxScaler
from sklearn.model_selection import StratifiedKFold
from pycaret.regression import *
from xgboost import XGBRegressor
from xgboost import XGBClassifier
from sklearn.tree import ExtraTreeClassifier
from sklearn.tree import ExtraTreeRegressor
from sklearn.experimental import enable_iterative_imputer 
from sklearn.impute import KNNImputer
from sklearn.impute import IterativeImputer
from sklearn.ensemble import GradientBoostingClassifier
from sklearn.ensemble import GradientBoostingRegressor
from sklearn.tree import DecisionTreeClassifier
from sklearn.svm import SVC
from sklearn.preprocessing import MinMaxScaler
from sklearn.preprocessing import OneHotEncoder
from sklearn.preprocessing import LabelEncoder
from sklearn.model_selection import train_test_split
from sklearn.model_selection import GridSearchCV
from sklearn.model_selection import RandomizedSearchCV
from sklearn.ensemble import RandomForestClassifier
from sklearn.ensemble import RandomForestRegressor
from catboost import CatBoostClassifier, Pool
from sklearn.ensemble import AdaBoostClassifier
from sklearn.ensemble import AdaBoostRegressor
from catboost import CatBoostRegressor
from catboost import CatBoostClassifier
from sklearn.metrics import mean_squared_error
from sklearn.impute import KNNImputer
from sklearn.decomposition import PCA

In [96]:
warnings.simplefilter(action='ignore')
pd.set_option('display.max_columns', None)

# Data

In [204]:
train_data = pd.read_csv("./train.csv")
train_data

PRODUCT_ID  Y_Class  Y_Quality         TIMESTAMP     LINE PRODUCT_CODE  \
0    TRAIN_000        1   0.533433   2022-06-13 5:14  T050304         A_31   
1    TRAIN_001        2   0.541819   2022-06-13 5:22  T050307         A_31   
2    TRAIN_002        1   0.531267   2022-06-13 5:30  T050304         A_31   
3    TRAIN_003        2   0.537325   2022-06-13 5:39  T050307         A_31   
4    TRAIN_004        1   0.531590   2022-06-13 5:47  T050304         A_31   
..         ...      ...        ...               ...      ...          ...   
593  TRAIN_593        1   0.526546  2022-09-08 14:30  T100306         T_31   
594  TRAIN_594        0   0.524022  2022-09-08 22:38  T050304         A_31   
595  TRAIN_595        0   0.521289  2022-09-08 22:47  T050304         A_31   
596  TRAIN_596        1   0.531375  2022-09-08 14:38  T100304         O_31   
597  TRAIN_597        1   0.533702  2022-09-08 14:46  T100306         O_31   

      X_1   X_2  X_3   X_4  ...  X_2866  X_2867  X_2868  X_2869  X_2870  \
0     NaN   NaN  NaN   NaN  ...   39.34   40.89   32.56   34.09   77.77   
1     NaN   NaN  NaN   NaN  ...   38.89   42.82   43.92   35.34   72.55   
2     NaN   NaN  NaN   NaN  ...   39.19   36.65   42.47   36.53   78.35   
3     NaN   NaN  NaN   NaN  ...   37.74   39.17   52.17   30.58   71.78   
4     NaN   NaN  NaN   NaN  ...   38.70   41.89   46.93   33.09   76.97   
..    ...   ...  ...   ...  ...     ...     ...     ...     ...     ...   
593   2.0  95.0  0.0  45.0  ...     NaN     NaN     NaN     NaN     NaN   
594   NaN   NaN  NaN   NaN  ...   49.47   53.07   50.89   55.10   66.49   
595   NaN   NaN  NaN   NaN  ...     NaN     NaN     NaN     NaN     NaN   
596  40.0  94.0  0.0  45.0  ...     NaN     NaN     NaN     NaN     NaN   
597  21.0  87.0  0.0  45.0  ...     NaN     NaN     NaN     NaN     NaN   

     X_2871  X_2872  X_2873  X_2874  X_2875  
0       NaN     NaN     NaN     NaN     NaN  
1       NaN     NaN     NaN     NaN     NaN  
2       NaN     NaN     NaN     NaN     NaN  
3       NaN     NaN     NaN     NaN     NaN  
4       NaN     NaN     NaN     NaN     NaN  
..      ...     ...     ...     ...     ...  
593     NaN     NaN     NaN     NaN     NaN  
594     1.0     NaN     NaN     NaN     NaN  
595     1.0     NaN     NaN     NaN     NaN  
596     NaN     NaN     NaN     NaN     NaN  
597     NaN     NaN     NaN     NaN     NaN  

[598 rows x 2881 columns]

In [205]:
train_data['YEAR'] =  pd.to_datetime(train_data['TIMESTAMP']).dt.year
train_data['MONTH'] =  pd.to_datetime(train_data['TIMESTAMP']).dt.month
train_data['DAY'] =  pd.to_datetime(train_data['TIMESTAMP']).dt.day
train_data['HOUR'] =  pd.to_datetime(train_data['TIMESTAMP']).dt.hour
train_data['MINUTE'] =  pd.to_datetime(train_data['TIMESTAMP']).dt.minute
train_data['DAY_OF_WEEK'] =  pd.to_datetime(train_data['TIMESTAMP']).dt.day_name()

In [206]:
train_data = train_data.drop(['MONTH', 'DAY', 'YEAR'], axis = 1)

In [207]:
train_data.loc[(train_data.PRODUCT_CODE == 'A_31')&(train_data.LINE == 'T010305'),'LINE_AND_CODE'] = 0
train_data.loc[(train_data.PRODUCT_CODE == 'A_31')&(train_data.LINE == 'T010306'),'LINE_AND_CODE'] = 1
train_data.loc[(train_data.PRODUCT_CODE == 'A_31')&(train_data.LINE == 'T050304'),'LINE_AND_CODE'] = 2
train_data.loc[(train_data.PRODUCT_CODE == 'A_31')&(train_data.LINE == 'T050307'),'LINE_AND_CODE'] = 3
train_data.loc[(train_data.PRODUCT_CODE == 'A_31')&(train_data.LINE == 'T100304'),'LINE_AND_CODE'] = 4
train_data.loc[(train_data.PRODUCT_CODE == 'A_31')&(train_data.LINE == 'T100306'),'LINE_AND_CODE'] = 5

train_data.loc[(train_data.PRODUCT_CODE == 'T_31')&(train_data.LINE == 'T010305'),'LINE_AND_CODE'] = 6
train_data.loc[(train_data.PRODUCT_CODE == 'T_31')&(train_data.LINE == 'T010306'),'LINE_AND_CODE'] = 7
train_data.loc[(train_data.PRODUCT_CODE == 'T_31')&(train_data.LINE == 'T050304'),'LINE_AND_CODE'] = 8
train_data.loc[(train_data.PRODUCT_CODE == 'T_31')&(train_data.LINE == 'T050307'),'LINE_AND_CODE'] = 9
train_data.loc[(train_data.PRODUCT_CODE == 'T_31')&(train_data.LINE == 'T100304'),'LINE_AND_CODE'] = 10
train_data.loc[(train_data.PRODUCT_CODE == 'T_31')&(train_data.LINE == 'T100306'),'LINE_AND_CODE'] = 11

train_data.loc[(train_data.PRODUCT_CODE == 'O_31')&(train_data.LINE == 'T010305'),'LINE_AND_CODE'] = 12
train_data.loc[(train_data.PRODUCT_CODE == 'O_31')&(train_data.LINE == 'T010306'),'LINE_AND_CODE'] = 13
train_data.loc[(train_data.PRODUCT_CODE == 'O_31')&(train_data.LINE == 'T050304'),'LINE_AND_CODE'] = 14
train_data.loc[(train_data.PRODUCT_CODE == 'O_31')&(train_data.LINE == 'T050307'),'LINE_AND_CODE'] = 15
train_data.loc[(train_data.PRODUCT_CODE == 'O_31')&(train_data.LINE == 'T100304'),'LINE_AND_CODE'] = 16
train_data.loc[(train_data.PRODUCT_CODE == 'O_31')&(train_data.LINE == 'T100306'),'LINE_AND_CODE'] = 17
train_data

PRODUCT_ID  Y_Class  Y_Quality         TIMESTAMP     LINE PRODUCT_CODE  \
0    TRAIN_000        1   0.533433   2022-06-13 5:14  T050304         A_31   
1    TRAIN_001        2   0.541819   2022-06-13 5:22  T050307         A_31   
2    TRAIN_002        1   0.531267   2022-06-13 5:30  T050304         A_31   
3    TRAIN_003        2   0.537325   2022-06-13 5:39  T050307         A_31   
4    TRAIN_004        1   0.531590   2022-06-13 5:47  T050304         A_31   
..         ...      ...        ...               ...      ...          ...   
593  TRAIN_593        1   0.526546  2022-09-08 14:30  T100306         T_31   
594  TRAIN_594        0   0.524022  2022-09-08 22:38  T050304         A_31   
595  TRAIN_595        0   0.521289  2022-09-08 22:47  T050304         A_31   
596  TRAIN_596        1   0.531375  2022-09-08 14:38  T100304         O_31   
597  TRAIN_597        1   0.533702  2022-09-08 14:46  T100306         O_31   

      X_1   X_2  X_3   X_4  ...  X_2870  X_2871  X_2872  X_2873  X_2874  \
0     NaN   NaN  NaN   NaN  ...   77.77     NaN     NaN     NaN     NaN   
1     NaN   NaN  NaN   NaN  ...   72.55     NaN     NaN     NaN     NaN   
2     NaN   NaN  NaN   NaN  ...   78.35     NaN     NaN     NaN     NaN   
3     NaN   NaN  NaN   NaN  ...   71.78     NaN     NaN     NaN     NaN   
4     NaN   NaN  NaN   NaN  ...   76.97     NaN     NaN     NaN     NaN   
..    ...   ...  ...   ...  ...     ...     ...     ...     ...     ...   
593   2.0  95.0  0.0  45.0  ...     NaN     NaN     NaN     NaN     NaN   
594   NaN   NaN  NaN   NaN  ...   66.49     1.0     NaN     NaN     NaN   
595   NaN   NaN  NaN   NaN  ...     NaN     1.0     NaN     NaN     NaN   
596  40.0  94.0  0.0  45.0  ...     NaN     NaN     NaN     NaN     NaN   
597  21.0  87.0  0.0  45.0  ...     NaN     NaN     NaN     NaN     NaN   

     X_2875  HOUR  MINUTE  DAY_OF_WEEK  LINE_AND_CODE  
0       NaN     5      14       Monday            2.0  
1       NaN     5      22       Monday            3.0  
2       NaN     5      30       Monday            2.0  
3       NaN     5      39       Monday            3.0  
4       NaN     5      47       Monday            2.0  
..      ...   ...     ...          ...            ...  
593     NaN    14      30     Thursday           11.0  
594     NaN    22      38     Thursday            2.0  
595     NaN    22      47     Thursday            2.0  
596     NaN    14      38     Thursday           16.0  
597     NaN    14      46     Thursday           17.0  

[598 rows x 2885 columns]

In [208]:
colls = []
for coll in train_data :
    if 'X' in coll and train_data[coll].isna().sum() == 598 :
        colls.append(coll)
print(len(colls))

82


In [209]:
train_data.drop(colls, inplace = True, axis = 1)

In [210]:
train_data.loc[train_data.PRODUCT_CODE == 'A_31','PRODUCT_CODE'] = 1
train_data.loc[train_data.PRODUCT_CODE == 'T_31','PRODUCT_CODE'] = 2
train_data.loc[train_data.PRODUCT_CODE == 'O_31','PRODUCT_CODE'] = 3

train_data.loc[train_data.DAY_OF_WEEK == 'Monday','DAY_OF_WEEK'] = 1
train_data.loc[train_data.DAY_OF_WEEK == 'Tuesday','DAY_OF_WEEK'] = 2
train_data.loc[train_data.DAY_OF_WEEK == 'Wednesday','DAY_OF_WEEK'] = 3
train_data.loc[train_data.DAY_OF_WEEK == 'Thursday','DAY_OF_WEEK'] = 4
train_data.loc[train_data.DAY_OF_WEEK == 'Friday','DAY_OF_WEEK'] = 5
train_data.loc[train_data.DAY_OF_WEEK == 'Saturday','DAY_OF_WEEK'] = 6
train_data.loc[train_data.DAY_OF_WEEK == 'Sunday','DAY_OF_WEEK'] = 7

train_data.drop(['PRODUCT_ID', 'TIMESTAMP', 'PRODUCT_CODE'], axis = 1, inplace = True)
train_data

Y_Class  Y_Quality     LINE   X_1   X_2  X_3   X_4   X_5  X_6   X_7  ...  \
0          1   0.533433  T050304   NaN   NaN  NaN   NaN   NaN  NaN   NaN  ...   
1          2   0.541819  T050307   NaN   NaN  NaN   NaN   NaN  NaN   NaN  ...   
2          1   0.531267  T050304   NaN   NaN  NaN   NaN   NaN  NaN   NaN  ...   
3          2   0.537325  T050307   NaN   NaN  NaN   NaN   NaN  NaN   NaN  ...   
4          1   0.531590  T050304   NaN   NaN  NaN   NaN   NaN  NaN   NaN  ...   
..       ...        ...      ...   ...   ...  ...   ...   ...  ...   ...  ...   
593        1   0.526546  T100306   2.0  95.0  0.0  45.0  10.0  0.0  50.0  ...   
594        0   0.524022  T050304   NaN   NaN  NaN   NaN   NaN  NaN   NaN  ...   
595        0   0.521289  T050304   NaN   NaN  NaN   NaN   NaN  NaN   NaN  ...   
596        1   0.531375  T100304  40.0  94.0  0.0  45.0  11.0  0.0  45.0  ...   
597        1   0.533702  T100306  21.0  87.0  0.0  45.0  10.0  0.0  61.0  ...   

     X_2866  X_2867  X_2868  X_2869  X_2870  X_2871  HOUR  MINUTE  \
0     39.34   40.89   32.56   34.09   77.77     NaN     5      14   
1     38.89   42.82   43.92   35.34   72.55     NaN     5      22   
2     39.19   36.65   42.47   36.53   78.35     NaN     5      30   
3     37.74   39.17   52.17   30.58   71.78     NaN     5      39   
4     38.70   41.89   46.93   33.09   76.97     NaN     5      47   
..      ...     ...     ...     ...     ...     ...   ...     ...   
593     NaN     NaN     NaN     NaN     NaN     NaN    14      30   
594   49.47   53.07   50.89   55.10   66.49     1.0    22      38   
595     NaN     NaN     NaN     NaN     NaN     1.0    22      47   
596     NaN     NaN     NaN     NaN     NaN     NaN    14      38   
597     NaN     NaN     NaN     NaN     NaN     NaN    14      46   

     DAY_OF_WEEK  LINE_AND_CODE  
0              1            2.0  
1              1            3.0  
2              1            2.0  
3              1            3.0  
4              1            2.0  
..           ...            ...  
593            4           11.0  
594            4            2.0  
595            4            2.0  
596            4           16.0  
597            4           17.0  

[598 rows x 2800 columns]

In [211]:
T050304 = train_data[train_data['LINE'] == 'T050304']
T050307 = train_data[train_data['LINE'] == 'T050307']
T010305 = train_data[train_data['LINE'] == 'T010305']
T010306 = train_data[train_data['LINE'] == 'T010306']
T100304 = train_data[train_data['LINE'] == 'T100304']
T100306 = train_data[train_data['LINE'] == 'T100306']

In [212]:
T050304.drop(['LINE'], axis = 1, inplace = True)
T050307.drop(['LINE'], axis = 1, inplace = True)
T010305.drop(['LINE'], axis = 1, inplace = True)
T010306.drop(['LINE'], axis = 1, inplace = True)
T100304.drop(['LINE'], axis = 1, inplace = True)
T100306.drop(['LINE'], axis = 1, inplace = True)

In [213]:
T050304_col = []
for col in T050304 :
    if 'X' in col and T050304[col].isna().sum() == len(T050304) :
        T050304_col.append(col)
print(len(T050304_col))

T050304.drop(T050304_col, inplace = True, axis = 1)

825


In [214]:
T050307_col = []
for col in T050307 :
    if 'X' in col and T050307[col].isna().sum() == len(T050307) :
        T050307_col.append(col)
print(len(T050307_col))

T050307.drop(T050307_col, inplace = True, axis = 1)

818


In [215]:
T010305_col = []
for col in T010305 :
    if 'X' in col and T010305[col].isna().sum() == len(T010305) :
        T010305_col.append(col)
print(len(T010305_col))

T010305.drop(T010305_col, inplace = True, axis = 1)

1907


In [216]:
T010306_col = []
for col in T010306 :
    if 'X' in col and T010306[col].isna().sum() == len(T010306) :
        T010306_col.append(col)
print(len(T010306_col))

T010306.drop(T010306_col, inplace = True, axis = 1)

1907


In [217]:
T100304_col = []
for col in T100304 :
    if 'X' in col and T100304[col].isna().sum() == len(T100304) :
        T100304_col.append(col)
print(len(T100304_col))

T100304.drop(T100304_col, inplace = True, axis = 1)

2122


In [218]:
T100306_col = []
for col in T100306 :
    if 'X' in col and T100306[col].isna().sum() == len(T100306) :
        T100306_col.append(col)
print(len(T100306_col))

T100306.drop(T100306_col, inplace = True, axis = 1)

2122


In [219]:
T051 = list(set(T050307_col)-set(T050304_col))
T052 = list(set(T050304_col)-set(T050307_col))
T5drop = T051 + T052

T011 = list(set(T010305_col)-set(T010306_col))
T012 = list(set(T010306_col)-set(T010305_col))
T0drop = T011 + T012

T101 = list(set(T100304_col)-set(T100306_col))
T102 = list(set(T100306_col)-set(T100304_col))
T1drop = T101 + T102

In [220]:
T05 = pd.concat([T050304, T050307])
T01 = pd.concat([T010305, T010306])
T10 = pd.concat([T100304, T100306])

In [221]:
T05.drop(T5drop, inplace = True, axis = 1)
T01.drop(T0drop, inplace = True, axis = 1)
T10.drop(T1drop, inplace = True, axis = 1)

In [222]:
T05 = T05.fillna(0)
T01 = T01.fillna(0)
T10 = T10.fillna(0)

# T05

In [223]:
T05_class = T05['Y_Class']
T05_target = T05['Y_Quality']
T05_data = T05.drop(['Y_Class', 'Y_Quality'], axis = 1)

In [117]:
T_05c = T05_data.columns
T_05scaler = RobustScaler()
T_05scaled = T_05scaler.fit_transform(T05_data)
T05_data = pd.DataFrame(T_05scaled, columns = T_05c)
T05_data

X_132  X_133  X_134  X_135     X_136     X_137     X_138     X_139  \
0     -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864 -0.024793   
1     -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864  0.024793   
2     -1.0   -1.0   -2.0    0.0 -0.199797 -0.201826 -0.208864 -0.008264   
3     -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864  0.002755   
4     -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864 -0.002755   
..     ...    ...    ...    ...       ...       ...       ...       ...   
115   -1.0   -1.0   -1.0    0.0 -0.497972 -0.500000 -0.502292 -1.049587   
116   -1.0   -1.0   -1.0    0.0 -0.495943 -0.497972 -0.500255 -1.049587   
117   -1.0   -1.0   -1.0    0.0 -0.491886 -0.493915 -0.496179 -1.044077   
118   -1.0   -1.0   -1.0    0.0 -0.491886 -0.493915 -0.496179 -1.033058   
119   -1.0   -1.0   -1.0    0.0 -0.485801 -0.487830 -0.490066 -1.082645   

        X_140     X_141  X_142  X_143  X_144  X_145     X_146  X_147  \
0   -0.052154  0.023438    0.0    0.0   -1.0    0.0 -0.003454    0.0   
1   -0.029478  0.315104    0.0    0.0    0.0    0.0  0.563040    0.0   
2   -0.043084 -0.049479    0.0    0.0   -1.0    0.0 -0.348877    0.0   
3   -0.043084 -1.195312    0.0    0.0   -2.0    0.0 -4.113990    0.0   
4   -0.047619  0.263021    0.0    0.0    0.0    0.0  0.514680    0.0   
..        ...       ...    ...    ...    ...    ...       ...    ...   
115 -0.882086 -0.898437    0.0    0.0    0.0    0.0  0.373057    0.0   
116 -0.891156 -0.929687    0.0    0.0   -1.0    0.0  0.158895    0.0   
117 -0.886621 -0.695312    0.0    0.0    0.0    0.0  0.618307    0.0   
118 -0.877551 -0.919271    0.0    0.0    0.0    0.0  0.158895    0.0   
119 -0.877551 -1.263021    0.0    0.0   -1.0    0.0 -0.873921    0.0   

        X_148     X_149   X_150  X_151  X_152  X_153  X_154  X_155  X_156  \
0    0.000000  0.072727  0.0625   -1.0    0.0    0.0    0.0    0.0    0.0   
1   -0.074074  0.000000  0.0000   -1.0    0.0   -1.0    0.0    0.0    0.0   
2    0.000000  0.000000  0.0625    0.0    0.0   -1.0    0.0    0.0    0.1   
3    0.000000  0.000000  0.0000    0.0    0.1    0.0    0.0   -1.0    0.0   
4    0.000000  0.000000  0.0625    0.0    0.0    0.0    0.0    0.0    0.0   
..        ...       ...     ...    ...    ...    ...    ...    ...    ...   
115  1.037037  1.163636  0.8750   -1.0    0.0   -2.0    0.0    0.0    0.0   
116  1.037037  1.163636  0.8750    0.0    0.0    0.0    0.0    0.0    0.0   
117  1.037037  1.163636  0.8750   -1.0    0.0   -1.0    0.0   -1.0    0.0   
118  1.037037  1.163636  0.8750   -1.0   -0.1   -1.0    0.0    0.0    0.0   
119  1.111111  1.236364  0.8750    0.0    0.0    0.0    0.0   -1.0    0.0   

     X_157  X_158  X_159  X_160  X_161  X_162  X_163  X_164  X_165  X_166  \
0      0.0    0.0   -1.0    0.0    0.0    0.0   -0.1    0.0   -0.5    0.0   
1      0.0    0.0    0.0    0.0    0.0    0.0   -0.1    0.0   -0.5    0.0   
2      0.1    0.0   -1.0    0.0    0.0    0.0    0.0    1.0    0.5    0.0   
3      0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   -0.5    0.0   
4      0.0    0.0    0.0    0.0    0.0    0.0    0.0    1.0    0.5    0.0   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
115    0.0    0.0   -1.0    0.0    0.0    0.0   -0.1    0.0   -0.5    0.0   
116    0.0    0.0    0.0    0.0    0.0    0.0    0.0    1.0    0.5    0.0   
117    0.0    0.0   -1.0    0.0    0.0    0.0    0.0    0.0    0.5    0.0   
118   -0.1    0.0   -1.0    0.1    0.0    0.0   -0.1    0.0   -0.5    0.0   
119    0.0    0.0    0.0    0.1    0.0    0.0    0.0    0.0    0.5    0.0   

     X_167  X_168  X_169  X_170  X_171  X_172  X_173  X_174  X_175  X_176  \
0     -1.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
1     -1.0    0.0    0.0    0.0   -1.0    0.0    0.0    0.0    0.0    0.0   
2     -1.0    0.0    0.0    0.0   -1.0    0.0    0.0    0.0    0.0    0.0   
3      0.0    0.0    0.0    0.0   -1.0    0.0    0.0    0.0    1.0    0.0   
4   

In [118]:
T05_y_class = pd.DataFrame(T05_target, columns = ['Y_Quality'])
T05_idx = T05_y_class.index
T05_y_class = T05_y_class.reset_index()
T05_data = pd.concat([T05_data, T05_y_class], axis = 1)
T05_data = T05_data.set_index('index')
T05_data.drop(['Y_Quality'], axis = 1, inplace = True)
T05_data

X_132  X_133  X_134  X_135     X_136     X_137     X_138     X_139  \
index                                                                       
0       -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864 -0.024793   
2       -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864  0.024793   
4       -1.0   -1.0   -2.0    0.0 -0.199797 -0.201826 -0.208864 -0.008264   
6       -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864  0.002755   
8       -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864 -0.002755   
...      ...    ...    ...    ...       ...       ...       ...       ...   
549     -1.0   -1.0   -1.0    0.0 -0.497972 -0.500000 -0.502292 -1.049587   
550     -1.0   -1.0   -1.0    0.0 -0.495943 -0.497972 -0.500255 -1.049587   
551     -1.0   -1.0   -1.0    0.0 -0.491886 -0.493915 -0.496179 -1.044077   
552     -1.0   -1.0   -1.0    0.0 -0.491886 -0.493915 -0.496179 -1.033058   
555     -1.0   -1.0   -1.0    0.0 -0.485801 -0.487830 -0.490066 -1.082645   

          X_140     X_141  X_142  X_143  X_144  X_145     X_146  X_147  \
index                                                                    
0     -0.052154  0.023438    0.0    0.0   -1.0    0.0 -0.003454    0.0   
2     -0.029478  0.315104    0.0    0.0    0.0    0.0  0.563040    0.0   
4     -0.043084 -0.049479    0.0    0.0   -1.0    0.0 -0.348877    0.0   
6     -0.043084 -1.195312    0.0    0.0   -2.0    0.0 -4.113990    0.0   
8     -0.047619  0.263021    0.0    0.0    0.0    0.0  0.514680    0.0   
...         ...       ...    ...    ...    ...    ...       ...    ...   
549   -0.882086 -0.898437    0.0    0.0    0.0    0.0  0.373057    0.0   
550   -0.891156 -0.929687    0.0    0.0   -1.0    0.0  0.158895    0.0   
551   -0.886621 -0.695312    0.0    0.0    0.0    0.0  0.618307    0.0   
552   -0.877551 -0.919271    0.0    0.0    0.0    0.0  0.158895    0.0   
555   -0.877551 -1.263021    0.0    0.0   -1.0    0.0 -0.873921    0.0   

          X_148     X_149   X_150  X_151  X_152  X_153  X_154  X_155  X_156  \
index                                                                         
0      0.000000  0.072727  0.0625   -1.0    0.0    0.0    0.0    0.0    0.0   
2     -0.074074  0.000000  0.0000   -1.0    0.0   -1.0    0.0    0.0    0.0   
4      0.000000  0.000000  0.0625    0.0    0.0   -1.0    0.0    0.0    0.1   
6      0.000000  0.000000  0.0000    0.0    0.1    0.0    0.0   -1.0    0.0   
8      0.000000  0.000000  0.0625    0.0    0.0    0.0    0.0    0.0    0.0   
...         ...       ...     ...    ...    ...    ...    ...    ...    ...   
549    1.037037  1.163636  0.8750   -1.0    0.0   -2.0    0.0    0.0    0.0   
550    1.037037  1.163636  0.8750    0.0    0.0    0.0    0.0    0.0    0.0   
551    1.037037  1.163636  0.8750   -1.0    0.0   -1.0    0.0   -1.0    0.0   
552    1.037037  1.163636  0.8750   -1.0   -0.1   -1.0    0.0    0.0    0.0   
555    1.111111  1.236364  0.8750    0.0    0.0    0.0    0.0   -1.0    0.0   

       X_157  X_158  X_159  X_160  X_161  X_162  X_163  X_164  X_165  X_166  \
index                                                                         
0        0.0    0.0   -1.0    0.0    0.0    0.0   -0.1    0.0   -0.5    0.0   
2        0.0    0.0    0.0    0.0    0.0    0.0   -0.1    0.0   -0.5    0.0   
4        0.1    0.0   -1.0    0.0    0.0    0.0    0.0    1.0    0.5    0.0   
6        0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   -0.5    0.0   
8        0.0    0.0    0.0    0.0    0.0    0.0    0.0    1.0    0.5    0.0   
...      ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
549      0.0    0.0   -1.0    0.0    0.0    0.0   -0.1    0.0   -0.5    0.0   
550      0.0    0.0    0.0    0.0    0.0    0.0    0.0    1.0    0.5    0.0   
551      0.0    0.0   -1.0    0.0    0.0    0.0    0.0    0.0    0.5    0.0   
552     -0.1    0.0   -1.0    0.1    0.0    0.0   -0.1    0.0   -0.5    0.0   
555      0.0    0.0    0.0    0.1    0.0    0.0    0.0    0.0    0

In [119]:
#13
setup_rgs = setup(data = T05_data, target = T05_target, session_id = 414)
top5 = compare_models(sort='MSE', n_select=5)

Processing:   0%|          | 0/89 [00:00<?, ?it/s]

In [120]:
T05_total_models = []

T05_model_lightgbm = create_model('lightgbm', fold = 5)
T05_total_models.append(T05_model_lightgbm)

T05_model_rf = create_model('rf', fold = 5)
T05_total_models.append(T05_model_rf)

T05_model_gbr = create_model('gbr', fold = 5)
T05_total_models.append(T05_model_gbr)

T05_model_et = create_model('et', fold = 5)
T05_total_models.append(T05_model_et)

T05_model_catboost = create_model('catboost', fold = 5)
T05_total_models.append(T05_model_catboost)

T05_model_xgb = create_model('xgboost', fold = 5)
T05_total_models.append(T05_model_xgb)

T05_model_ada = create_model('ada', fold = 5)

T05_total_models.append(T05_model_ada)

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

In [121]:
T05_model_lightgbm = tune_model(T05_model_lightgbm, fold=5, choose_better = True)

T05_model_rf = tune_model(T05_model_rf, fold=5, choose_better = True)

T05_model_gbr = tune_model(T05_model_gbr, fold=5, choose_better = True)

T05_model_et = tune_model(T05_model_et, fold=5, choose_better = True)

T05_model_catboost = tune_model(T05_model_catboost, fold=5, choose_better = True)

T05_model_xgb = tune_model(T05_model_xgb, fold=5, choose_better = True)

T05_model_ada = tune_model(T05_model_ada, fold=5, choose_better = True)

Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

...

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


In [122]:
T05_tuned_models = [T05_model_lightgbm, T05_model_rf, T05_model_gbr, T05_model_et, T05_model_catboost, T05_model_xgb, T05_model_ada]
T05_tuned_models

[LGBMRegressor(boosting_type='gbdt', class_weight=None, colsample_bytree=1.0,
               importance_type='split', learning_rate=0.1, max_depth=-1,
               min_child_samples=20, min_child_weight=0.001, min_split_gain=0.0,
               n_estimators=100, n_jobs=-1, num_leaves=31, objective=None,
               random_state=414, reg_alpha=0.0, reg_lambda=0.0, silent=True,
               subsample=1.0, subsample_for_bin=200000, subsample_freq=0),
 RandomForestRegressor(bootstrap=True, ccp_alpha=0.0, criterion='squared_error',
                       max_depth=None, max_features='auto', max_leaf_nodes=None,
                       max_samples=None, min_impurity_decrease=0.0,
                       min_samples_leaf=1, min_samples_split=2,
                       min_weight_fraction_leaf=0.0, n_estimators=100, n_jobs=-1,
                       oob_score=False, random_state=414, verbose=0,
                       warm_start=False),
 GradientBoostingRegressor(alpha=0.9, ccp_alpha=0.0, c

In [123]:
for model in T05_tuned_models:
    display(predict_model(model))

X_132  X_133  X_134  X_135     X_136     X_137     X_138     X_139  \
84     0.0    0.0    0.0    0.0  0.360041  0.347870  0.359654  0.371901   
85     0.0    0.0   -1.0    0.0  0.648073  0.646045  0.649007 -0.079890   
86    -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.202751  0.019284   
87    -1.0    0.0   -1.0    0.0 -0.542596 -0.544625 -0.547122 -1.628099   
88     0.0    0.0    0.0    0.0  0.453347  0.451318  0.453388  0.190083   
89    -1.0    0.0   -1.0    0.0  0.982759  0.980730  0.985227  0.933884   
90     0.0    0.0    0.0    0.0  0.897566  0.895537  0.899643  0.757576   
91     0.0    0.0    0.0    0.0  0.495943  0.493915  0.496179  0.278237   
92     0.0    0.0    0.0    0.0  1.110548  1.108519  1.115639  1.071625   
93     0.0    0.0    0.0    0.0  0.792089  0.790061  0.795721  0.636364   
94    -1.0   -1.0   -2.0    0.0 -0.149087 -0.151116 -0.157922  0.008264   
95     0.0    0.0    0.0    0.0  0.757607  0.755578  0.759042  0.520661   
96    -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864  0.024793   
97    -1.0   -1.0   -1.0    0.0 -0.313387 -0.315416 -0.316862 -0.217631   
98     0.0    0.0    0.0    0.0  0.248479  0.250507  0.251656 -0.184573   
99     0.0    0.0    0.0    0.0  1.015213  1.013185  1.019868  0.757576   
100    0.0    0.0    0.0    0.0 -0.301217 -0.299189 -0.300560 -0.873278   
101    0.0    0.0    0.0    0.0  0.280933  0.278905  0.280183 -0.019284   
102   -1.0    0.0   -1.0    0.0 -0.560852 -0.558824 -0.561386 -1.275482   
103   -1.0   -1.0   -1.0    0.0 -0.495943 -0.497972 -0.500255 -1.049587   
104    0.0    0.0    0.0    0.0 -0.412779 -0.414807 -0.416709 -0.663912   
105   -1.0   -1.0   -1.0    0.0 -0.485801 -0.487830 -0.490066 -1.082645   
106   -1.0   -1.0   -1.0    0.0 -0.195740 -0.197769 -0.198675  0.035813   
107    0.0    0.0    0.0    0.0  0.177485  0.175456  0.176261  0.327824   
108    0.0    0.0   -1.0    0.0  0.266734  0.264706  0.265920 -0.112948   
109    0.0    0.0    0.0    0.0 -0.313387 -0.315416 -0.316862 -0.614325   
110    0.0    0.0    0.0    0.0 -0.445233 -0.447262 -0.449312 -0.487603   
111   -1.0    0.0   -1.0    0.0 -0.542596 -0.544625 -0.547122 -1.650138   
112    0.0    0.0    0.0    0.0  0.792089  0.790061  0.793683  0.641873   
113    0.0    0.0   -1.0    0.0  0.191684  0.189655  0.190525 -0.162534   
114    0.0    0.0    0.0    0.0  0.591278  0.577079  0.591951  0.669421   
115    0.0    0.0   -1.0    0.0  0.406694  0.404665  0.402445  0.674931   
116   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864 -0.041322   
117   -1.0   -1.0   -1.0    0.0 -0.045639 -0.047667 -0.047886  0.305785   
118    0.0    0.0    0.0    0.0  0.901623  0.899594  0.903719  0.741047   
119    0.0    0.0    0.0    0.0  0.621704  0.619675  0.622517  0.063361   

        X_140     X_141  ...    X_2868    X_2869     X_2870  X_2871      HOUR  \
84   0.551020 -0.690104  ...  0.660000  0.185721   1.368812     0.0  1.777778   
85   0.024943 -1.226562  ...  0.679286  0.161771   0.158416     0.0  1.777778   
86   0.006803  0.226562  ...  0.215000  0.045639   0.509901     0.0 -0.111111   
87  -1.340136 -2.565104  ...  0.007857  0.082241  -0.089109     0.0  0.333333   
88   0.192744  0.039062  ...  0.018571  0.009941   0.551980     0.0 -0.111111   
89   0.877551  0.356771  ...  0.063571  0.000904   0.306931     0.0  0.777778   
90   0.700680  0.929688  ...  0.661429  0.084953  -0.470297     0.0 -0.666667   
91   0.269841  0.429688  ...  0.325714  0.050158   0.549505     0.0  0.555556   
92   0.950113  1.091146  ... -3.568571 -2.499322 -15.997525     0.0 -0.333333   
93   0.596372  0.466146  ... -0.668571  0.057840   0.121287     0.0  0.777778   
94  -0.002268 -0.992188  ... -3.568571 -2.499322 -15.997525     0.0 -0.222222   
95   0.505669  0.617188  ...  0.458571  0.056936  -0.106436     0.0 -0.777778   
96  -0.029478  0.315104  ... -0.535000 -0.848622   3.396039    -1.0 -0.222222   
97  -0.219955  0.065104  ...  0.234286  0.063714  -0.113861     0.0 -0.666667   
98  -0.160998 

X_132  X_133  X_134  X_135     X_136     X_137     X_138     X_139  \
84     0.0    0.0    0.0    0.0  0.360041  0.347870  0.359654  0.371901   
85     0.0    0.0   -1.0    0.0  0.648073  0.646045  0.649007 -0.079890   
86    -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.202751  0.019284   
87    -1.0    0.0   -1.0    0.0 -0.542596 -0.544625 -0.547122 -1.628099   
88     0.0    0.0    0.0    0.0  0.453347  0.451318  0.453388  0.190083   
89    -1.0    0.0   -1.0    0.0  0.982759  0.980730  0.985227  0.933884   
90     0.0    0.0    0.0    0.0  0.897566  0.895537  0.899643  0.757576   
91     0.0    0.0    0.0    0.0  0.495943  0.493915  0.496179  0.278237   
92     0.0    0.0    0.0    0.0  1.110548  1.108519  1.115639  1.071625   
93     0.0    0.0    0.0    0.0  0.792089  0.790061  0.795721  0.636364   
94    -1.0   -1.0   -2.0    0.0 -0.149087 -0.151116 -0.157922  0.008264   
95     0.0    0.0    0.0    0.0  0.757607  0.755578  0.759042  0.520661   
96    -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864  0.024793   
97    -1.0   -1.0   -1.0    0.0 -0.313387 -0.315416 -0.316862 -0.217631   
98     0.0    0.0    0.0    0.0  0.248479  0.250507  0.251656 -0.184573   
99     0.0    0.0    0.0    0.0  1.015213  1.013185  1.019868  0.757576   
100    0.0    0.0    0.0    0.0 -0.301217 -0.299189 -0.300560 -0.873278   
101    0.0    0.0    0.0    0.0  0.280933  0.278905  0.280183 -0.019284   
102   -1.0    0.0   -1.0    0.0 -0.560852 -0.558824 -0.561386 -1.275482   
103   -1.0   -1.0   -1.0    0.0 -0.495943 -0.497972 -0.500255 -1.049587   
104    0.0    0.0    0.0    0.0 -0.412779 -0.414807 -0.416709 -0.663912   
105   -1.0   -1.0   -1.0    0.0 -0.485801 -0.487830 -0.490066 -1.082645   
106   -1.0   -1.0   -1.0    0.0 -0.195740 -0.197769 -0.198675  0.035813   
107    0.0    0.0    0.0    0.0  0.177485  0.175456  0.176261  0.327824   
108    0.0    0.0   -1.0    0.0  0.266734  0.264706  0.265920 -0.112948   
109    0.0    0.0    0.0    0.0 -0.313387 -0.315416 -0.316862 -0.614325   
110    0.0    0.0    0.0    0.0 -0.445233 -0.447262 -0.449312 -0.487603   
111   -1.0    0.0   -1.0    0.0 -0.542596 -0.544625 -0.547122 -1.650138   
112    0.0    0.0    0.0    0.0  0.792089  0.790061  0.793683  0.641873   
113    0.0    0.0   -1.0    0.0  0.191684  0.189655  0.190525 -0.162534   
114    0.0    0.0    0.0    0.0  0.591278  0.577079  0.591951  0.669421   
115    0.0    0.0   -1.0    0.0  0.406694  0.404665  0.402445  0.674931   
116   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864 -0.041322   
117   -1.0   -1.0   -1.0    0.0 -0.045639 -0.047667 -0.047886  0.305785   
118    0.0    0.0    0.0    0.0  0.901623  0.899594  0.903719  0.741047   
119    0.0    0.0    0.0    0.0  0.621704  0.619675  0.622517  0.063361   

        X_140     X_141  ...    X_2868    X_2869     X_2870  X_2871      HOUR  \
84   0.551020 -0.690104  ...  0.660000  0.185721   1.368812     0.0  1.777778   
85   0.024943 -1.226562  ...  0.679286  0.161771   0.158416     0.0  1.777778   
86   0.006803  0.226562  ...  0.215000  0.045639   0.509901     0.0 -0.111111   
87  -1.340136 -2.565104  ...  0.007857  0.082241  -0.089109     0.0  0.333333   
88   0.192744  0.039062  ...  0.018571  0.009941   0.551980     0.0 -0.111111   
89   0.877551  0.356771  ...  0.063571  0.000904   0.306931     0.0  0.777778   
90   0.700680  0.929688  ...  0.661429  0.084953  -0.470297     0.0 -0.666667   
91   0.269841  0.429688  ...  0.325714  0.050158   0.549505     0.0  0.555556   
92   0.950113  1.091146  ... -3.568571 -2.499322 -15.997525     0.0 -0.333333   
93   0.596372  0.466146  ... -0.668571  0.057840   0.121287     0.0  0.777778   
94  -0.002268 -0.992188  ... -3.568571 -2.499322 -15.997525     0.0 -0.222222   
95   0.505669  0.617188  ...  0.458571  0.056936  -0.106436     0.0 -0.777778   
96  -0.029478  0.315104  ... -0.535000 -0.848622   3.396039    -1.0 -0.222222   
97  -0.219955  0.065104  ...  0.234286  0.063714  -0.113861     0.0 -0.666667   
98  -0.160998 

X_132  X_133  X_134  X_135     X_136     X_137     X_138     X_139  \
84     0.0    0.0    0.0    0.0  0.360041  0.347870  0.359654  0.371901   
85     0.0    0.0   -1.0    0.0  0.648073  0.646045  0.649007 -0.079890   
86    -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.202751  0.019284   
87    -1.0    0.0   -1.0    0.0 -0.542596 -0.544625 -0.547122 -1.628099   
88     0.0    0.0    0.0    0.0  0.453347  0.451318  0.453388  0.190083   
89    -1.0    0.0   -1.0    0.0  0.982759  0.980730  0.985227  0.933884   
90     0.0    0.0    0.0    0.0  0.897566  0.895537  0.899643  0.757576   
91     0.0    0.0    0.0    0.0  0.495943  0.493915  0.496179  0.278237   
92     0.0    0.0    0.0    0.0  1.110548  1.108519  1.115639  1.071625   
93     0.0    0.0    0.0    0.0  0.792089  0.790061  0.795721  0.636364   
94    -1.0   -1.0   -2.0    0.0 -0.149087 -0.151116 -0.157922  0.008264   
95     0.0    0.0    0.0    0.0  0.757607  0.755578  0.759042  0.520661   
96    -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864  0.024793   
97    -1.0   -1.0   -1.0    0.0 -0.313387 -0.315416 -0.316862 -0.217631   
98     0.0    0.0    0.0    0.0  0.248479  0.250507  0.251656 -0.184573   
99     0.0    0.0    0.0    0.0  1.015213  1.013185  1.019868  0.757576   
100    0.0    0.0    0.0    0.0 -0.301217 -0.299189 -0.300560 -0.873278   
101    0.0    0.0    0.0    0.0  0.280933  0.278905  0.280183 -0.019284   
102   -1.0    0.0   -1.0    0.0 -0.560852 -0.558824 -0.561386 -1.275482   
103   -1.0   -1.0   -1.0    0.0 -0.495943 -0.497972 -0.500255 -1.049587   
104    0.0    0.0    0.0    0.0 -0.412779 -0.414807 -0.416709 -0.663912   
105   -1.0   -1.0   -1.0    0.0 -0.485801 -0.487830 -0.490066 -1.082645   
106   -1.0   -1.0   -1.0    0.0 -0.195740 -0.197769 -0.198675  0.035813   
107    0.0    0.0    0.0    0.0  0.177485  0.175456  0.176261  0.327824   
108    0.0    0.0   -1.0    0.0  0.266734  0.264706  0.265920 -0.112948   
109    0.0    0.0    0.0    0.0 -0.313387 -0.315416 -0.316862 -0.614325   
110    0.0    0.0    0.0    0.0 -0.445233 -0.447262 -0.449312 -0.487603   
111   -1.0    0.0   -1.0    0.0 -0.542596 -0.544625 -0.547122 -1.650138   
112    0.0    0.0    0.0    0.0  0.792089  0.790061  0.793683  0.641873   
113    0.0    0.0   -1.0    0.0  0.191684  0.189655  0.190525 -0.162534   
114    0.0    0.0    0.0    0.0  0.591278  0.577079  0.591951  0.669421   
115    0.0    0.0   -1.0    0.0  0.406694  0.404665  0.402445  0.674931   
116   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864 -0.041322   
117   -1.0   -1.0   -1.0    0.0 -0.045639 -0.047667 -0.047886  0.305785   
118    0.0    0.0    0.0    0.0  0.901623  0.899594  0.903719  0.741047   
119    0.0    0.0    0.0    0.0  0.621704  0.619675  0.622517  0.063361   

        X_140     X_141  ...    X_2868    X_2869     X_2870  X_2871      HOUR  \
84   0.551020 -0.690104  ...  0.660000  0.185721   1.368812     0.0  1.777778   
85   0.024943 -1.226562  ...  0.679286  0.161771   0.158416     0.0  1.777778   
86   0.006803  0.226562  ...  0.215000  0.045639   0.509901     0.0 -0.111111   
87  -1.340136 -2.565104  ...  0.007857  0.082241  -0.089109     0.0  0.333333   
88   0.192744  0.039062  ...  0.018571  0.009941   0.551980     0.0 -0.111111   
89   0.877551  0.356771  ...  0.063571  0.000904   0.306931     0.0  0.777778   
90   0.700680  0.929688  ...  0.661429  0.084953  -0.470297     0.0 -0.666667   
91   0.269841  0.429688  ...  0.325714  0.050158   0.549505     0.0  0.555556   
92   0.950113  1.091146  ... -3.568571 -2.499322 -15.997525     0.0 -0.333333   
93   0.596372  0.466146  ... -0.668571  0.057840   0.121287     0.0  0.777778   
94  -0.002268 -0.992188  ... -3.568571 -2.499322 -15.997525     0.0 -0.222222   
95   0.505669  0.617188  ...  0.458571  0.056936  -0.106436     0.0 -0.777778   
96  -0.029478  0.315104  ... -0.535000 -0.848622   3.396039    -1.0 -0.222222   
97  -0.219955  0.065104  ...  0.234286  0.063714  -0.113861     0.0 -0.666667   
98  -0.160998 

X_132  X_133  X_134  X_135     X_136     X_137     X_138     X_139  \
84     0.0    0.0    0.0    0.0  0.360041  0.347870  0.359654  0.371901   
85     0.0    0.0   -1.0    0.0  0.648073  0.646045  0.649007 -0.079890   
86    -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.202751  0.019284   
87    -1.0    0.0   -1.0    0.0 -0.542596 -0.544625 -0.547122 -1.628099   
88     0.0    0.0    0.0    0.0  0.453347  0.451318  0.453388  0.190083   
89    -1.0    0.0   -1.0    0.0  0.982759  0.980730  0.985227  0.933884   
90     0.0    0.0    0.0    0.0  0.897566  0.895537  0.899643  0.757576   
91     0.0    0.0    0.0    0.0  0.495943  0.493915  0.496179  0.278237   
92     0.0    0.0    0.0    0.0  1.110548  1.108519  1.115639  1.071625   
93     0.0    0.0    0.0    0.0  0.792089  0.790061  0.795721  0.636364   
94    -1.0   -1.0   -2.0    0.0 -0.149087 -0.151116 -0.157922  0.008264   
95     0.0    0.0    0.0    0.0  0.757607  0.755578  0.759042  0.520661   
96    -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864  0.024793   
97    -1.0   -1.0   -1.0    0.0 -0.313387 -0.315416 -0.316862 -0.217631   
98     0.0    0.0    0.0    0.0  0.248479  0.250507  0.251656 -0.184573   
99     0.0    0.0    0.0    0.0  1.015213  1.013185  1.019868  0.757576   
100    0.0    0.0    0.0    0.0 -0.301217 -0.299189 -0.300560 -0.873278   
101    0.0    0.0    0.0    0.0  0.280933  0.278905  0.280183 -0.019284   
102   -1.0    0.0   -1.0    0.0 -0.560852 -0.558824 -0.561386 -1.275482   
103   -1.0   -1.0   -1.0    0.0 -0.495943 -0.497972 -0.500255 -1.049587   
104    0.0    0.0    0.0    0.0 -0.412779 -0.414807 -0.416709 -0.663912   
105   -1.0   -1.0   -1.0    0.0 -0.485801 -0.487830 -0.490066 -1.082645   
106   -1.0   -1.0   -1.0    0.0 -0.195740 -0.197769 -0.198675  0.035813   
107    0.0    0.0    0.0    0.0  0.177485  0.175456  0.176261  0.327824   
108    0.0    0.0   -1.0    0.0  0.266734  0.264706  0.265920 -0.112948   
109    0.0    0.0    0.0    0.0 -0.313387 -0.315416 -0.316862 -0.614325   
110    0.0    0.0    0.0    0.0 -0.445233 -0.447262 -0.449312 -0.487603   
111   -1.0    0.0   -1.0    0.0 -0.542596 -0.544625 -0.547122 -1.650138   
112    0.0    0.0    0.0    0.0  0.792089  0.790061  0.793683  0.641873   
113    0.0    0.0   -1.0    0.0  0.191684  0.189655  0.190525 -0.162534   
114    0.0    0.0    0.0    0.0  0.591278  0.577079  0.591951  0.669421   
115    0.0    0.0   -1.0    0.0  0.406694  0.404665  0.402445  0.674931   
116   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864 -0.041322   
117   -1.0   -1.0   -1.0    0.0 -0.045639 -0.047667 -0.047886  0.305785   
118    0.0    0.0    0.0    0.0  0.901623  0.899594  0.903719  0.741047   
119    0.0    0.0    0.0    0.0  0.621704  0.619675  0.622517  0.063361   

        X_140     X_141  ...    X_2868    X_2869     X_2870  X_2871      HOUR  \
84   0.551020 -0.690104  ...  0.660000  0.185721   1.368812     0.0  1.777778   
85   0.024943 -1.226562  ...  0.679286  0.161771   0.158416     0.0  1.777778   
86   0.006803  0.226562  ...  0.215000  0.045639   0.509901     0.0 -0.111111   
87  -1.340136 -2.565104  ...  0.007857  0.082241  -0.089109     0.0  0.333333   
88   0.192744  0.039062  ...  0.018571  0.009941   0.551980     0.0 -0.111111   
89   0.877551  0.356771  ...  0.063571  0.000904   0.306931     0.0  0.777778   
90   0.700680  0.929688  ...  0.661429  0.084953  -0.470297     0.0 -0.666667   
91   0.269841  0.429688  ...  0.325714  0.050158   0.549505     0.0  0.555556   
92   0.950113  1.091146  ... -3.568571 -2.499322 -15.997525     0.0 -0.333333   
93   0.596372  0.466146  ... -0.668571  0.057840   0.121287     0.0  0.777778   
94  -0.002268 -0.992188  ... -3.568571 -2.499322 -15.997525     0.0 -0.222222   
95   0.505669  0.617188  ...  0.458571  0.056936  -0.106436     0.0 -0.777778   
96  -0.029478  0.315104  ... -0.535000 -0.848622   3.396039    -1.0 -0.222222   
97  -0.219955  0.065104  ...  0.234286  0.063714  -0.113861     0.0 -0.666667   
98  -0.160998 

X_132  X_133  X_134  X_135     X_136     X_137     X_138     X_139  \
84     0.0    0.0    0.0    0.0  0.360041  0.347870  0.359654  0.371901   
85     0.0    0.0   -1.0    0.0  0.648073  0.646045  0.649007 -0.079890   
86    -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.202751  0.019284   
87    -1.0    0.0   -1.0    0.0 -0.542596 -0.544625 -0.547122 -1.628099   
88     0.0    0.0    0.0    0.0  0.453347  0.451318  0.453388  0.190083   
89    -1.0    0.0   -1.0    0.0  0.982759  0.980730  0.985227  0.933884   
90     0.0    0.0    0.0    0.0  0.897566  0.895537  0.899643  0.757576   
91     0.0    0.0    0.0    0.0  0.495943  0.493915  0.496179  0.278237   
92     0.0    0.0    0.0    0.0  1.110548  1.108519  1.115639  1.071625   
93     0.0    0.0    0.0    0.0  0.792089  0.790061  0.795721  0.636364   
94    -1.0   -1.0   -2.0    0.0 -0.149087 -0.151116 -0.157922  0.008264   
95     0.0    0.0    0.0    0.0  0.757607  0.755578  0.759042  0.520661   
96    -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864  0.024793   
97    -1.0   -1.0   -1.0    0.0 -0.313387 -0.315416 -0.316862 -0.217631   
98     0.0    0.0    0.0    0.0  0.248479  0.250507  0.251656 -0.184573   
99     0.0    0.0    0.0    0.0  1.015213  1.013185  1.019868  0.757576   
100    0.0    0.0    0.0    0.0 -0.301217 -0.299189 -0.300560 -0.873278   
101    0.0    0.0    0.0    0.0  0.280933  0.278905  0.280183 -0.019284   
102   -1.0    0.0   -1.0    0.0 -0.560852 -0.558824 -0.561386 -1.275482   
103   -1.0   -1.0   -1.0    0.0 -0.495943 -0.497972 -0.500255 -1.049587   
104    0.0    0.0    0.0    0.0 -0.412779 -0.414807 -0.416709 -0.663912   
105   -1.0   -1.0   -1.0    0.0 -0.485801 -0.487830 -0.490066 -1.082645   
106   -1.0   -1.0   -1.0    0.0 -0.195740 -0.197769 -0.198675  0.035813   
107    0.0    0.0    0.0    0.0  0.177485  0.175456  0.176261  0.327824   
108    0.0    0.0   -1.0    0.0  0.266734  0.264706  0.265920 -0.112948   
109    0.0    0.0    0.0    0.0 -0.313387 -0.315416 -0.316862 -0.614325   
110    0.0    0.0    0.0    0.0 -0.445233 -0.447262 -0.449312 -0.487603   
111   -1.0    0.0   -1.0    0.0 -0.542596 -0.544625 -0.547122 -1.650138   
112    0.0    0.0    0.0    0.0  0.792089  0.790061  0.793683  0.641873   
113    0.0    0.0   -1.0    0.0  0.191684  0.189655  0.190525 -0.162534   
114    0.0    0.0    0.0    0.0  0.591278  0.577079  0.591951  0.669421   
115    0.0    0.0   -1.0    0.0  0.406694  0.404665  0.402445  0.674931   
116   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864 -0.041322   
117   -1.0   -1.0   -1.0    0.0 -0.045639 -0.047667 -0.047886  0.305785   
118    0.0    0.0    0.0    0.0  0.901623  0.899594  0.903719  0.741047   
119    0.0    0.0    0.0    0.0  0.621704  0.619675  0.622517  0.063361   

        X_140     X_141  ...    X_2868    X_2869     X_2870  X_2871      HOUR  \
84   0.551020 -0.690104  ...  0.660000  0.185721   1.368812     0.0  1.777778   
85   0.024943 -1.226562  ...  0.679286  0.161771   0.158416     0.0  1.777778   
86   0.006803  0.226562  ...  0.215000  0.045639   0.509901     0.0 -0.111111   
87  -1.340136 -2.565104  ...  0.007857  0.082241  -0.089109     0.0  0.333333   
88   0.192744  0.039062  ...  0.018571  0.009941   0.551980     0.0 -0.111111   
89   0.877551  0.356771  ...  0.063571  0.000904   0.306931     0.0  0.777778   
90   0.700680  0.929688  ...  0.661429  0.084953  -0.470297     0.0 -0.666667   
91   0.269841  0.429688  ...  0.325714  0.050158   0.549505     0.0  0.555556   
92   0.950113  1.091146  ... -3.568571 -2.499322 -15.997525     0.0 -0.333333   
93   0.596372  0.466146  ... -0.668571  0.057840   0.121287     0.0  0.777778   
94  -0.002268 -0.992188  ... -3.568571 -2.499322 -15.997525     0.0 -0.222222   
95   0.505669  0.617188  ...  0.458571  0.056936  -0.106436     0.0 -0.777778   
96  -0.029478  0.315104  ... -0.535000 -0.848622   3.396039    -1.0 -0.222222   
97  -0.219955  0.065104  ...  0.234286  0.063714  -0.113861     0.0 -0.666667   
98  -0.160998 

X_132  X_133  X_134  X_135     X_136     X_137     X_138     X_139  \
84     0.0    0.0    0.0    0.0  0.360041  0.347870  0.359654  0.371901   
85     0.0    0.0   -1.0    0.0  0.648073  0.646045  0.649007 -0.079890   
86    -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.202751  0.019284   
87    -1.0    0.0   -1.0    0.0 -0.542596 -0.544625 -0.547122 -1.628099   
88     0.0    0.0    0.0    0.0  0.453347  0.451318  0.453388  0.190083   
89    -1.0    0.0   -1.0    0.0  0.982759  0.980730  0.985227  0.933884   
90     0.0    0.0    0.0    0.0  0.897566  0.895537  0.899643  0.757576   
91     0.0    0.0    0.0    0.0  0.495943  0.493915  0.496179  0.278237   
92     0.0    0.0    0.0    0.0  1.110548  1.108519  1.115639  1.071625   
93     0.0    0.0    0.0    0.0  0.792089  0.790061  0.795721  0.636364   
94    -1.0   -1.0   -2.0    0.0 -0.149087 -0.151116 -0.157922  0.008264   
95     0.0    0.0    0.0    0.0  0.757607  0.755578  0.759042  0.520661   
96    -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864  0.024793   
97    -1.0   -1.0   -1.0    0.0 -0.313387 -0.315416 -0.316862 -0.217631   
98     0.0    0.0    0.0    0.0  0.248479  0.250507  0.251656 -0.184573   
99     0.0    0.0    0.0    0.0  1.015213  1.013185  1.019868  0.757576   
100    0.0    0.0    0.0    0.0 -0.301217 -0.299189 -0.300560 -0.873278   
101    0.0    0.0    0.0    0.0  0.280933  0.278905  0.280183 -0.019284   
102   -1.0    0.0   -1.0    0.0 -0.560852 -0.558824 -0.561386 -1.275482   
103   -1.0   -1.0   -1.0    0.0 -0.495943 -0.497972 -0.500255 -1.049587   
104    0.0    0.0    0.0    0.0 -0.412779 -0.414807 -0.416709 -0.663912   
105   -1.0   -1.0   -1.0    0.0 -0.485801 -0.487830 -0.490066 -1.082645   
106   -1.0   -1.0   -1.0    0.0 -0.195740 -0.197769 -0.198675  0.035813   
107    0.0    0.0    0.0    0.0  0.177485  0.175456  0.176261  0.327824   
108    0.0    0.0   -1.0    0.0  0.266734  0.264706  0.265920 -0.112948   
109    0.0    0.0    0.0    0.0 -0.313387 -0.315416 -0.316862 -0.614325   
110    0.0    0.0    0.0    0.0 -0.445233 -0.447262 -0.449312 -0.487603   
111   -1.0    0.0   -1.0    0.0 -0.542596 -0.544625 -0.547122 -1.650138   
112    0.0    0.0    0.0    0.0  0.792089  0.790061  0.793683  0.641873   
113    0.0    0.0   -1.0    0.0  0.191684  0.189655  0.190525 -0.162534   
114    0.0    0.0    0.0    0.0  0.591278  0.577079  0.591951  0.669421   
115    0.0    0.0   -1.0    0.0  0.406694  0.404665  0.402445  0.674931   
116   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864 -0.041322   
117   -1.0   -1.0   -1.0    0.0 -0.045639 -0.047667 -0.047886  0.305785   
118    0.0    0.0    0.0    0.0  0.901623  0.899594  0.903719  0.741047   
119    0.0    0.0    0.0    0.0  0.621704  0.619675  0.622517  0.063361   

        X_140     X_141  ...    X_2868    X_2869     X_2870  X_2871      HOUR  \
84   0.551020 -0.690104  ...  0.660000  0.185721   1.368812     0.0  1.777778   
85   0.024943 -1.226562  ...  0.679286  0.161771   0.158416     0.0  1.777778   
86   0.006803  0.226562  ...  0.215000  0.045639   0.509901     0.0 -0.111111   
87  -1.340136 -2.565104  ...  0.007857  0.082241  -0.089109     0.0  0.333333   
88   0.192744  0.039062  ...  0.018571  0.009941   0.551980     0.0 -0.111111   
89   0.877551  0.356771  ...  0.063571  0.000904   0.306931     0.0  0.777778   
90   0.700680  0.929688  ...  0.661429  0.084953  -0.470297     0.0 -0.666667   
91   0.269841  0.429688  ...  0.325714  0.050158   0.549505     0.0  0.555556   
92   0.950113  1.091146  ... -3.568571 -2.499322 -15.997525     0.0 -0.333333   
93   0.596372  0.466146  ... -0.668571  0.057840   0.121287     0.0  0.777778   
94  -0.002268 -0.992188  ... -3.568571 -2.499322 -15.997525     0.0 -0.222222   
95   0.505669  0.617188  ...  0.458571  0.056936  -0.106436     0.0 -0.777778   
96  -0.029478  0.315104  ... -0.535000 -0.848622   3.396039    -1.0 -0.222222   
97  -0.219955  0.065104  ...  0.234286  0.063714  -0.113861     0.0 -0.666667   
98  -0.160998 

X_132  X_133  X_134  X_135     X_136     X_137     X_138     X_139  \
84     0.0    0.0    0.0    0.0  0.360041  0.347870  0.359654  0.371901   
85     0.0    0.0   -1.0    0.0  0.648073  0.646045  0.649007 -0.079890   
86    -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.202751  0.019284   
87    -1.0    0.0   -1.0    0.0 -0.542596 -0.544625 -0.547122 -1.628099   
88     0.0    0.0    0.0    0.0  0.453347  0.451318  0.453388  0.190083   
89    -1.0    0.0   -1.0    0.0  0.982759  0.980730  0.985227  0.933884   
90     0.0    0.0    0.0    0.0  0.897566  0.895537  0.899643  0.757576   
91     0.0    0.0    0.0    0.0  0.495943  0.493915  0.496179  0.278237   
92     0.0    0.0    0.0    0.0  1.110548  1.108519  1.115639  1.071625   
93     0.0    0.0    0.0    0.0  0.792089  0.790061  0.795721  0.636364   
94    -1.0   -1.0   -2.0    0.0 -0.149087 -0.151116 -0.157922  0.008264   
95     0.0    0.0    0.0    0.0  0.757607  0.755578  0.759042  0.520661   
96    -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864  0.024793   
97    -1.0   -1.0   -1.0    0.0 -0.313387 -0.315416 -0.316862 -0.217631   
98     0.0    0.0    0.0    0.0  0.248479  0.250507  0.251656 -0.184573   
99     0.0    0.0    0.0    0.0  1.015213  1.013185  1.019868  0.757576   
100    0.0    0.0    0.0    0.0 -0.301217 -0.299189 -0.300560 -0.873278   
101    0.0    0.0    0.0    0.0  0.280933  0.278905  0.280183 -0.019284   
102   -1.0    0.0   -1.0    0.0 -0.560852 -0.558824 -0.561386 -1.275482   
103   -1.0   -1.0   -1.0    0.0 -0.495943 -0.497972 -0.500255 -1.049587   
104    0.0    0.0    0.0    0.0 -0.412779 -0.414807 -0.416709 -0.663912   
105   -1.0   -1.0   -1.0    0.0 -0.485801 -0.487830 -0.490066 -1.082645   
106   -1.0   -1.0   -1.0    0.0 -0.195740 -0.197769 -0.198675  0.035813   
107    0.0    0.0    0.0    0.0  0.177485  0.175456  0.176261  0.327824   
108    0.0    0.0   -1.0    0.0  0.266734  0.264706  0.265920 -0.112948   
109    0.0    0.0    0.0    0.0 -0.313387 -0.315416 -0.316862 -0.614325   
110    0.0    0.0    0.0    0.0 -0.445233 -0.447262 -0.449312 -0.487603   
111   -1.0    0.0   -1.0    0.0 -0.542596 -0.544625 -0.547122 -1.650138   
112    0.0    0.0    0.0    0.0  0.792089  0.790061  0.793683  0.641873   
113    0.0    0.0   -1.0    0.0  0.191684  0.189655  0.190525 -0.162534   
114    0.0    0.0    0.0    0.0  0.591278  0.577079  0.591951  0.669421   
115    0.0    0.0   -1.0    0.0  0.406694  0.404665  0.402445  0.674931   
116   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864 -0.041322   
117   -1.0   -1.0   -1.0    0.0 -0.045639 -0.047667 -0.047886  0.305785   
118    0.0    0.0    0.0    0.0  0.901623  0.899594  0.903719  0.741047   
119    0.0    0.0    0.0    0.0  0.621704  0.619675  0.622517  0.063361   

        X_140     X_141  ...    X_2868    X_2869     X_2870  X_2871      HOUR  \
84   0.551020 -0.690104  ...  0.660000  0.185721   1.368812     0.0  1.777778   
85   0.024943 -1.226562  ...  0.679286  0.161771   0.158416     0.0  1.777778   
86   0.006803  0.226562  ...  0.215000  0.045639   0.509901     0.0 -0.111111   
87  -1.340136 -2.565104  ...  0.007857  0.082241  -0.089109     0.0  0.333333   
88   0.192744  0.039062  ...  0.018571  0.009941   0.551980     0.0 -0.111111   
89   0.877551  0.356771  ...  0.063571  0.000904   0.306931     0.0  0.777778   
90   0.700680  0.929688  ...  0.661429  0.084953  -0.470297     0.0 -0.666667   
91   0.269841  0.429688  ...  0.325714  0.050158   0.549505     0.0  0.555556   
92   0.950113  1.091146  ... -3.568571 -2.499322 -15.997525     0.0 -0.333333   
93   0.596372  0.466146  ... -0.668571  0.057840   0.121287     0.0  0.777778   
94  -0.002268 -0.992188  ... -3.568571 -2.499322 -15.997525     0.0 -0.222222   
95   0.505669  0.617188  ...  0.458571  0.056936  -0.106436     0.0 -0.777778   
96  -0.029478  0.315104  ... -0.535000 -0.848622   3.396039    -1.0 -0.222222   
97  -0.219955  0.065104  ...  0.234286  0.063714  -0.113861     0.0 -0.666667   
98  -0.160998 

In [124]:
T05_vote_regressor_models = [
    ('ada',  T05_model_ada),
    ('lightgbm', T05_model_lightgbm),
    ('rf', T05_model_rf),
    ('gbc', T05_model_gbr),
    ('et', T05_model_et),
    ('cat', T05_model_catboost),
    ('xgb', T05_model_xgb),
]

In [125]:
T05_vote_regressor = VotingRegressor(estimators = T05_vote_regressor_models)
#soft_vote_cv = cross_validate(soft_vote, T01_datas, T01_class, cv = KFold)
#soft_vote.fit(T05_datas, T05_class)

In [126]:
T05_vote_regressor.fit(T05_data, T05_target)
T05_pred = T05_vote_regressor.predict(T05_data)

In [127]:
T05_datas = pd.DataFrame(T05_pred, columns = ['Y_Quality'])

In [128]:
#T05_final_regression_model = finalize_model(T05_model_et)

In [129]:
#T05_prediction = predict_model(T05_final_regression_model, data=T05_data)
#prediction.drop(['Y_Quality'], axis = 1, inplace = True)
#T05_prediction

In [130]:
#T05_datas = T05_prediction['prediction_label']
#T05_datas = pd.DataFrame(T05_datas.values, columns = ['Y_Quality'])
#T05_datas

In [131]:
T05y_idx= T05_class.index
T05y_idx = pd.DataFrame(T05y_idx, columns = ['index'])
T05_datas = pd.concat([T05y_idx, T05_datas], axis = 1)
T05_datas = T05_datas.set_index('index')
T05_datas

Y_Quality
index           
0       0.533175
2       0.531474
4       0.531926
6       0.533457
8       0.531898
...          ...
549     0.534109
550     0.534265
551     0.527136
552     0.530497
555     0.522454

[120 rows x 1 columns]

In [133]:
from pycaret.classification import *
# 분류 패키지의 모든 모듈을 임포트한다.
exp_clf101 = setup(data=T05_datas, 
                   target=T05_class, 
                   fold=5,
                   session_id=414)
top5 = compare_models(sort='Accuracy', n_select=5)

Processing:   0%|          | 0/73 [00:00<?, ?it/s]

In [134]:
T05_total_models = []

T05_model_lightgbm = create_model('lightgbm', fold = 5)
T05_total_models.append(T05_model_lightgbm)

T05_model_rf = create_model('rf', fold = 5)
T05_total_models.append(T05_model_rf)

T05_model_gbc = create_model('gbc', fold = 5)
T05_total_models.append(T05_model_gbc)

T05_model_et = create_model('et', fold = 5)
T05_total_models.append(T05_model_et)

T05_model_catboost = create_model('catboost', fold = 5)
T05_total_models.append(T05_model_catboost)

T05_model_xgb = create_model('xgboost', fold = 5)
T05_total_models.append(T05_model_xgb)

T05_model_ada = create_model('ada', fold = 5)

T05_total_models.append(T05_model_ada)

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

In [135]:
T05_model_lightgbm = tune_model(T05_model_lightgbm, fold=5, choose_better = True)

T05_model_rf = tune_model(T05_model_rf, fold=5, choose_better = True)

T05_model_gbc = tune_model(T05_model_gbc, fold=5, choose_better = True)

T05_model_et = tune_model(T05_model_et, fold=5, choose_better = True)

T05_model_catboost = tune_model(T05_model_catboost, fold=5, choose_better = True)

T05_model_xgb = tune_model(T05_model_xgb, fold=5, choose_better = True)

T05_model_ada = tune_model(T05_model_ada, fold=5, choose_better = True)

Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

...

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


In [136]:
T05_tuned_models = [T05_model_lightgbm, T05_model_rf, T05_model_gbc, T05_model_et, T05_model_catboost, T05_model_xgb, T05_model_ada]
T05_tuned_models

[LGBMClassifier(boosting_type='gbdt', class_weight=None, colsample_bytree=1.0,
                importance_type='split', learning_rate=0.1, max_depth=-1,
                min_child_samples=20, min_child_weight=0.001, min_split_gain=0.0,
                n_estimators=100, n_jobs=-1, num_leaves=31, objective=None,
                random_state=414, reg_alpha=0.0, reg_lambda=0.0, silent=True,
                subsample=1.0, subsample_for_bin=200000, subsample_freq=0),
 RandomForestClassifier(bootstrap=True, ccp_alpha=0.0, class_weight='balanced',
                        criterion='gini', max_depth=11, max_features='log2',
                        max_leaf_nodes=None, max_samples=None,
                        min_impurity_decrease=0.001, min_samples_leaf=5,
                        min_samples_split=9, min_weight_fraction_leaf=0.0,
                        n_estimators=10, n_jobs=-1, oob_score=False,
                        random_state=414, verbose=0, warm_start=False),
 GradientBoostingClassifie

In [137]:
for model in T05_tuned_models:
    display(predict_model(model))

Y_Quality  Y_Class  prediction_label  prediction_score
84    0.520170        0                 0            0.9888
85    0.525313        0                 1            0.5596
86    0.527798        1                 1            0.9949
87    0.520328        0                 0            0.9888
88    0.550434        2                 2            0.9898
89    0.515399        0                 0            0.9888
90    0.527209        1                 1            0.9949
91    0.543311        2                 2            0.9898
92    0.529082        1                 1            0.9949
93    0.527610        1                 1            0.9949
94    0.525162        0                 1            0.5596
95    0.534148        2                 1            0.9862
96    0.531898        1                 1            0.9947
97    0.529910        1                 1            0.9949
98    0.557698        2                 2            0.9898
99    0.525406        1                 1            0.5596
100   0.526986        1                 1            0.9949
101   0.560599        2                 2            0.9898
102   0.539450        2                 2            0.9898
103   0.520294        0                 0            0.9888
104   0.531857        1                 1            0.9947
105   0.521359        0                 0            0.9888
106   0.546629        2                 2            0.9898
107   0.533457        1                 1            0.9862
108   0.521373        0                 0            0.9888
109   0.544003        2                 2            0.9898
110   0.558832        2                 2            0.9898
111   0.523777        0                 0            0.9888
112   0.521340        0                 0            0.9888
113   0.523155        0                 0            0.9888
114   0.523902        0                 0            0.9888
115   0.531474        1                 1            0.9949
116   0.533680        1                 1            0.9862
117   0.532053        1                 1            0.9947
118   0.531446        1                 1            0.9949
119   0.536877        2                 2            0.9898

Y_Quality  Y_Class  prediction_label  prediction_score
84    0.520170        0                 0            1.0000
85    0.525313        0                 0            0.6512
86    0.527798        1                 1            1.0000
87    0.520328        0                 0            1.0000
88    0.550434        2                 2            1.0000
89    0.515399        0                 0            1.0000
90    0.527209        1                 1            1.0000
91    0.543311        2                 2            1.0000
92    0.529082        1                 1            1.0000
93    0.527610        1                 1            1.0000
94    0.525162        0                 0            0.6512
95    0.534148        2                 1            0.9000
96    0.531898        1                 1            1.0000
97    0.529910        1                 1            1.0000
98    0.557698        2                 2            1.0000
99    0.525406        1                 0            0.6512
100   0.526986        1                 1            1.0000
101   0.560599        2                 2            1.0000
102   0.539450        2                 2            1.0000
103   0.520294        0                 0            1.0000
104   0.531857        1                 1            1.0000
105   0.521359        0                 0            1.0000
106   0.546629        2                 2            1.0000
107   0.533457        1                 1            1.0000
108   0.521373        0                 0            1.0000
109   0.544003        2                 2            1.0000
110   0.558832        2                 2            1.0000
111   0.523777        0                 0            0.9531
112   0.521340        0                 0            1.0000
113   0.523155        0                 0            0.9531
114   0.523902        0                 0            0.9346
115   0.531474        1                 1            1.0000
116   0.533680        1                 1            1.0000
117   0.532053        1                 1            1.0000
118   0.531446        1                 1            1.0000
119   0.536877        2                 2            1.0000

Y_Quality  Y_Class  prediction_label  prediction_score
84    0.520170        0                 0            0.9446
85    0.525313        0                 0            0.5199
86    0.527798        1                 1            0.9047
87    0.520328        0                 0            0.9446
88    0.550434        2                 2            0.9068
89    0.515399        0                 0            0.9446
90    0.527209        1                 1            0.9047
91    0.543311        2                 2            0.9068
92    0.529082        1                 1            0.9047
93    0.527610        1                 1            0.9047
94    0.525162        0                 0            0.5199
95    0.534148        2                 1            0.9047
96    0.531898        1                 1            0.9047
97    0.529910        1                 1            0.9047
98    0.557698        2                 2            0.9068
99    0.525406        1                 0            0.5199
100   0.526986        1                 1            0.9047
101   0.560599        2                 2            0.9068
102   0.539450        2                 2            0.9068
103   0.520294        0                 0            0.9446
104   0.531857        1                 1            0.9047
105   0.521359        0                 0            0.9446
106   0.546629        2                 2            0.9068
107   0.533457        1                 1            0.9047
108   0.521373        0                 0            0.9446
109   0.544003        2                 2            0.9068
110   0.558832        2                 2            0.9068
111   0.523777        0                 0            0.9446
112   0.521340        0                 0            0.9446
113   0.523155        0                 0            0.9446
114   0.523902        0                 0            0.8827
115   0.531474        1                 1            0.9047
116   0.533680        1                 1            0.9047
117   0.532053        1                 1            0.9047
118   0.531446        1                 1            0.9047
119   0.536877        2                 2            0.9068

Y_Quality  Y_Class  prediction_label  prediction_score
84    0.520170        0                 0            0.6371
85    0.525313        0                 1            0.4071
86    0.527798        1                 1            0.4962
87    0.520328        0                 0            0.6331
88    0.550434        2                 2            0.6551
89    0.515399        0                 0            0.6951
90    0.527209        1                 1            0.4806
91    0.543311        2                 2            0.6212
92    0.529082        1                 1            0.5054
93    0.527610        1                 1            0.4946
94    0.525162        0                 0            0.4173
95    0.534148        2                 1            0.4399
96    0.531898        1                 1            0.4798
97    0.529910        1                 1            0.5053
98    0.557698        2                 2            0.6585
99    0.525406        1                 1            0.4130
100   0.526986        1                 1            0.4676
101   0.560599        2                 2            0.6585
102   0.539450        2                 2            0.5932
103   0.520294        0                 0            0.6331
104   0.531857        1                 1            0.4798
105   0.521359        0                 0            0.6015
106   0.546629        2                 2            0.6438
107   0.533457        1                 1            0.4588
108   0.521373        0                 0            0.5992
109   0.544003        2                 2            0.6259
110   0.558832        2                 2            0.6585
111   0.523777        0                 0            0.4901
112   0.521340        0                 0            0.6015
113   0.523155        0                 0            0.5094
114   0.523902        0                 0            0.4783
115   0.531474        1                 1            0.4860
116   0.533680        1                 1            0.4558
117   0.532053        1                 1            0.4805
118   0.531446        1                 1            0.4860
119   0.536877        2                 2            0.5100

Y_Quality  Y_Class  prediction_label  prediction_score
84    0.520170        0                 0            0.3335
85    0.525313        0                 0            0.3334
86    0.527798        1                 1            0.3335
87    0.520328        0                 0            0.3335
88    0.550434        2                 2            0.3335
89    0.515399        0                 0            0.3335
90    0.527209        1                 1            0.3335
91    0.543311        2                 2            0.3335
92    0.529082        1                 1            0.3335
93    0.527610        1                 1            0.3335
94    0.525162        0                 0            0.3334
95    0.534148        2                 1            0.3334
96    0.531898        1                 1            0.3335
97    0.529910        1                 1            0.3335
98    0.557698        2                 2            0.3335
99    0.525406        1                 1            0.3334
100   0.526986        1                 1            0.3335
101   0.560599        2                 2            0.3335
102   0.539450        2                 2            0.3335
103   0.520294        0                 0            0.3335
104   0.531857        1                 1            0.3335
105   0.521359        0                 0            0.3335
106   0.546629        2                 2            0.3335
107   0.533457        1                 1            0.3335
108   0.521373        0                 0            0.3335
109   0.544003        2                 2            0.3335
110   0.558832        2                 2            0.3335
111   0.523777        0                 0            0.3335
112   0.521340        0                 0            0.3335
113   0.523155        0                 0            0.3335
114   0.523902        0                 0            0.3334
115   0.531474        1                 1            0.3335
116   0.533680        1                 1            0.3335
117   0.532053        1                 1            0.3335
118   0.531446        1                 1            0.3335
119   0.536877        2                 2            0.3335

Y_Quality  Y_Class  prediction_label  prediction_score
84    0.520170        0                 0            0.3339
85    0.525313        0                 0            0.3336
86    0.527798        1                 1            0.3338
87    0.520328        0                 0            0.3339
88    0.550434        2                 2            0.3339
89    0.515399        0                 0            0.3339
90    0.527209        1                 1            0.3338
91    0.543311        2                 2            0.3339
92    0.529082        1                 1            0.3338
93    0.527610        1                 1            0.3338
94    0.525162        0                 0            0.3336
95    0.534148        2                 1            0.3338
96    0.531898        1                 1            0.3338
97    0.529910        1                 1            0.3338
98    0.557698        2                 2            0.3339
99    0.525406        1                 0            0.3336
100   0.526986        1                 1            0.3338
101   0.560599        2                 2            0.3339
102   0.539450        2                 2            0.3339
103   0.520294        0                 0            0.3339
104   0.531857        1                 1            0.3338
105   0.521359        0                 0            0.3339
106   0.546629        2                 2            0.3339
107   0.533457        1                 1            0.3338
108   0.521373        0                 0            0.3339
109   0.544003        2                 2            0.3339
110   0.558832        2                 2            0.3339
111   0.523777        0                 0            0.3339
112   0.521340        0                 0            0.3339
113   0.523155        0                 0            0.3339
114   0.523902        0                 0            0.3339
115   0.531474        1                 1            0.3338
116   0.533680        1                 1            0.3338
117   0.532053        1                 1            0.3338
118   0.531446        1                 1            0.3338
119   0.536877        2                 2            0.3339

Y_Quality  Y_Class  prediction_label  prediction_score
84    0.520170        0                 0            0.7013
85    0.525313        0                 0            0.5834
86    0.527798        1                 1            0.9910
87    0.520328        0                 0            0.7013
88    0.550434        2                 2            0.9213
89    0.515399        0                 0            0.7013
90    0.527209        1                 1            0.9910
91    0.543311        2                 2            0.9213
92    0.529082        1                 1            0.9910
93    0.527610        1                 1            0.9910
94    0.525162        0                 0            0.5834
95    0.534148        2                 1            0.9910
96    0.531898        1                 1            0.9910
97    0.529910        1                 1            0.9910
98    0.557698        2                 2            0.9213
99    0.525406        1                 0            0.5834
100   0.526986        1                 1            0.9910
101   0.560599        2                 2            0.9213
102   0.539450        2                 2            0.9213
103   0.520294        0                 0            0.7013
104   0.531857        1                 1            0.9910
105   0.521359        0                 0            0.7013
106   0.546629        2                 2            0.9213
107   0.533457        1                 1            0.9910
108   0.521373        0                 0            0.7013
109   0.544003        2                 2            0.9213
110   0.558832        2                 2            0.9213
111   0.523777        0                 0            0.7013
112   0.521340        0                 0            0.7013
113   0.523155        0                 0            0.7013
114   0.523902        0                 0            0.7013
115   0.531474        1                 1            0.9910
116   0.533680        1                 1            0.9910
117   0.532053        1                 1            0.9910
118   0.531446        1                 1            0.9910
119   0.536877        2                 2            0.9213

In [138]:
T05_vote_classification_models = [
    ('ada',  T05_model_ada),
    ('lightgbm', T05_model_lightgbm),
    ('rf', T05_model_rf),
    ('gbc', T05_model_gbc),
    ('et', T05_model_et),
    ('cat', T05_model_catboost),
    ('xgb', T05_model_xgb),
]

In [139]:
T05_soft_vote = VotingClassifier(T05_vote_classification_models, voting = 'soft')
#soft_vote_cv = cross_validate(soft_vote, T01_datas, T01_class, cv = KFold)
T05_soft_vote.fit(T05_datas, T05_class)

VotingClassifier(estimators=[('ada',
                              AdaBoostClassifier(algorithm='SAMME.R',
                                                 base_estimator=None,
                                                 learning_rate=0.05,
                                                 n_estimators=290,
                                                 random_state=414)),
                             ('lightgbm',
                              LGBMClassifier(boosting_type='gbdt',
                                             class_weight=None,
                                             colsample_bytree=1.0,
                                             importance_type='split',
                                             learning_rate=0.1, max_depth=-1,
                                             min_child_samples=20,
                                             min_child_weight=0.001,
                                             min_split_gain...
                               

In [140]:
T05_prediction = pd.DataFrame(T05_soft_vote.predict(T05_datas), columns = ['prediction_label'])
T05_prediction

prediction_label
0                   1
1                   1
2                   1
3                   1
4                   1
..                ...
115                 1
116                 2
117                 1
118                 1
119                 0

[120 rows x 1 columns]

In [117]:
T05_final_classification_model = finalize_model(T05_model_lightgbm)

In [119]:
T05_prediction = predict_model(T05_final_classification_model, data=T05_datas)
#prediction.drop(['Y_Quality'], axis = 1, inplace = True)
T05_prediction

Y_Quality  prediction_label  prediction_score
0     0.533367                 1            0.9990
1     0.531336                 1            0.9989
2     0.531602                 1            0.9990
3     0.533609                 1            0.9990
4     0.531837                 1            0.9990
..         ...               ...               ...
115   0.533785                 1            0.9990
116   0.533616                 1            0.9990
117   0.525143                 1            0.9978
118   0.529837                 1            0.9989
119   0.521435                 0            0.9983

[120 rows x 3 columns]

In [141]:
T05_y_class = pd.DataFrame(T05_class, columns = ['Y_Class'])
T05_idx = T05_y_class.index
T05_y_class = T05_y_class.reset_index()
T05_prediction = pd.concat([T05_prediction, T05_y_class], axis = 1)
T05_prediction = T05_prediction.set_index('index')
T05_prediction.drop(['Y_Class'], axis = 1, inplace = True)

In [142]:
T05_prediction

prediction_label
index                  
0                     1
2                     1
4                     1
6                     1
8                     1
...                 ...
549                   1
550                   2
551                   1
552                   1
555                   0

[120 rows x 1 columns]

# T01

In [224]:
T01_class = T01['Y_Class']
T01_target = T01['Y_Quality']
T01_data = T01.drop(['Y_Class', 'Y_Quality'], axis = 1)
T01_data

X_246  X_247  X_248  X_249  X_250  X_251  X_252  X_253  X_254  X_255  \
28     1.0   89.0    0.0   45.0   11.0   90.0   45.0   11.0   42.0    2.0   
33     1.0   95.0    0.0   45.0   11.0   98.0   45.0   11.0   42.0    2.0   
39     1.0   95.0    0.0   45.0   11.0  102.0   45.0   12.0   42.0    2.0   
40     1.0   95.0    0.0   45.0   11.0  105.0   45.0   11.0   42.0    2.0   
41     1.0   87.0    0.0   45.0   11.0  105.0   45.0   11.0   42.0    2.0   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
479    1.0   93.0  107.0   45.0   11.0    0.0   45.0   12.0   51.0    2.0   
501    2.0   95.0  124.0   45.0   11.0    0.0   45.0   12.0   51.0    2.0   
523    1.0   89.0  136.0   45.0   12.0    0.0   45.0   12.0   51.0    2.0   
531    1.0   90.0  142.0   45.0   11.0    0.0   45.0   12.0   51.0    2.0   
585    1.0   93.0   63.0   45.0   12.0    0.0   45.0   12.0   51.0    2.0   

     ...  X_2860      X_2861  X_2862  X_2863      X_2864  X_2865  HOUR  \
28   ...   182.0  174.727586   160.5   446.0  429.716981   413.0    20   
33   ...   175.7  168.258621   158.3   446.0  429.301887   413.0     7   
39   ...   184.1  173.479310   165.8   447.0  427.867925   407.0     4   
40   ...   191.8  178.832143   168.6   446.0  428.403846   413.0    12   
41   ...   182.4  170.379310   162.9   446.0  429.094340   406.0    12   
..   ...     ...         ...     ...     ...         ...     ...   ...   
479  ...   183.3  169.553571   154.2   456.0  438.132075   413.0    15   
501  ...   187.6  182.142857   175.1   466.0  445.307692   425.0    15   
523  ...   189.2  181.700000   172.7   466.0  444.615385   423.0    10   
531  ...   192.6  185.207143   173.2   466.0  446.038461   427.0    15   
585  ...   192.2  187.396552   176.7   472.0  450.339623   432.0    11   

     MINUTE  DAY_OF_WEEK  LINE_AND_CODE  
28       26            7            0.0  
33       14            2            0.0  
39       45            3            0.0  
40       26            3            0.0  
41       34            3            0.0  
..      ...          ...            ...  
479      28            2            1.0  
501      58            5            1.0  
523      39            7            1.0  
531      38            1            1.0  
585      17            1            1.0  

[129 rows x 882 columns]

In [144]:
T_01c = T01_data.columns
T_01scaler = RobustScaler()
T_01scaled = T_05scaler.fit_transform(T01_data)
T01_data = pd.DataFrame(T_01scaled, columns = T_01c)
T01_data

X_246  X_247     X_248  X_249  X_250     X_251  X_252  X_253  X_254  \
0      0.0  -0.25 -0.054348    0.0    0.0  1.011236    0.0   -1.0   -1.0   
1      0.0   1.25 -0.054348    0.0    0.0  1.101124    0.0   -1.0   -1.0   
2      0.0   1.25 -0.054348    0.0    0.0  1.146067    0.0    0.0   -1.0   
3      0.0   1.25 -0.054348    0.0    0.0  1.179775    0.0   -1.0   -1.0   
4      0.0  -0.75 -0.054348    0.0    0.0  1.179775    0.0   -1.0   -1.0   
..     ...    ...       ...    ...    ...       ...    ...    ...    ...   
124    0.0   0.75  1.108696    0.0    0.0  0.000000    0.0    0.0    0.0   
125    1.0   1.25  1.293478    0.0    0.0  0.000000    0.0    0.0    0.0   
126    0.0  -0.25  1.423913    0.0    1.0  0.000000    0.0    0.0    0.0   
127    0.0   0.00  1.489130    0.0    0.0  0.000000    0.0    0.0    0.0   
128    0.0   0.75  0.630435    0.0    1.0  0.000000    0.0    0.0    0.0   

     X_255  ...    X_2860    X_2861    X_2862  X_2863    X_2864  X_2865  \
0      0.0  ... -0.053030  0.321839  0.041096    -1.9 -1.452964    -5.0   
1      0.0  ... -0.530303 -0.217241 -0.109589    -1.9 -1.500816    -5.0   
2      0.0  ...  0.106061  0.217816  0.404110    -1.8 -1.666123    -8.0   
3      0.0  ...  0.689394  0.663885  0.595890    -1.9 -1.604342    -5.0   
4      0.0  ... -0.022727 -0.040517  0.205479    -1.9 -1.524742    -8.5   
..     ...  ...       ...       ...       ...     ...       ...     ...   
124    0.0  ...  0.045455 -0.109329 -0.390411    -0.9 -0.482871    -5.0   
125    0.0  ...  0.371212  0.939778  1.041096     0.1  0.344334     1.0   
126    0.0  ...  0.492424  0.902874  0.876712     0.1  0.264525     0.0   
127    0.0  ...  0.750000  1.195135  0.910959     0.1  0.428577     2.0   
128    0.0  ...  0.719697  1.377586  1.150685     0.7  0.924415     4.5   

         HOUR    MINUTE  DAY_OF_WEEK  LINE_AND_CODE  
0    0.777778 -0.142857     0.666667           -1.0  
1   -0.666667 -0.571429    -1.000000           -1.0  
2   -1.000000  0.535714    -0.666667           -1.0  
3   -0.111111 -0.142857    -0.666667           -1.0  
4   -0.111111  0.142857    -0.666667           -1.0  
..        ...       ...          ...            ...  
124  0.222222 -0.071429    -1.000000            0.0  
125  0.222222  1.000000     0.000000            0.0  
126 -0.333333  0.321429     0.666667            0.0  
127  0.222222  0.285714    -1.333333            0.0  
128 -0.222222 -0.464286    -1.333333            0.0  

[129 rows x 882 columns]

In [145]:
T01_y_class = pd.DataFrame(T01_target, columns = ['Y_Quality'])
T01_idx = T01_y_class.index
T01_y_class = T01_y_class.reset_index()
T01_data = pd.concat([T01_data, T01_y_class], axis = 1)
T01_data = T01_data.set_index('index')
T01_data.drop(['Y_Quality'], axis = 1, inplace = True)
T01_data

X_246  X_247     X_248  X_249  X_250     X_251  X_252  X_253  X_254  \
index                                                                        
28       0.0  -0.25 -0.054348    0.0    0.0  1.011236    0.0   -1.0   -1.0   
33       0.0   1.25 -0.054348    0.0    0.0  1.101124    0.0   -1.0   -1.0   
39       0.0   1.25 -0.054348    0.0    0.0  1.146067    0.0    0.0   -1.0   
40       0.0   1.25 -0.054348    0.0    0.0  1.179775    0.0   -1.0   -1.0   
41       0.0  -0.75 -0.054348    0.0    0.0  1.179775    0.0   -1.0   -1.0   
...      ...    ...       ...    ...    ...       ...    ...    ...    ...   
479      0.0   0.75  1.108696    0.0    0.0  0.000000    0.0    0.0    0.0   
501      1.0   1.25  1.293478    0.0    0.0  0.000000    0.0    0.0    0.0   
523      0.0  -0.25  1.423913    0.0    1.0  0.000000    0.0    0.0    0.0   
531      0.0   0.00  1.489130    0.0    0.0  0.000000    0.0    0.0    0.0   
585      0.0   0.75  0.630435    0.0    1.0  0.000000    0.0    0.0    0.0   

       X_255  ...    X_2860    X_2861    X_2862  X_2863    X_2864  X_2865  \
index         ...                                                           
28       0.0  ... -0.053030  0.321839  0.041096    -1.9 -1.452964    -5.0   
33       0.0  ... -0.530303 -0.217241 -0.109589    -1.9 -1.500816    -5.0   
39       0.0  ...  0.106061  0.217816  0.404110    -1.8 -1.666123    -8.0   
40       0.0  ...  0.689394  0.663885  0.595890    -1.9 -1.604342    -5.0   
41       0.0  ... -0.022727 -0.040517  0.205479    -1.9 -1.524742    -8.5   
...      ...  ...       ...       ...       ...     ...       ...     ...   
479      0.0  ...  0.045455 -0.109329 -0.390411    -0.9 -0.482871    -5.0   
501      0.0  ...  0.371212  0.939778  1.041096     0.1  0.344334     1.0   
523      0.0  ...  0.492424  0.902874  0.876712     0.1  0.264525     0.0   
531      0.0  ...  0.750000  1.195135  0.910959     0.1  0.428577     2.0   
585      0.0  ...  0.719697  1.377586  1.150685     0.7  0.924415     4.5   

           HOUR    MINUTE  DAY_OF_WEEK  LINE_AND_CODE  
index                                                  
28     0.777778 -0.142857     0.666667           -1.0  
33    -0.666667 -0.571429    -1.000000           -1.0  
39    -1.000000  0.535714    -0.666667           -1.0  
40    -0.111111 -0.142857    -0.666667           -1.0  
41    -0.111111  0.142857    -0.666667           -1.0  
...         ...       ...          ...            ...  
479    0.222222 -0.071429    -1.000000            0.0  
501    0.222222  1.000000     0.000000            0.0  
523   -0.333333  0.321429     0.666667            0.0  
531    0.222222  0.285714    -1.333333            0.0  
585   -0.222222 -0.464286    -1.333333            0.0  

[129 rows x 882 columns]

In [146]:
#13
from pycaret.regression import *
setup_rgs = setup(data = T01_data, target = T01_target, session_id = 414)
top5 = compare_models(sort='MSE', n_select=5)

Processing:   0%|          | 0/89 [00:00<?, ?it/s]

In [147]:
T01_total_models = []

T01_model_lightgbm = create_model('lightgbm', fold = 5)
T01_total_models.append(T01_model_lightgbm)

T01_model_rf = create_model('rf', fold = 5)
T01_total_models.append(T01_model_rf)

T01_model_gbr = create_model('gbr', fold = 5)
T01_total_models.append(T01_model_gbr)

T01_model_et = create_model('et', fold = 5)
T01_total_models.append(T01_model_et)

T01_model_catboost = create_model('catboost', fold = 5)
T01_total_models.append(T01_model_catboost)

T01_model_xgb = create_model('xgboost', fold = 5)
T01_total_models.append(T01_model_xgb)

T01_model_ada = create_model('ada', fold = 5)
T01_total_models.append(T01_model_ada)

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

In [148]:
T01_model_lightgbm = tune_model(T01_model_lightgbm, fold=5, choose_better = True)

T01_model_rf = tune_model(T01_model_rf, fold=5, choose_better = True)

T01_model_gbr = tune_model(T01_model_gbr, fold=5, choose_better = True)

T01_model_et = tune_model(T01_model_et, fold=5, choose_better = True)

T01_model_catboost = tune_model(T01_model_catboost, fold=5, choose_better = True)

T01_model_xgb = tune_model(T01_model_xgb, fold=5, choose_better = True)

T01_model_ada = tune_model(T01_model_ada, fold=5, choose_better = True)

Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

...

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


In [149]:
T01_tuned_models = [T01_model_lightgbm, T01_model_rf, T01_model_gbr, T01_model_et, T01_model_catboost, T01_model_xgb, T01_model_ada]
T01_tuned_models

[LGBMRegressor(boosting_type='gbdt', class_weight=None, colsample_bytree=1.0,
               importance_type='split', learning_rate=0.1, max_depth=-1,
               min_child_samples=20, min_child_weight=0.001, min_split_gain=0.0,
               n_estimators=100, n_jobs=-1, num_leaves=31, objective=None,
               random_state=414, reg_alpha=0.0, reg_lambda=0.0, silent=True,
               subsample=1.0, subsample_for_bin=200000, subsample_freq=0),
 RandomForestRegressor(bootstrap=True, ccp_alpha=0.0, criterion='squared_error',
                       max_depth=None, max_features='auto', max_leaf_nodes=None,
                       max_samples=None, min_impurity_decrease=0.0,
                       min_samples_leaf=1, min_samples_split=2,
                       min_weight_fraction_leaf=0.0, n_estimators=100, n_jobs=-1,
                       oob_score=False, random_state=414, verbose=0,
                       warm_start=False),
 GradientBoostingRegressor(alpha=0.9, ccp_alpha=0.0, c

In [150]:
for model in T01_tuned_models:
    display(predict_model(model))

X_246  X_247     X_248  X_249  X_250     X_251  X_252  X_253  X_254  \
90     1.0   0.25 -0.054348    0.0    0.0  0.426966    0.0   -1.0   -1.0   
91     0.0   1.25 -0.054348    0.0    0.0  0.314607    0.0   -1.0   -1.0   
92     1.0  -0.75 -0.054348    0.0    0.0  1.415730    0.0   -1.0   -1.0   
93     0.0   1.25  0.663043    0.0    0.0  0.000000    0.0    0.0    0.0   
94     0.0   0.25  0.217391    0.0    1.0  0.000000    0.0    0.0    0.0   
95     0.0  -0.25 -0.054348    0.0    0.0  1.370787    0.0   -1.0   -1.0   
96     0.0  -0.25  0.652174    0.0    1.0  0.000000    0.0    0.0    0.0   
97     0.0  -0.75  1.510870    0.0    1.0  0.000000    0.0    0.0    0.0   
98     0.0   0.75  0.163043    0.0    1.0  0.000000    0.0    0.0    0.0   
99     0.0   0.75  1.108696    0.0    0.0  0.000000    0.0    0.0    0.0   
100    0.0   0.75  1.586957    0.0    1.0  0.000000    0.0    0.0    0.0   
101    1.0   0.25  1.663043    0.0    0.0  0.000000    0.0    0.0    0.0   
102    0.0   0.75  1.445652    0.0    0.0  0.000000    0.0    0.0    0.0   
103    0.0  -0.25  0.782609    0.0    1.0  0.000000    0.0    0.0    0.0   
104    1.0   0.25  1.793478    0.0    0.0  0.000000    0.0    0.0    0.0   
105    0.0  -0.25  0.021739    0.0    1.0  0.000000    0.0    0.0    0.0   
106    0.0   0.00  1.489130    0.0    0.0  0.000000    0.0    0.0    0.0   
107    1.0   0.25  0.826087    0.0    1.0  0.000000    0.0    0.0    0.0   
108    0.0  -0.75 -0.054348    0.0    0.0  0.123596    0.0   -1.0   -1.0   
109    0.0  -0.50  0.076087    0.0    1.0  0.000000    0.0    0.0    0.0   
110    0.0   1.25 -0.054348    0.0    0.0  1.101124    0.0   -1.0   -1.0   
111    0.0  -0.25 -0.054348    0.0    0.0  0.146067    0.0    0.0   -1.0   
112    1.0   1.50  0.326087    0.0    1.0  0.000000    0.0    0.0    0.0   
113    1.0   0.75  1.793478    0.0    0.0  0.000000    0.0    0.0    0.0   
114    0.0   0.00 -0.054348    0.0    0.0  0.393258    0.0   -1.0   -1.0   
115    0.0  -0.50  0.847826    0.0    1.0  0.000000    0.0    0.0    0.0   
116    1.0   0.25 -0.054348    0.0    0.0  0.752809    0.0   -1.0   -1.0   
117    1.0  -0.50 -0.054348    0.0    0.0  1.011236    0.0   -1.0   -1.0   
118    0.0   1.25 -0.054348    0.0    0.0  0.247191    0.0   -1.0   -1.0   
119    0.0  -0.50 -0.054348    0.0    0.0  1.078652    0.0   -1.0   -1.0   
120    1.0  -0.50 -0.054348    0.0    0.0  0.955056    0.0   -1.0   -1.0   
121    0.0   1.25  1.521739    0.0    0.0  0.000000    0.0    0.0    0.0   
122    0.0  -0.50 -0.054348    0.0    0.0  1.876405    0.0   -1.0   -1.0   
123    0.0  -0.25  0.206522    0.0    1.0  0.000000    0.0    0.0    0.0   
124    0.0  -0.25 -0.054348    0.0    0.0  1.449438    0.0   -1.0   -1.0   
125    0.0  -0.25  0.619565    0.0    0.0  0.000000    0.0    0.0    0.0   
126    0.0  -0.25  0.510870    0.0    1.0  0.000000    0.0    0.0    0.0   
127    1.0  -0.50 -0.054348    0.0    0.0  0.471910    0.0   -1.0   -1.0   
128    0.0   0.75 -0.010870    0.0    0.0  0.000000    0.0    0.0    0.0   

     X_255  ...    X_2862  X_2863    X_2864  X_2865      HOUR    MINUTE  \
90     0.0  ... -0.623288    -0.9 -0.317564     0.0 -1.222222  0.142857   
91     0.0  ... -0.650685    -0.9 -0.427155    -0.5  0.222222  0.035714   
92     0.0  ...  1.041096    -0.2 -0.167482     0.0  0.555556  0.785714   
93     0.0  ... -0.383562    -0.9 -0.132304    -0.5  0.444444 -0.500000   
94     0.0  ...  0.506849     0.1  0.406408     0.0 -0.666667  0.107143   
95     0.0  ...  1.219178     0.0 -0.048061     0.0 -0.222222  0.035714   
96     0.0  ... -0.294521     0.1  0.758899     4.5  0.222222  0.071429   
97     0.0  ...  0.000000    -1.9 -1.369348    -5.0  0.777778 -0.428571   
98     0.0  ...  0.767123    -0.9 -0.263187     0.0  0.444444 -0.821429   
99     0.0  ... -0.390411    -0.9 -0.482871    -5.0  0.222222 -0.071429   
100    0.0  ... -0.376712     0.1  0.654704     4.5 -1.444444 -0.035714   
101    0.0  ...  0.458904    -1.9 -1.852637    -9.5 -1.000000  0

X_246  X_247     X_248  X_249  X_250     X_251  X_252  X_253  X_254  \
90     1.0   0.25 -0.054348    0.0    0.0  0.426966    0.0   -1.0   -1.0   
91     0.0   1.25 -0.054348    0.0    0.0  0.314607    0.0   -1.0   -1.0   
92     1.0  -0.75 -0.054348    0.0    0.0  1.415730    0.0   -1.0   -1.0   
93     0.0   1.25  0.663043    0.0    0.0  0.000000    0.0    0.0    0.0   
94     0.0   0.25  0.217391    0.0    1.0  0.000000    0.0    0.0    0.0   
95     0.0  -0.25 -0.054348    0.0    0.0  1.370787    0.0   -1.0   -1.0   
96     0.0  -0.25  0.652174    0.0    1.0  0.000000    0.0    0.0    0.0   
97     0.0  -0.75  1.510870    0.0    1.0  0.000000    0.0    0.0    0.0   
98     0.0   0.75  0.163043    0.0    1.0  0.000000    0.0    0.0    0.0   
99     0.0   0.75  1.108696    0.0    0.0  0.000000    0.0    0.0    0.0   
100    0.0   0.75  1.586957    0.0    1.0  0.000000    0.0    0.0    0.0   
101    1.0   0.25  1.663043    0.0    0.0  0.000000    0.0    0.0    0.0   
102    0.0   0.75  1.445652    0.0    0.0  0.000000    0.0    0.0    0.0   
103    0.0  -0.25  0.782609    0.0    1.0  0.000000    0.0    0.0    0.0   
104    1.0   0.25  1.793478    0.0    0.0  0.000000    0.0    0.0    0.0   
105    0.0  -0.25  0.021739    0.0    1.0  0.000000    0.0    0.0    0.0   
106    0.0   0.00  1.489130    0.0    0.0  0.000000    0.0    0.0    0.0   
107    1.0   0.25  0.826087    0.0    1.0  0.000000    0.0    0.0    0.0   
108    0.0  -0.75 -0.054348    0.0    0.0  0.123596    0.0   -1.0   -1.0   
109    0.0  -0.50  0.076087    0.0    1.0  0.000000    0.0    0.0    0.0   
110    0.0   1.25 -0.054348    0.0    0.0  1.101124    0.0   -1.0   -1.0   
111    0.0  -0.25 -0.054348    0.0    0.0  0.146067    0.0    0.0   -1.0   
112    1.0   1.50  0.326087    0.0    1.0  0.000000    0.0    0.0    0.0   
113    1.0   0.75  1.793478    0.0    0.0  0.000000    0.0    0.0    0.0   
114    0.0   0.00 -0.054348    0.0    0.0  0.393258    0.0   -1.0   -1.0   
115    0.0  -0.50  0.847826    0.0    1.0  0.000000    0.0    0.0    0.0   
116    1.0   0.25 -0.054348    0.0    0.0  0.752809    0.0   -1.0   -1.0   
117    1.0  -0.50 -0.054348    0.0    0.0  1.011236    0.0   -1.0   -1.0   
118    0.0   1.25 -0.054348    0.0    0.0  0.247191    0.0   -1.0   -1.0   
119    0.0  -0.50 -0.054348    0.0    0.0  1.078652    0.0   -1.0   -1.0   
120    1.0  -0.50 -0.054348    0.0    0.0  0.955056    0.0   -1.0   -1.0   
121    0.0   1.25  1.521739    0.0    0.0  0.000000    0.0    0.0    0.0   
122    0.0  -0.50 -0.054348    0.0    0.0  1.876405    0.0   -1.0   -1.0   
123    0.0  -0.25  0.206522    0.0    1.0  0.000000    0.0    0.0    0.0   
124    0.0  -0.25 -0.054348    0.0    0.0  1.449438    0.0   -1.0   -1.0   
125    0.0  -0.25  0.619565    0.0    0.0  0.000000    0.0    0.0    0.0   
126    0.0  -0.25  0.510870    0.0    1.0  0.000000    0.0    0.0    0.0   
127    1.0  -0.50 -0.054348    0.0    0.0  0.471910    0.0   -1.0   -1.0   
128    0.0   0.75 -0.010870    0.0    0.0  0.000000    0.0    0.0    0.0   

     X_255  ...    X_2862  X_2863    X_2864  X_2865      HOUR    MINUTE  \
90     0.0  ... -0.623288    -0.9 -0.317564     0.0 -1.222222  0.142857   
91     0.0  ... -0.650685    -0.9 -0.427155    -0.5  0.222222  0.035714   
92     0.0  ...  1.041096    -0.2 -0.167482     0.0  0.555556  0.785714   
93     0.0  ... -0.383562    -0.9 -0.132304    -0.5  0.444444 -0.500000   
94     0.0  ...  0.506849     0.1  0.406408     0.0 -0.666667  0.107143   
95     0.0  ...  1.219178     0.0 -0.048061     0.0 -0.222222  0.035714   
96     0.0  ... -0.294521     0.1  0.758899     4.5  0.222222  0.071429   
97     0.0  ...  0.000000    -1.9 -1.369348    -5.0  0.777778 -0.428571   
98     0.0  ...  0.767123    -0.9 -0.263187     0.0  0.444444 -0.821429   
99     0.0  ... -0.390411    -0.9 -0.482871    -5.0  0.222222 -0.071429   
100    0.0  ... -0.376712     0.1  0.654704     4.5 -1.444444 -0.035714   
101    0.0  ...  0.458904    -1.9 -1.852637    -9.5 -1.000000  0

X_246  X_247     X_248  X_249  X_250     X_251  X_252  X_253  X_254  \
90     1.0   0.25 -0.054348    0.0    0.0  0.426966    0.0   -1.0   -1.0   
91     0.0   1.25 -0.054348    0.0    0.0  0.314607    0.0   -1.0   -1.0   
92     1.0  -0.75 -0.054348    0.0    0.0  1.415730    0.0   -1.0   -1.0   
93     0.0   1.25  0.663043    0.0    0.0  0.000000    0.0    0.0    0.0   
94     0.0   0.25  0.217391    0.0    1.0  0.000000    0.0    0.0    0.0   
95     0.0  -0.25 -0.054348    0.0    0.0  1.370787    0.0   -1.0   -1.0   
96     0.0  -0.25  0.652174    0.0    1.0  0.000000    0.0    0.0    0.0   
97     0.0  -0.75  1.510870    0.0    1.0  0.000000    0.0    0.0    0.0   
98     0.0   0.75  0.163043    0.0    1.0  0.000000    0.0    0.0    0.0   
99     0.0   0.75  1.108696    0.0    0.0  0.000000    0.0    0.0    0.0   
100    0.0   0.75  1.586957    0.0    1.0  0.000000    0.0    0.0    0.0   
101    1.0   0.25  1.663043    0.0    0.0  0.000000    0.0    0.0    0.0   
102    0.0   0.75  1.445652    0.0    0.0  0.000000    0.0    0.0    0.0   
103    0.0  -0.25  0.782609    0.0    1.0  0.000000    0.0    0.0    0.0   
104    1.0   0.25  1.793478    0.0    0.0  0.000000    0.0    0.0    0.0   
105    0.0  -0.25  0.021739    0.0    1.0  0.000000    0.0    0.0    0.0   
106    0.0   0.00  1.489130    0.0    0.0  0.000000    0.0    0.0    0.0   
107    1.0   0.25  0.826087    0.0    1.0  0.000000    0.0    0.0    0.0   
108    0.0  -0.75 -0.054348    0.0    0.0  0.123596    0.0   -1.0   -1.0   
109    0.0  -0.50  0.076087    0.0    1.0  0.000000    0.0    0.0    0.0   
110    0.0   1.25 -0.054348    0.0    0.0  1.101124    0.0   -1.0   -1.0   
111    0.0  -0.25 -0.054348    0.0    0.0  0.146067    0.0    0.0   -1.0   
112    1.0   1.50  0.326087    0.0    1.0  0.000000    0.0    0.0    0.0   
113    1.0   0.75  1.793478    0.0    0.0  0.000000    0.0    0.0    0.0   
114    0.0   0.00 -0.054348    0.0    0.0  0.393258    0.0   -1.0   -1.0   
115    0.0  -0.50  0.847826    0.0    1.0  0.000000    0.0    0.0    0.0   
116    1.0   0.25 -0.054348    0.0    0.0  0.752809    0.0   -1.0   -1.0   
117    1.0  -0.50 -0.054348    0.0    0.0  1.011236    0.0   -1.0   -1.0   
118    0.0   1.25 -0.054348    0.0    0.0  0.247191    0.0   -1.0   -1.0   
119    0.0  -0.50 -0.054348    0.0    0.0  1.078652    0.0   -1.0   -1.0   
120    1.0  -0.50 -0.054348    0.0    0.0  0.955056    0.0   -1.0   -1.0   
121    0.0   1.25  1.521739    0.0    0.0  0.000000    0.0    0.0    0.0   
122    0.0  -0.50 -0.054348    0.0    0.0  1.876405    0.0   -1.0   -1.0   
123    0.0  -0.25  0.206522    0.0    1.0  0.000000    0.0    0.0    0.0   
124    0.0  -0.25 -0.054348    0.0    0.0  1.449438    0.0   -1.0   -1.0   
125    0.0  -0.25  0.619565    0.0    0.0  0.000000    0.0    0.0    0.0   
126    0.0  -0.25  0.510870    0.0    1.0  0.000000    0.0    0.0    0.0   
127    1.0  -0.50 -0.054348    0.0    0.0  0.471910    0.0   -1.0   -1.0   
128    0.0   0.75 -0.010870    0.0    0.0  0.000000    0.0    0.0    0.0   

     X_255  ...    X_2862  X_2863    X_2864  X_2865      HOUR    MINUTE  \
90     0.0  ... -0.623288    -0.9 -0.317564     0.0 -1.222222  0.142857   
91     0.0  ... -0.650685    -0.9 -0.427155    -0.5  0.222222  0.035714   
92     0.0  ...  1.041096    -0.2 -0.167482     0.0  0.555556  0.785714   
93     0.0  ... -0.383562    -0.9 -0.132304    -0.5  0.444444 -0.500000   
94     0.0  ...  0.506849     0.1  0.406408     0.0 -0.666667  0.107143   
95     0.0  ...  1.219178     0.0 -0.048061     0.0 -0.222222  0.035714   
96     0.0  ... -0.294521     0.1  0.758899     4.5  0.222222  0.071429   
97     0.0  ...  0.000000    -1.9 -1.369348    -5.0  0.777778 -0.428571   
98     0.0  ...  0.767123    -0.9 -0.263187     0.0  0.444444 -0.821429   
99     0.0  ... -0.390411    -0.9 -0.482871    -5.0  0.222222 -0.071429   
100    0.0  ... -0.376712     0.1  0.654704     4.5 -1.444444 -0.035714   
101    0.0  ...  0.458904    -1.9 -1.852637    -9.5 -1.000000  0

X_246  X_247     X_248  X_249  X_250     X_251  X_252  X_253  X_254  \
90     1.0   0.25 -0.054348    0.0    0.0  0.426966    0.0   -1.0   -1.0   
91     0.0   1.25 -0.054348    0.0    0.0  0.314607    0.0   -1.0   -1.0   
92     1.0  -0.75 -0.054348    0.0    0.0  1.415730    0.0   -1.0   -1.0   
93     0.0   1.25  0.663043    0.0    0.0  0.000000    0.0    0.0    0.0   
94     0.0   0.25  0.217391    0.0    1.0  0.000000    0.0    0.0    0.0   
95     0.0  -0.25 -0.054348    0.0    0.0  1.370787    0.0   -1.0   -1.0   
96     0.0  -0.25  0.652174    0.0    1.0  0.000000    0.0    0.0    0.0   
97     0.0  -0.75  1.510870    0.0    1.0  0.000000    0.0    0.0    0.0   
98     0.0   0.75  0.163043    0.0    1.0  0.000000    0.0    0.0    0.0   
99     0.0   0.75  1.108696    0.0    0.0  0.000000    0.0    0.0    0.0   
100    0.0   0.75  1.586957    0.0    1.0  0.000000    0.0    0.0    0.0   
101    1.0   0.25  1.663043    0.0    0.0  0.000000    0.0    0.0    0.0   
102    0.0   0.75  1.445652    0.0    0.0  0.000000    0.0    0.0    0.0   
103    0.0  -0.25  0.782609    0.0    1.0  0.000000    0.0    0.0    0.0   
104    1.0   0.25  1.793478    0.0    0.0  0.000000    0.0    0.0    0.0   
105    0.0  -0.25  0.021739    0.0    1.0  0.000000    0.0    0.0    0.0   
106    0.0   0.00  1.489130    0.0    0.0  0.000000    0.0    0.0    0.0   
107    1.0   0.25  0.826087    0.0    1.0  0.000000    0.0    0.0    0.0   
108    0.0  -0.75 -0.054348    0.0    0.0  0.123596    0.0   -1.0   -1.0   
109    0.0  -0.50  0.076087    0.0    1.0  0.000000    0.0    0.0    0.0   
110    0.0   1.25 -0.054348    0.0    0.0  1.101124    0.0   -1.0   -1.0   
111    0.0  -0.25 -0.054348    0.0    0.0  0.146067    0.0    0.0   -1.0   
112    1.0   1.50  0.326087    0.0    1.0  0.000000    0.0    0.0    0.0   
113    1.0   0.75  1.793478    0.0    0.0  0.000000    0.0    0.0    0.0   
114    0.0   0.00 -0.054348    0.0    0.0  0.393258    0.0   -1.0   -1.0   
115    0.0  -0.50  0.847826    0.0    1.0  0.000000    0.0    0.0    0.0   
116    1.0   0.25 -0.054348    0.0    0.0  0.752809    0.0   -1.0   -1.0   
117    1.0  -0.50 -0.054348    0.0    0.0  1.011236    0.0   -1.0   -1.0   
118    0.0   1.25 -0.054348    0.0    0.0  0.247191    0.0   -1.0   -1.0   
119    0.0  -0.50 -0.054348    0.0    0.0  1.078652    0.0   -1.0   -1.0   
120    1.0  -0.50 -0.054348    0.0    0.0  0.955056    0.0   -1.0   -1.0   
121    0.0   1.25  1.521739    0.0    0.0  0.000000    0.0    0.0    0.0   
122    0.0  -0.50 -0.054348    0.0    0.0  1.876405    0.0   -1.0   -1.0   
123    0.0  -0.25  0.206522    0.0    1.0  0.000000    0.0    0.0    0.0   
124    0.0  -0.25 -0.054348    0.0    0.0  1.449438    0.0   -1.0   -1.0   
125    0.0  -0.25  0.619565    0.0    0.0  0.000000    0.0    0.0    0.0   
126    0.0  -0.25  0.510870    0.0    1.0  0.000000    0.0    0.0    0.0   
127    1.0  -0.50 -0.054348    0.0    0.0  0.471910    0.0   -1.0   -1.0   
128    0.0   0.75 -0.010870    0.0    0.0  0.000000    0.0    0.0    0.0   

     X_255  ...    X_2862  X_2863    X_2864  X_2865      HOUR    MINUTE  \
90     0.0  ... -0.623288    -0.9 -0.317564     0.0 -1.222222  0.142857   
91     0.0  ... -0.650685    -0.9 -0.427155    -0.5  0.222222  0.035714   
92     0.0  ...  1.041096    -0.2 -0.167482     0.0  0.555556  0.785714   
93     0.0  ... -0.383562    -0.9 -0.132304    -0.5  0.444444 -0.500000   
94     0.0  ...  0.506849     0.1  0.406408     0.0 -0.666667  0.107143   
95     0.0  ...  1.219178     0.0 -0.048061     0.0 -0.222222  0.035714   
96     0.0  ... -0.294521     0.1  0.758899     4.5  0.222222  0.071429   
97     0.0  ...  0.000000    -1.9 -1.369348    -5.0  0.777778 -0.428571   
98     0.0  ...  0.767123    -0.9 -0.263187     0.0  0.444444 -0.821429   
99     0.0  ... -0.390411    -0.9 -0.482871    -5.0  0.222222 -0.071429   
100    0.0  ... -0.376712     0.1  0.654704     4.5 -1.444444 -0.035714   
101    0.0  ...  0.458904    -1.9 -1.852637    -9.5 -1.000000  0

X_246  X_247     X_248  X_249  X_250     X_251  X_252  X_253  X_254  \
90     1.0   0.25 -0.054348    0.0    0.0  0.426966    0.0   -1.0   -1.0   
91     0.0   1.25 -0.054348    0.0    0.0  0.314607    0.0   -1.0   -1.0   
92     1.0  -0.75 -0.054348    0.0    0.0  1.415730    0.0   -1.0   -1.0   
93     0.0   1.25  0.663043    0.0    0.0  0.000000    0.0    0.0    0.0   
94     0.0   0.25  0.217391    0.0    1.0  0.000000    0.0    0.0    0.0   
95     0.0  -0.25 -0.054348    0.0    0.0  1.370787    0.0   -1.0   -1.0   
96     0.0  -0.25  0.652174    0.0    1.0  0.000000    0.0    0.0    0.0   
97     0.0  -0.75  1.510870    0.0    1.0  0.000000    0.0    0.0    0.0   
98     0.0   0.75  0.163043    0.0    1.0  0.000000    0.0    0.0    0.0   
99     0.0   0.75  1.108696    0.0    0.0  0.000000    0.0    0.0    0.0   
100    0.0   0.75  1.586957    0.0    1.0  0.000000    0.0    0.0    0.0   
101    1.0   0.25  1.663043    0.0    0.0  0.000000    0.0    0.0    0.0   
102    0.0   0.75  1.445652    0.0    0.0  0.000000    0.0    0.0    0.0   
103    0.0  -0.25  0.782609    0.0    1.0  0.000000    0.0    0.0    0.0   
104    1.0   0.25  1.793478    0.0    0.0  0.000000    0.0    0.0    0.0   
105    0.0  -0.25  0.021739    0.0    1.0  0.000000    0.0    0.0    0.0   
106    0.0   0.00  1.489130    0.0    0.0  0.000000    0.0    0.0    0.0   
107    1.0   0.25  0.826087    0.0    1.0  0.000000    0.0    0.0    0.0   
108    0.0  -0.75 -0.054348    0.0    0.0  0.123596    0.0   -1.0   -1.0   
109    0.0  -0.50  0.076087    0.0    1.0  0.000000    0.0    0.0    0.0   
110    0.0   1.25 -0.054348    0.0    0.0  1.101124    0.0   -1.0   -1.0   
111    0.0  -0.25 -0.054348    0.0    0.0  0.146067    0.0    0.0   -1.0   
112    1.0   1.50  0.326087    0.0    1.0  0.000000    0.0    0.0    0.0   
113    1.0   0.75  1.793478    0.0    0.0  0.000000    0.0    0.0    0.0   
114    0.0   0.00 -0.054348    0.0    0.0  0.393258    0.0   -1.0   -1.0   
115    0.0  -0.50  0.847826    0.0    1.0  0.000000    0.0    0.0    0.0   
116    1.0   0.25 -0.054348    0.0    0.0  0.752809    0.0   -1.0   -1.0   
117    1.0  -0.50 -0.054348    0.0    0.0  1.011236    0.0   -1.0   -1.0   
118    0.0   1.25 -0.054348    0.0    0.0  0.247191    0.0   -1.0   -1.0   
119    0.0  -0.50 -0.054348    0.0    0.0  1.078652    0.0   -1.0   -1.0   
120    1.0  -0.50 -0.054348    0.0    0.0  0.955056    0.0   -1.0   -1.0   
121    0.0   1.25  1.521739    0.0    0.0  0.000000    0.0    0.0    0.0   
122    0.0  -0.50 -0.054348    0.0    0.0  1.876405    0.0   -1.0   -1.0   
123    0.0  -0.25  0.206522    0.0    1.0  0.000000    0.0    0.0    0.0   
124    0.0  -0.25 -0.054348    0.0    0.0  1.449438    0.0   -1.0   -1.0   
125    0.0  -0.25  0.619565    0.0    0.0  0.000000    0.0    0.0    0.0   
126    0.0  -0.25  0.510870    0.0    1.0  0.000000    0.0    0.0    0.0   
127    1.0  -0.50 -0.054348    0.0    0.0  0.471910    0.0   -1.0   -1.0   
128    0.0   0.75 -0.010870    0.0    0.0  0.000000    0.0    0.0    0.0   

     X_255  ...    X_2862  X_2863    X_2864  X_2865      HOUR    MINUTE  \
90     0.0  ... -0.623288    -0.9 -0.317564     0.0 -1.222222  0.142857   
91     0.0  ... -0.650685    -0.9 -0.427155    -0.5  0.222222  0.035714   
92     0.0  ...  1.041096    -0.2 -0.167482     0.0  0.555556  0.785714   
93     0.0  ... -0.383562    -0.9 -0.132304    -0.5  0.444444 -0.500000   
94     0.0  ...  0.506849     0.1  0.406408     0.0 -0.666667  0.107143   
95     0.0  ...  1.219178     0.0 -0.048061     0.0 -0.222222  0.035714   
96     0.0  ... -0.294521     0.1  0.758899     4.5  0.222222  0.071429   
97     0.0  ...  0.000000    -1.9 -1.369348    -5.0  0.777778 -0.428571   
98     0.0  ...  0.767123    -0.9 -0.263187     0.0  0.444444 -0.821429   
99     0.0  ... -0.390411    -0.9 -0.482871    -5.0  0.222222 -0.071429   
100    0.0  ... -0.376712     0.1  0.654704     4.5 -1.444444 -0.035714   
101    0.0  ...  0.458904    -1.9 -1.852637    -9.5 -1.000000  0

X_246  X_247     X_248  X_249  X_250     X_251  X_252  X_253  X_254  \
90     1.0   0.25 -0.054348    0.0    0.0  0.426966    0.0   -1.0   -1.0   
91     0.0   1.25 -0.054348    0.0    0.0  0.314607    0.0   -1.0   -1.0   
92     1.0  -0.75 -0.054348    0.0    0.0  1.415730    0.0   -1.0   -1.0   
93     0.0   1.25  0.663043    0.0    0.0  0.000000    0.0    0.0    0.0   
94     0.0   0.25  0.217391    0.0    1.0  0.000000    0.0    0.0    0.0   
95     0.0  -0.25 -0.054348    0.0    0.0  1.370787    0.0   -1.0   -1.0   
96     0.0  -0.25  0.652174    0.0    1.0  0.000000    0.0    0.0    0.0   
97     0.0  -0.75  1.510870    0.0    1.0  0.000000    0.0    0.0    0.0   
98     0.0   0.75  0.163043    0.0    1.0  0.000000    0.0    0.0    0.0   
99     0.0   0.75  1.108696    0.0    0.0  0.000000    0.0    0.0    0.0   
100    0.0   0.75  1.586957    0.0    1.0  0.000000    0.0    0.0    0.0   
101    1.0   0.25  1.663043    0.0    0.0  0.000000    0.0    0.0    0.0   
102    0.0   0.75  1.445652    0.0    0.0  0.000000    0.0    0.0    0.0   
103    0.0  -0.25  0.782609    0.0    1.0  0.000000    0.0    0.0    0.0   
104    1.0   0.25  1.793478    0.0    0.0  0.000000    0.0    0.0    0.0   
105    0.0  -0.25  0.021739    0.0    1.0  0.000000    0.0    0.0    0.0   
106    0.0   0.00  1.489130    0.0    0.0  0.000000    0.0    0.0    0.0   
107    1.0   0.25  0.826087    0.0    1.0  0.000000    0.0    0.0    0.0   
108    0.0  -0.75 -0.054348    0.0    0.0  0.123596    0.0   -1.0   -1.0   
109    0.0  -0.50  0.076087    0.0    1.0  0.000000    0.0    0.0    0.0   
110    0.0   1.25 -0.054348    0.0    0.0  1.101124    0.0   -1.0   -1.0   
111    0.0  -0.25 -0.054348    0.0    0.0  0.146067    0.0    0.0   -1.0   
112    1.0   1.50  0.326087    0.0    1.0  0.000000    0.0    0.0    0.0   
113    1.0   0.75  1.793478    0.0    0.0  0.000000    0.0    0.0    0.0   
114    0.0   0.00 -0.054348    0.0    0.0  0.393258    0.0   -1.0   -1.0   
115    0.0  -0.50  0.847826    0.0    1.0  0.000000    0.0    0.0    0.0   
116    1.0   0.25 -0.054348    0.0    0.0  0.752809    0.0   -1.0   -1.0   
117    1.0  -0.50 -0.054348    0.0    0.0  1.011236    0.0   -1.0   -1.0   
118    0.0   1.25 -0.054348    0.0    0.0  0.247191    0.0   -1.0   -1.0   
119    0.0  -0.50 -0.054348    0.0    0.0  1.078652    0.0   -1.0   -1.0   
120    1.0  -0.50 -0.054348    0.0    0.0  0.955056    0.0   -1.0   -1.0   
121    0.0   1.25  1.521739    0.0    0.0  0.000000    0.0    0.0    0.0   
122    0.0  -0.50 -0.054348    0.0    0.0  1.876405    0.0   -1.0   -1.0   
123    0.0  -0.25  0.206522    0.0    1.0  0.000000    0.0    0.0    0.0   
124    0.0  -0.25 -0.054348    0.0    0.0  1.449438    0.0   -1.0   -1.0   
125    0.0  -0.25  0.619565    0.0    0.0  0.000000    0.0    0.0    0.0   
126    0.0  -0.25  0.510870    0.0    1.0  0.000000    0.0    0.0    0.0   
127    1.0  -0.50 -0.054348    0.0    0.0  0.471910    0.0   -1.0   -1.0   
128    0.0   0.75 -0.010870    0.0    0.0  0.000000    0.0    0.0    0.0   

     X_255  ...    X_2862  X_2863    X_2864  X_2865      HOUR    MINUTE  \
90     0.0  ... -0.623288    -0.9 -0.317564     0.0 -1.222222  0.142857   
91     0.0  ... -0.650685    -0.9 -0.427155    -0.5  0.222222  0.035714   
92     0.0  ...  1.041096    -0.2 -0.167482     0.0  0.555556  0.785714   
93     0.0  ... -0.383562    -0.9 -0.132304    -0.5  0.444444 -0.500000   
94     0.0  ...  0.506849     0.1  0.406408     0.0 -0.666667  0.107143   
95     0.0  ...  1.219178     0.0 -0.048061     0.0 -0.222222  0.035714   
96     0.0  ... -0.294521     0.1  0.758899     4.5  0.222222  0.071429   
97     0.0  ...  0.000000    -1.9 -1.369348    -5.0  0.777778 -0.428571   
98     0.0  ...  0.767123    -0.9 -0.263187     0.0  0.444444 -0.821429   
99     0.0  ... -0.390411    -0.9 -0.482871    -5.0  0.222222 -0.071429   
100    0.0  ... -0.376712     0.1  0.654704     4.5 -1.444444 -0.035714   
101    0.0  ...  0.458904    -1.9 -1.852637    -9.5 -1.000000  0

X_246  X_247     X_248  X_249  X_250     X_251  X_252  X_253  X_254  \
90     1.0   0.25 -0.054348    0.0    0.0  0.426966    0.0   -1.0   -1.0   
91     0.0   1.25 -0.054348    0.0    0.0  0.314607    0.0   -1.0   -1.0   
92     1.0  -0.75 -0.054348    0.0    0.0  1.415730    0.0   -1.0   -1.0   
93     0.0   1.25  0.663043    0.0    0.0  0.000000    0.0    0.0    0.0   
94     0.0   0.25  0.217391    0.0    1.0  0.000000    0.0    0.0    0.0   
95     0.0  -0.25 -0.054348    0.0    0.0  1.370787    0.0   -1.0   -1.0   
96     0.0  -0.25  0.652174    0.0    1.0  0.000000    0.0    0.0    0.0   
97     0.0  -0.75  1.510870    0.0    1.0  0.000000    0.0    0.0    0.0   
98     0.0   0.75  0.163043    0.0    1.0  0.000000    0.0    0.0    0.0   
99     0.0   0.75  1.108696    0.0    0.0  0.000000    0.0    0.0    0.0   
100    0.0   0.75  1.586957    0.0    1.0  0.000000    0.0    0.0    0.0   
101    1.0   0.25  1.663043    0.0    0.0  0.000000    0.0    0.0    0.0   
102    0.0   0.75  1.445652    0.0    0.0  0.000000    0.0    0.0    0.0   
103    0.0  -0.25  0.782609    0.0    1.0  0.000000    0.0    0.0    0.0   
104    1.0   0.25  1.793478    0.0    0.0  0.000000    0.0    0.0    0.0   
105    0.0  -0.25  0.021739    0.0    1.0  0.000000    0.0    0.0    0.0   
106    0.0   0.00  1.489130    0.0    0.0  0.000000    0.0    0.0    0.0   
107    1.0   0.25  0.826087    0.0    1.0  0.000000    0.0    0.0    0.0   
108    0.0  -0.75 -0.054348    0.0    0.0  0.123596    0.0   -1.0   -1.0   
109    0.0  -0.50  0.076087    0.0    1.0  0.000000    0.0    0.0    0.0   
110    0.0   1.25 -0.054348    0.0    0.0  1.101124    0.0   -1.0   -1.0   
111    0.0  -0.25 -0.054348    0.0    0.0  0.146067    0.0    0.0   -1.0   
112    1.0   1.50  0.326087    0.0    1.0  0.000000    0.0    0.0    0.0   
113    1.0   0.75  1.793478    0.0    0.0  0.000000    0.0    0.0    0.0   
114    0.0   0.00 -0.054348    0.0    0.0  0.393258    0.0   -1.0   -1.0   
115    0.0  -0.50  0.847826    0.0    1.0  0.000000    0.0    0.0    0.0   
116    1.0   0.25 -0.054348    0.0    0.0  0.752809    0.0   -1.0   -1.0   
117    1.0  -0.50 -0.054348    0.0    0.0  1.011236    0.0   -1.0   -1.0   
118    0.0   1.25 -0.054348    0.0    0.0  0.247191    0.0   -1.0   -1.0   
119    0.0  -0.50 -0.054348    0.0    0.0  1.078652    0.0   -1.0   -1.0   
120    1.0  -0.50 -0.054348    0.0    0.0  0.955056    0.0   -1.0   -1.0   
121    0.0   1.25  1.521739    0.0    0.0  0.000000    0.0    0.0    0.0   
122    0.0  -0.50 -0.054348    0.0    0.0  1.876405    0.0   -1.0   -1.0   
123    0.0  -0.25  0.206522    0.0    1.0  0.000000    0.0    0.0    0.0   
124    0.0  -0.25 -0.054348    0.0    0.0  1.449438    0.0   -1.0   -1.0   
125    0.0  -0.25  0.619565    0.0    0.0  0.000000    0.0    0.0    0.0   
126    0.0  -0.25  0.510870    0.0    1.0  0.000000    0.0    0.0    0.0   
127    1.0  -0.50 -0.054348    0.0    0.0  0.471910    0.0   -1.0   -1.0   
128    0.0   0.75 -0.010870    0.0    0.0  0.000000    0.0    0.0    0.0   

     X_255  ...    X_2862  X_2863    X_2864  X_2865      HOUR    MINUTE  \
90     0.0  ... -0.623288    -0.9 -0.317564     0.0 -1.222222  0.142857   
91     0.0  ... -0.650685    -0.9 -0.427155    -0.5  0.222222  0.035714   
92     0.0  ...  1.041096    -0.2 -0.167482     0.0  0.555556  0.785714   
93     0.0  ... -0.383562    -0.9 -0.132304    -0.5  0.444444 -0.500000   
94     0.0  ...  0.506849     0.1  0.406408     0.0 -0.666667  0.107143   
95     0.0  ...  1.219178     0.0 -0.048061     0.0 -0.222222  0.035714   
96     0.0  ... -0.294521     0.1  0.758899     4.5  0.222222  0.071429   
97     0.0  ...  0.000000    -1.9 -1.369348    -5.0  0.777778 -0.428571   
98     0.0  ...  0.767123    -0.9 -0.263187     0.0  0.444444 -0.821429   
99     0.0  ... -0.390411    -0.9 -0.482871    -5.0  0.222222 -0.071429   
100    0.0  ... -0.376712     0.1  0.654704     4.5 -1.444444 -0.035714   
101    0.0  ...  0.458904    -1.9 -1.852637    -9.5 -1.000000  0

In [151]:
T01_vote_regressor_models = [
    ('ada',  T01_model_ada),
    ('lightgbm', T01_model_lightgbm),
    ('rf', T01_model_rf),
    ('gbc', T01_model_gbr),
    ('et', T01_model_et),
    ('cat', T01_model_catboost),
    ('xgb', T01_model_xgb),
]

In [152]:
T01_vote_regressor = VotingRegressor(estimators = T01_vote_regressor_models)
#soft_vote_cv = cross_validate(soft_vote, T01_datas, T01_class, cv = KFold)
#soft_vote.fit(T05_datas, T05_class)

In [153]:
T01_vote_regressor.fit(T01_data, T01_target)
T01_pred = T01_vote_regressor.predict(T01_data)

In [154]:
T01_datas = pd.DataFrame(T01_pred, columns = ['Y_Quality'])
T01_datas

Y_Quality
0     0.522792
1     0.527068
2     0.531853
3     0.530675
4     0.528856
..         ...
124   0.534632
125   0.533179
126   0.534454
127   0.558143
128   0.516612

[129 rows x 1 columns]

In [156]:
T01_class

28     0
33     1
39     1
40     1
41     1
      ..
479    1
501    1
523    1
531    2
585    0
Name: Y_Class, Length: 129, dtype: int64

In [115]:
#T01_final_regression_model = finalize_model(T01_model_ada)

In [116]:
#T01_prediction = predict_model(T01_final_regression_model, data=T01_data)
#prediction.drop(['Y_Quality'], axis = 1, inplace = True)

In [65]:
#T01_datas = T01_prediction['prediction_label']
#T01_datas = pd.DataFrame(T01_datas.values, columns = ['Y_Quality'])
#T01_datas

In [155]:
T01y_idx= T01_class.index
T01y_idx = pd.DataFrame(T01y_idx, columns = ['index'])
T01_datas = pd.concat([T01y_idx, T01_datas], axis = 1)
T01_datas = T01_datas.set_index('index')
T01_datas

Y_Quality
index           
28      0.522792
33      0.527068
39      0.531853
40      0.530675
41      0.528856
...          ...
479     0.534632
501     0.533179
523     0.534454
531     0.558143
585     0.516612

[129 rows x 1 columns]

In [157]:
from pycaret.classification import *
# 분류 패키지의 모든 모듈을 임포트한다.
exp_clf101 = setup(data=T01_datas, 
                   target=T01_class, 
                   fold=5,
                   session_id=414)
top5 = compare_models(sort='Accuracy', n_select=5)

Processing:   0%|          | 0/73 [00:00<?, ?it/s]

In [158]:
T01_total_models = []

T01_model_lightgbm = create_model('lightgbm', fold = 5)
T01_total_models.append(T01_model_lightgbm)

T01_model_rf = create_model('rf', fold = 5)
T01_total_models.append(T01_model_rf)

T01_model_gbc = create_model('gbc', fold = 5)
T01_total_models.append(T01_model_gbc)

T01_model_et = create_model('et', fold = 5)
T01_total_models.append(T01_model_et)

T01_model_catboost = create_model('catboost', fold = 5)
T01_total_models.append(T01_model_catboost)

T01_model_xgb = create_model('xgboost', fold = 5)
T01_total_models.append(T01_model_xgb)

T01_model_ada = create_model('ada', fold = 5)
T01_total_models.append(T01_model_ada)

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

In [159]:
T01_model_lightgbm = tune_model(T01_model_lightgbm, fold=5, choose_better = True)

T01_model_rf = tune_model(T01_model_rf, fold=5, choose_better = True)

T01_model_gbc = tune_model(T01_model_gbc, fold=5, choose_better = True)

T01_model_et = tune_model(T01_model_et, fold=5, choose_better = True)

T01_model_catboost = tune_model(T01_model_catboost, fold=5, choose_better = True)

T01_model_xgb = tune_model(T01_model_xgb, fold=5, choose_better = True)

T01_model_ada = tune_model(T01_model_ada, fold=5, choose_better = True)

Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

...

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


In [160]:
T01_tuned_models = [T01_model_lightgbm, T01_model_rf, T01_model_gbc, T01_model_et, T01_model_catboost, T01_model_xgb, T01_model_ada]
T01_tuned_models

[LGBMClassifier(boosting_type='gbdt', class_weight=None, colsample_bytree=1.0,
                importance_type='split', learning_rate=0.1, max_depth=-1,
                min_child_samples=20, min_child_weight=0.001, min_split_gain=0.0,
                n_estimators=100, n_jobs=-1, num_leaves=31, objective=None,
                random_state=414, reg_alpha=0.0, reg_lambda=0.0, silent=True,
                subsample=1.0, subsample_for_bin=200000, subsample_freq=0),
 RandomForestClassifier(bootstrap=True, ccp_alpha=0.0,
                        class_weight='balanced_subsample', criterion='gini',
                        max_depth=9, max_features='sqrt', max_leaf_nodes=None,
                        max_samples=None, min_impurity_decrease=0.0005,
                        min_samples_leaf=6, min_samples_split=5,
                        min_weight_fraction_leaf=0.0, n_estimators=50, n_jobs=-1,
                        oob_score=False, random_state=414, verbose=0,
                        warm_start=

In [161]:
for model in T01_tuned_models:
    display(predict_model(model))

Y_Quality  Y_Class  prediction_label  prediction_score
90    0.531149        1                 1            0.9973
91    0.518269        0                 0            0.9885
92    0.525803        0                 1            0.6561
93    0.525085        0                 0            0.9885
94    0.527979        1                 1            0.9983
95    0.525577        0                 0            0.9885
96    0.531175        1                 1            0.9973
97    0.558143        2                 2            0.9845
98    0.535697        2                 2            0.9845
99    0.549414        2                 2            0.9845
100   0.529449        1                 1            0.9983
101   0.543397        2                 2            0.9845
102   0.546914        2                 2            0.9845
103   0.528809        1                 1            0.9983
104   0.545529        2                 2            0.9845
105   0.532656        1                 1            0.9935
106   0.532657        1                 1            0.9935
107   0.528473        1                 1            0.9983
108   0.531413        1                 1            0.9973
109   0.518452        0                 0            0.9885
110   0.528856        1                 1            0.9983
111   0.536134        2                 2            0.9845
112   0.530915        1                 1            0.9978
113   0.533964        1                 1            0.9790
114   0.535304        2                 2            0.9845
115   0.537936        2                 2            0.9845
116   0.529954        1                 1            0.9981
117   0.534044        1                 1            0.9790
118   0.528636        1                 1            0.9983
119   0.527457        1                 1            0.9939
120   0.526139        1                 1            0.6561
121   0.528088        1                 1            0.9983
122   0.531852        1                 1            0.9958
123   0.530134        1                 1            0.9981
124   0.528504        1                 1            0.9983
125   0.532805        1                 1            0.9935
126   0.536308        2                 2            0.9845
127   0.522628        0                 0            0.9885
128   0.537989        2                 2            0.9845

Y_Quality  Y_Class  prediction_label  prediction_score
90    0.531149        1                 1            1.0000
91    0.518269        0                 0            0.9951
92    0.525803        0                 0            0.9951
93    0.525085        0                 0            0.9951
94    0.527979        1                 1            1.0000
95    0.525577        0                 0            0.9951
96    0.531175        1                 1            1.0000
97    0.558143        2                 2            0.9989
98    0.535697        2                 2            0.9477
99    0.549414        2                 2            0.9989
100   0.529449        1                 1            1.0000
101   0.543397        2                 2            0.9989
102   0.546914        2                 2            0.9989
103   0.528809        1                 1            1.0000
104   0.545529        2                 2            0.9989
105   0.532656        1                 1            1.0000
106   0.532657        1                 1            1.0000
107   0.528473        1                 1            1.0000
108   0.531413        1                 1            1.0000
109   0.518452        0                 0            0.9951
110   0.528856        1                 1            1.0000
111   0.536134        2                 2            0.9836
112   0.530915        1                 1            1.0000
113   0.533964        1                 1            0.8032
114   0.535304        2                 2            0.9276
115   0.537936        2                 2            0.9989
116   0.529954        1                 1            1.0000
117   0.534044        1                 1            0.8032
118   0.528636        1                 1            1.0000
119   0.527457        1                 1            1.0000
120   0.526139        1                 1            0.5449
121   0.528088        1                 1            1.0000
122   0.531852        1                 1            1.0000
123   0.530134        1                 1            1.0000
124   0.528504        1                 1            1.0000
125   0.532805        1                 1            0.9968
126   0.536308        2                 2            0.9941
127   0.522628        0                 0            0.9951
128   0.537989        2                 2            0.9989

Y_Quality  Y_Class  prediction_label  prediction_score
90    0.531149        1                 1            0.9639
91    0.518269        0                 0            0.9225
92    0.525803        0                 0            0.9225
93    0.525085        0                 0            0.9225
94    0.527979        1                 1            0.9639
95    0.525577        0                 0            0.9225
96    0.531175        1                 1            0.9639
97    0.558143        2                 2            0.9511
98    0.535697        2                 2            0.9497
99    0.549414        2                 2            0.9511
100   0.529449        1                 1            0.9639
101   0.543397        2                 2            0.9511
102   0.546914        2                 2            0.9511
103   0.528809        1                 1            0.9639
104   0.545529        2                 2            0.9511
105   0.532656        1                 1            0.9639
106   0.532657        1                 1            0.9639
107   0.528473        1                 1            0.9639
108   0.531413        1                 1            0.9639
109   0.518452        0                 0            0.9225
110   0.528856        1                 1            0.9639
111   0.536134        2                 2            0.9511
112   0.530915        1                 1            0.9639
113   0.533964        1                 1            0.7262
114   0.535304        2                 2            0.8923
115   0.537936        2                 2            0.9511
116   0.529954        1                 1            0.9639
117   0.534044        1                 1            0.9000
118   0.528636        1                 1            0.9639
119   0.527457        1                 1            0.9639
120   0.526139        1                 1            0.9457
121   0.528088        1                 1            0.9639
122   0.531852        1                 1            0.9639
123   0.530134        1                 1            0.9639
124   0.528504        1                 1            0.9639
125   0.532805        1                 1            0.9639
126   0.536308        2                 2            0.9511
127   0.522628        0                 0            0.9225
128   0.537989        2                 2            0.9511

Y_Quality  Y_Class  prediction_label  prediction_score
90    0.531149        1                 1              1.00
91    0.518269        0                 0              1.00
92    0.525803        0                 0              1.00
93    0.525085        0                 0              1.00
94    0.527979        1                 1              1.00
95    0.525577        0                 0              1.00
96    0.531175        1                 1              1.00
97    0.558143        2                 2              1.00
98    0.535697        2                 2              1.00
99    0.549414        2                 2              1.00
100   0.529449        1                 1              1.00
101   0.543397        2                 2              1.00
102   0.546914        2                 2              1.00
103   0.528809        1                 1              1.00
104   0.545529        2                 2              1.00
105   0.532656        1                 1              1.00
106   0.532657        1                 1              1.00
107   0.528473        1                 1              1.00
108   0.531413        1                 1              1.00
109   0.518452        0                 0              1.00
110   0.528856        1                 1              1.00
111   0.536134        2                 2              1.00
112   0.530915        1                 1              1.00
113   0.533964        1                 1              1.00
114   0.535304        2                 2              1.00
115   0.537936        2                 2              1.00
116   0.529954        1                 1              1.00
117   0.534044        1                 1              1.00
118   0.528636        1                 1              1.00
119   0.527457        1                 1              1.00
120   0.526139        1                 1              0.65
121   0.528088        1                 1              1.00
122   0.531852        1                 1              1.00
123   0.530134        1                 1              1.00
124   0.528504        1                 1              1.00
125   0.532805        1                 1              1.00
126   0.536308        2                 2              1.00
127   0.522628        0                 0              1.00
128   0.537989        2                 2              1.00

Y_Quality  Y_Class  prediction_label  prediction_score
90    0.531149        1                 1            0.8173
91    0.518269        0                 0            0.7118
92    0.525803        0                 0            0.6979
93    0.525085        0                 0            0.7156
94    0.527979        1                 1            0.8249
95    0.525577        0                 0            0.7156
96    0.531175        1                 1            0.8173
97    0.558143        2                 2            0.7860
98    0.535697        2                 2            0.8108
99    0.549414        2                 2            0.8156
100   0.529449        1                 1            0.8245
101   0.543397        2                 2            0.8147
102   0.546914        2                 2            0.8147
103   0.528809        1                 1            0.8245
104   0.545529        2                 2            0.8147
105   0.532656        1                 1            0.8025
106   0.532657        1                 1            0.8025
107   0.528473        1                 1            0.8249
108   0.531413        1                 1            0.7858
109   0.518452        0                 0            0.7118
110   0.528856        1                 1            0.8245
111   0.536134        2                 2            0.8108
112   0.530915        1                 1            0.8232
113   0.533964        1                 1            0.7427
114   0.535304        2                 2            0.7758
115   0.537936        2                 2            0.8196
116   0.529954        1                 1            0.8285
117   0.534044        1                 1            0.7438
118   0.528636        1                 1            0.8245
119   0.527457        1                 1            0.8244
120   0.526139        1                 1            0.8014
121   0.528088        1                 1            0.8249
122   0.531852        1                 1            0.7974
123   0.530134        1                 1            0.8285
124   0.528504        1                 1            0.8249
125   0.532805        1                 1            0.7980
126   0.536308        2                 2            0.8108
127   0.522628        0                 0            0.7156
128   0.537989        2                 2            0.8196

Y_Quality  Y_Class  prediction_label  prediction_score
90    0.531149        1                 1            0.5164
91    0.518269        0                 0            0.4398
92    0.525803        0                 0            0.4008
93    0.525085        0                 0            0.4183
94    0.527979        1                 1            0.4912
95    0.525577        0                 0            0.4133
96    0.531175        1                 1            0.5164
97    0.558143        2                 2            0.5095
98    0.535697        2                 2            0.4935
99    0.549414        2                 2            0.5095
100   0.529449        1                 1            0.5102
101   0.543397        2                 2            0.5070
102   0.546914        2                 2            0.5095
103   0.528809        1                 1            0.5050
104   0.545529        2                 2            0.5095
105   0.532656        1                 1            0.5121
106   0.532657        1                 1            0.5121
107   0.528473        1                 1            0.4961
108   0.531413        1                 1            0.5164
109   0.518452        0                 0            0.4398
110   0.528856        1                 1            0.5050
111   0.536134        2                 2            0.4988
112   0.530915        1                 1            0.5164
113   0.533964        1                 1            0.4666
114   0.535304        2                 2            0.4618
115   0.537936        2                 2            0.5032
116   0.529954        1                 1            0.5137
117   0.534044        1                 1            0.4627
118   0.528636        1                 1            0.5007
119   0.527457        1                 1            0.4701
120   0.526139        1                 0            0.3771
121   0.528088        1                 1            0.4912
122   0.531852        1                 1            0.5164
123   0.530134        1                 1            0.5137
124   0.528504        1                 1            0.4984
125   0.532805        1                 1            0.5121
126   0.536308        2                 2            0.4993
127   0.522628        0                 0            0.4373
128   0.537989        2                 2            0.5032

Y_Quality  Y_Class  prediction_label  prediction_score
90    0.531149        1                 1            0.3962
91    0.518269        0                 0            0.3870
92    0.525803        0                 0            0.3870
93    0.525085        0                 0            0.3870
94    0.527979        1                 1            0.3962
95    0.525577        0                 0            0.3870
96    0.531175        1                 1            0.3962
97    0.558143        2                 2            0.3873
98    0.535697        2                 2            0.3873
99    0.549414        2                 2            0.3873
100   0.529449        1                 1            0.3962
101   0.543397        2                 2            0.3873
102   0.546914        2                 2            0.3873
103   0.528809        1                 1            0.3962
104   0.545529        2                 2            0.3873
105   0.532656        1                 1            0.3962
106   0.532657        1                 1            0.3962
107   0.528473        1                 1            0.3962
108   0.531413        1                 1            0.3962
109   0.518452        0                 0            0.3870
110   0.528856        1                 1            0.3962
111   0.536134        2                 2            0.3873
112   0.530915        1                 1            0.3962
113   0.533964        1                 1            0.3727
114   0.535304        2                 2            0.3873
115   0.537936        2                 2            0.3873
116   0.529954        1                 1            0.3962
117   0.534044        1                 1            0.3727
118   0.528636        1                 1            0.3962
119   0.527457        1                 1            0.3962
120   0.526139        1                 1            0.3962
121   0.528088        1                 1            0.3962
122   0.531852        1                 1            0.3962
123   0.530134        1                 1            0.3962
124   0.528504        1                 1            0.3962
125   0.532805        1                 1            0.3962
126   0.536308        2                 2            0.3873
127   0.522628        0                 0            0.3870
128   0.537989        2                 2            0.3873

In [163]:
T01_classifier_models = [
    ('ada',  T01_model_ada),
    ('lightgbm', T01_model_lightgbm),
    ('rf', T01_model_rf),
    ('gbc', T01_model_gbc),
    ('et', T01_model_et),
    ('cat', T01_model_catboost),
    ('xgb', T01_model_xgb),
]

In [164]:
T01_soft_vote = VotingClassifier(T01_classifier_models, voting = 'soft')
#soft_vote_cv = cross_validate(soft_vote, T01_datas, T01_class, cv = KFold)
T01_soft_vote.fit(T01_datas, T01_class)

VotingClassifier(estimators=[('ada',
                              AdaBoostClassifier(algorithm='SAMME',
                                                 base_estimator=None,
                                                 learning_rate=0.05,
                                                 n_estimators=190,
                                                 random_state=414)),
                             ('lightgbm',
                              LGBMClassifier(boosting_type='gbdt',
                                             class_weight=None,
                                             colsample_bytree=1.0,
                                             importance_type='split',
                                             learning_rate=0.1, max_depth=-1,
                                             min_child_samples=20,
                                             min_child_weight=0.001,
                                             min_split_gain=0...
                               

In [282]:
T01_class = pd.DataFrame(T01_class, columns = ['Y_Class'])

In [281]:
T01_datas = T01_datas['Y_Quality']

In [125]:
T01_final_classification_model = finalize_model(T01_model_et)

In [126]:
T01_prediction = predict_model(T01_final_classification_model, data=T01_datas)
#prediction.drop(['Y_Quality'], axis = 1, inplace = True)

In [165]:
T01_prediction = pd.DataFrame(T01_soft_vote.predict(T01_datas), columns = ['prediction_label'])
T01_prediction

prediction_label
0                   0
1                   1
2                   1
3                   1
4                   1
..                ...
124                 1
125                 1
126                 1
127                 2
128                 0

[129 rows x 1 columns]

In [166]:
T01_y_class = pd.DataFrame(T01_class, columns = ['Y_Class'])
T01_idx = T01_y_class.index
T01_y_class = T01_y_class.reset_index()
T01_prediction = pd.concat([T01_prediction, T01_y_class], axis = 1)
T01_prediction = T01_prediction.set_index('index')
T01_prediction.drop(['Y_Class'], axis = 1, inplace = True)

In [167]:
T01_prediction

prediction_label
index                  
28                    0
33                    1
39                    1
40                    1
41                    1
...                 ...
479                   1
501                   1
523                   1
531                   2
585                   0

[129 rows x 1 columns]

# T10

In [225]:
T10_class = T10['Y_Class']
T10_target = T10['Y_Quality']
T10_data = T10.drop(['Y_Class', 'Y_Quality'], axis = 1)
T10_data

X_1    X_2  X_3   X_4   X_5  X_6   X_7   X_8   X_9  X_10  ...  X_928  \
22    2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0   2.0  ...  326.0   
23    2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0   2.0  ...    0.0   
25    2.0   97.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0   2.0  ...  327.0   
29    2.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0   2.0  ...  327.0   
37    2.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0   2.0  ...  327.0   
..    ...    ...  ...   ...   ...  ...   ...   ...   ...   ...  ...    ...   
589   1.0   94.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0   2.0  ...  326.0   
590   1.0   89.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0   2.0  ...  327.0   
591   1.0   87.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0   2.0  ...  326.0   
593   2.0   95.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0   2.0  ...  327.0   
597  21.0   87.0  0.0  45.0  10.0  0.0  61.0  10.0  52.0   2.0  ...  326.0   

          X_929  X_930  X_931      X_932  X_933  HOUR  MINUTE  DAY_OF_WEEK  \
22   309.290909  290.0   13.7  13.443333   13.2     8      53            2   
23     0.000000    0.0    0.0   0.000000    0.0     9       1            2   
25   310.854546  298.0   13.7  13.454839   13.2     9      11            7   
29   312.109091  298.0   13.7  13.422581   13.2    23      31            7   
37   312.254546  298.0   13.7  13.456667   13.3     3      47            3   
..          ...    ...    ...        ...    ...   ...     ...          ...   
589  311.272727  298.0   13.7  13.483871   13.3    18       0            2   
590  313.400000  299.0   13.6  13.393548   13.2     1       1            3   
591  313.472727  298.0   13.6  13.400000   13.2     1       9            3   
593  313.363636  298.0   13.6  13.351613   13.2    14      30            4   
597  304.818182  289.0   13.6  13.380000   13.2    14      46            4   

     LINE_AND_CODE  
22            10.0  
23            10.0  
25            10.0  
29            10.0  
37            10.0  
..             ...  
589           11.0  
590           11.0  
591           11.0  
593           11.0  
597           17.0  

[349 rows x 669 columns]

In [169]:
T_10c = T10_data.columns
T_10scaler = RobustScaler()
T_10scaled = T_10scaler.fit_transform(T10_data)
T10_data = pd.DataFrame(T_10scaled, columns = T_10c)
T10_data

X_1  X_2  X_3  X_4  X_5  X_6       X_7  X_8  X_9  X_10  ...  X_928  \
0     0.0  1.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...    0.0   
1     0.0  1.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...  -32.6   
2     0.0  0.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...    0.1   
3     0.0  1.0  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...    0.1   
4     0.0  1.0  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...    0.1   
..    ...  ...  ...  ...  ...  ...       ...  ...  ...   ...  ...    ...   
344  -1.0 -0.2  0.0  0.0  0.0  0.0  0.833333  0.0  1.0   0.0  ...    0.0   
345  -1.0 -1.2  0.0  0.0  0.0  0.0  0.833333  0.0  1.0   0.0  ...    0.1   
346  -1.0 -1.6  0.0  0.0  0.0  0.0  0.833333  0.0  1.0   0.0  ...    0.0   
347   0.0  0.0  0.0  0.0  0.0  0.0  0.833333  0.0  1.0   0.0  ...    0.1   
348  19.0 -1.6  0.0  0.0  0.0  0.0  2.666667  0.0  1.0   0.0  ...    0.0   

         X_929      X_930  X_931       X_932  X_933      HOUR    MINUTE  \
0     0.386364   0.111111    1.0    0.584058    0.0 -0.166667  0.793103   
1   -38.275000 -32.111111 -136.0 -180.608692  -13.2 -0.083333 -1.000000   
2     0.581818   1.000000    1.0    0.739130    0.0 -0.083333 -0.655172   
3     0.738636   1.000000    1.0    0.304348    0.0  1.083333  0.034483   
4     0.756818   1.000000    1.0    0.763768    0.1 -0.583333  0.586207   
..         ...        ...    ...         ...    ...       ...       ...   
344   0.634091   1.000000    1.0    1.130435    0.1  0.666667 -1.034483   
345   0.900000   1.111111    0.0   -0.086956    0.0 -0.750000 -1.000000   
346   0.909091   1.000000    0.0    0.000000    0.0 -0.750000 -0.724138   
347   0.895455   1.000000    0.0   -0.652174    0.0  0.333333  0.000000   
348  -0.172727   0.000000    0.0   -0.269565    0.0  0.333333  0.551724   

     DAY_OF_WEEK  LINE_AND_CODE  
0      -1.000000           -1.0  
1      -1.000000           -1.0  
2       0.666667           -1.0  
3       0.666667           -1.0  
4      -0.666667           -1.0  
..           ...            ...  
344    -1.000000            0.0  
345    -0.666667            0.0  
346    -0.666667            0.0  
347    -0.333333            0.0  
348    -0.333333            6.0  

[349 rows x 669 columns]

In [170]:
T10_y_class = pd.DataFrame(T10_target, columns = ['Y_Quality'])
T10_idx = T10_y_class.index
T10_y_class = T10_y_class.reset_index()
T10_data = pd.concat([T10_data, T10_y_class], axis = 1)
T10_data = T10_data.set_index('index')
T10_data.drop(['Y_Quality'], axis = 1, inplace = True)
T10_data

X_1  X_2  X_3  X_4  X_5  X_6       X_7  X_8  X_9  X_10  ...  X_928  \
index                                                           ...          
22      0.0  1.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...    0.0   
23      0.0  1.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...  -32.6   
25      0.0  0.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...    0.1   
29      0.0  1.0  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...    0.1   
37      0.0  1.0  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...    0.1   
...     ...  ...  ...  ...  ...  ...       ...  ...  ...   ...  ...    ...   
589    -1.0 -0.2  0.0  0.0  0.0  0.0  0.833333  0.0  1.0   0.0  ...    0.0   
590    -1.0 -1.2  0.0  0.0  0.0  0.0  0.833333  0.0  1.0   0.0  ...    0.1   
591    -1.0 -1.6  0.0  0.0  0.0  0.0  0.833333  0.0  1.0   0.0  ...    0.0   
593     0.0  0.0  0.0  0.0  0.0  0.0  0.833333  0.0  1.0   0.0  ...    0.1   
597    19.0 -1.6  0.0  0.0  0.0  0.0  2.666667  0.0  1.0   0.0  ...    0.0   

           X_929      X_930  X_931       X_932  X_933      HOUR    MINUTE  \
index                                                                       
22      0.386364   0.111111    1.0    0.584058    0.0 -0.166667  0.793103   
23    -38.275000 -32.111111 -136.0 -180.608692  -13.2 -0.083333 -1.000000   
25      0.581818   1.000000    1.0    0.739130    0.0 -0.083333 -0.655172   
29      0.738636   1.000000    1.0    0.304348    0.0  1.083333  0.034483   
37      0.756818   1.000000    1.0    0.763768    0.1 -0.583333  0.586207   
...          ...        ...    ...         ...    ...       ...       ...   
589     0.634091   1.000000    1.0    1.130435    0.1  0.666667 -1.034483   
590     0.900000   1.111111    0.0   -0.086956    0.0 -0.750000 -1.000000   
591     0.909091   1.000000    0.0    0.000000    0.0 -0.750000 -0.724138   
593     0.895455   1.000000    0.0   -0.652174    0.0  0.333333  0.000000   
597    -0.172727   0.000000    0.0   -0.269565    0.0  0.333333  0.551724   

       DAY_OF_WEEK  LINE_AND_CODE  
index                              
22       -1.000000           -1.0  
23       -1.000000           -1.0  
25        0.666667           -1.0  
29        0.666667           -1.0  
37       -0.666667           -1.0  
...            ...            ...  
589      -1.000000            0.0  
590      -0.666667            0.0  
591      -0.666667            0.0  
593      -0.333333            0.0  
597      -0.333333            6.0  

[349 rows x 669 columns]

In [171]:
#13
from pycaret.regression import *
setup_rgs = setup(data = T10_data, target = T10_target, session_id = 414)
top5 = compare_models(sort='MSE', n_select=5)

Processing:   0%|          | 0/89 [00:00<?, ?it/s]

In [172]:
T10_total_models = []

T10_model_rf = create_model('rf', fold = 5)
T10_total_models.append(T10_model_rf)

T10_model_gbr = create_model('gbr', fold = 5)
T10_total_models.append(T10_model_gbr)

T10_model_et = create_model('et', fold = 5)
T10_total_models.append(T10_model_et)

T10_model_catboost = create_model('catboost', fold = 5)
T10_total_models.append(T10_model_catboost)

T10_model_xgb = create_model('xgboost', fold = 5)
T10_total_models.append(T10_model_xgb)

T10_model_ada = create_model('ada', fold = 5)
T10_total_models.append(T10_model_ada)

T10_model_lightgbm = create_model('lightgbm', fold = 5)
T10_total_models.append(T10_model_lightgbm)

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

In [173]:
T10_model_rf = tune_model(T10_model_rf, fold=5, choose_better = True)

T10_model_gbr = tune_model(T10_model_gbr, fold=5, choose_better = True)

T10_model_et = tune_model(T10_model_et, fold=5, choose_better = True)

T10_model_catboost = tune_model(T10_model_catboost, fold=5, choose_better = True)

T10_model_xgb = tune_model(T10_model_xgb, fold=5, choose_better = True)

T10_model_ada = tune_model(T10_model_ada, fold=5, choose_better = True)

T10_model_lightgbm = tune_model(T10_model_lightgbm, fold=5, choose_better = True)

Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

...

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


In [174]:
T10_tuned_models = [T10_model_rf, T10_model_gbr, T10_model_et, T10_model_catboost, T10_model_xgb, T10_model_ada, T10_model_lightgbm]
T10_tuned_models

[RandomForestRegressor(bootstrap=False, ccp_alpha=0.0,
                       criterion='absolute_error', max_depth=2,
                       max_features='log2', max_leaf_nodes=None,
                       max_samples=None, min_impurity_decrease=0,
                       min_samples_leaf=6, min_samples_split=9,
                       min_weight_fraction_leaf=0.0, n_estimators=160, n_jobs=-1,
                       oob_score=False, random_state=414, verbose=0,
                       warm_start=False),
 GradientBoostingRegressor(alpha=0.9, ccp_alpha=0.0, criterion='friedman_mse',
                           init=None, learning_rate=0.1, loss='squared_error',
                           max_depth=3, max_features=None, max_leaf_nodes=None,
                           min_impurity_decrease=0.0, min_samples_leaf=1,
                           min_samples_split=2, min_weight_fraction_leaf=0.0,
                           n_estimators=100, n_iter_no_change=None,
                           random_s

In [175]:
for model in T10_tuned_models:
    display(predict_model(model))

X_1  X_2  X_3  X_4  X_5  X_6       X_7  X_8  X_9  X_10  ...     X_930  \
244  0.0 -0.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ... -0.111111   
245  0.0 -0.2  0.0  0.0  0.0  0.0  1.500000  0.0  1.0   0.0  ...  1.000000   
246  0.0  1.2  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...  0.000000   
247  0.0  1.0  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...  0.222222   
248  0.0  0.8  0.0  0.0  0.0  0.0  0.000000  0.0  0.0   0.0  ...  1.000000   
..   ...  ...  ...  ...  ...  ...       ...  ...  ...   ...  ...       ...   
344  0.0  0.8  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...  1.111111   
345  0.0 -0.4  0.0  0.0  0.0  0.0  1.000000  0.0  1.0   0.0  ... -1.000000   
346  0.0 -0.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...  0.000000   
347  0.0  1.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ... -0.111111   
348  0.0  0.0  0.0  0.0  0.0  0.0  0.833333  0.0  1.0   0.0  ...  1.000000   

     X_931     X_932  X_933      HOUR    MINUTE  DAY_OF_WEEK  LINE_AND_CODE  \
244    0.0 -0.739130   -0.1  0.666667 -0.172414     0.000000           -1.0   
245    0.0 -0.434783    0.0  0.333333 -0.517241    -1.000000            0.0   
246    1.0  1.437681    0.1  0.000000  0.758621    -0.666667           -1.0   
247    1.0  0.304348    0.1 -0.666667  0.379310     0.333333           -1.0   
248    0.0 -0.134783    0.0  0.166667  0.068966     0.000000           -1.0   
..     ...       ...    ...       ...       ...          ...            ...   
344    1.0  0.739130    0.0 -0.166667  0.827586    -0.666667           -1.0   
345    1.0  0.089855    0.0  0.833333  0.724138     0.666667            0.0   
346    0.0 -0.134783    0.0  0.166667  0.689655     0.333333           -1.0   
347    0.0 -0.608696    0.0 -0.166667 -0.103448     0.666667           -1.0   
348    0.0 -0.304348    0.0  0.916667  0.379310    -1.333333            0.0   

     Y_Quality  prediction_label  
244   0.531825          0.530258  
245   0.530560          0.530522  
246   0.532981          0.530505  
247   0.530986          0.530670  
248   0.545678          0.530800  
..         ...               ...  
344   0.526413          0.530455  
345   0.531676          0.530213  
346   0.529456          0.530761  
347   0.528094          0.530142  
348   0.531684          0.530616  

[105 rows x 671 columns]

X_1  X_2  X_3  X_4  X_5  X_6       X_7  X_8  X_9  X_10  ...     X_930  \
244  0.0 -0.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ... -0.111111   
245  0.0 -0.2  0.0  0.0  0.0  0.0  1.500000  0.0  1.0   0.0  ...  1.000000   
246  0.0  1.2  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...  0.000000   
247  0.0  1.0  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...  0.222222   
248  0.0  0.8  0.0  0.0  0.0  0.0  0.000000  0.0  0.0   0.0  ...  1.000000   
..   ...  ...  ...  ...  ...  ...       ...  ...  ...   ...  ...       ...   
344  0.0  0.8  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...  1.111111   
345  0.0 -0.4  0.0  0.0  0.0  0.0  1.000000  0.0  1.0   0.0  ... -1.000000   
346  0.0 -0.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...  0.000000   
347  0.0  1.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ... -0.111111   
348  0.0  0.0  0.0  0.0  0.0  0.0  0.833333  0.0  1.0   0.0  ...  1.000000   

     X_931     X_932  X_933      HOUR    MINUTE  DAY_OF_WEEK  LINE_AND_CODE  \
244    0.0 -0.739130   -0.1  0.666667 -0.172414     0.000000           -1.0   
245    0.0 -0.434783    0.0  0.333333 -0.517241    -1.000000            0.0   
246    1.0  1.437681    0.1  0.000000  0.758621    -0.666667           -1.0   
247    1.0  0.304348    0.1 -0.666667  0.379310     0.333333           -1.0   
248    0.0 -0.134783    0.0  0.166667  0.068966     0.000000           -1.0   
..     ...       ...    ...       ...       ...          ...            ...   
344    1.0  0.739130    0.0 -0.166667  0.827586    -0.666667           -1.0   
345    1.0  0.089855    0.0  0.833333  0.724138     0.666667            0.0   
346    0.0 -0.134783    0.0  0.166667  0.689655     0.333333           -1.0   
347    0.0 -0.608696    0.0 -0.166667 -0.103448     0.666667           -1.0   
348    0.0 -0.304348    0.0  0.916667  0.379310    -1.333333            0.0   

     Y_Quality  prediction_label  
244   0.531825          0.529767  
245   0.530560          0.533748  
246   0.532981          0.529958  
247   0.530986          0.529814  
248   0.545678          0.543592  
..         ...               ...  
344   0.526413          0.530341  
345   0.531676          0.529398  
346   0.529456          0.530344  
347   0.528094          0.529892  
348   0.531684          0.530338  

[105 rows x 671 columns]

X_1  X_2  X_3  X_4  X_5  X_6       X_7  X_8  X_9  X_10  ...     X_930  \
244  0.0 -0.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ... -0.111111   
245  0.0 -0.2  0.0  0.0  0.0  0.0  1.500000  0.0  1.0   0.0  ...  1.000000   
246  0.0  1.2  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...  0.000000   
247  0.0  1.0  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...  0.222222   
248  0.0  0.8  0.0  0.0  0.0  0.0  0.000000  0.0  0.0   0.0  ...  1.000000   
..   ...  ...  ...  ...  ...  ...       ...  ...  ...   ...  ...       ...   
344  0.0  0.8  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...  1.111111   
345  0.0 -0.4  0.0  0.0  0.0  0.0  1.000000  0.0  1.0   0.0  ... -1.000000   
346  0.0 -0.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...  0.000000   
347  0.0  1.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ... -0.111111   
348  0.0  0.0  0.0  0.0  0.0  0.0  0.833333  0.0  1.0   0.0  ...  1.000000   

     X_931     X_932  X_933      HOUR    MINUTE  DAY_OF_WEEK  LINE_AND_CODE  \
244    0.0 -0.739130   -0.1  0.666667 -0.172414     0.000000           -1.0   
245    0.0 -0.434783    0.0  0.333333 -0.517241    -1.000000            0.0   
246    1.0  1.437681    0.1  0.000000  0.758621    -0.666667           -1.0   
247    1.0  0.304348    0.1 -0.666667  0.379310     0.333333           -1.0   
248    0.0 -0.134783    0.0  0.166667  0.068966     0.000000           -1.0   
..     ...       ...    ...       ...       ...          ...            ...   
344    1.0  0.739130    0.0 -0.166667  0.827586    -0.666667           -1.0   
345    1.0  0.089855    0.0  0.833333  0.724138     0.666667            0.0   
346    0.0 -0.134783    0.0  0.166667  0.689655     0.333333           -1.0   
347    0.0 -0.608696    0.0 -0.166667 -0.103448     0.666667           -1.0   
348    0.0 -0.304348    0.0  0.916667  0.379310    -1.333333            0.0   

     Y_Quality  prediction_label  
244   0.531825          0.531514  
245   0.530560          0.531152  
246   0.532981          0.529418  
247   0.530986          0.530596  
248   0.545678          0.545946  
..         ...               ...  
344   0.526413          0.529920  
345   0.531676          0.529352  
346   0.529456          0.530292  
347   0.528094          0.529778  
348   0.531684          0.529866  

[105 rows x 671 columns]

X_1  X_2  X_3  X_4  X_5  X_6       X_7  X_8  X_9  X_10  ...     X_930  \
244  0.0 -0.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ... -0.111111   
245  0.0 -0.2  0.0  0.0  0.0  0.0  1.500000  0.0  1.0   0.0  ...  1.000000   
246  0.0  1.2  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...  0.000000   
247  0.0  1.0  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...  0.222222   
248  0.0  0.8  0.0  0.0  0.0  0.0  0.000000  0.0  0.0   0.0  ...  1.000000   
..   ...  ...  ...  ...  ...  ...       ...  ...  ...   ...  ...       ...   
344  0.0  0.8  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...  1.111111   
345  0.0 -0.4  0.0  0.0  0.0  0.0  1.000000  0.0  1.0   0.0  ... -1.000000   
346  0.0 -0.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...  0.000000   
347  0.0  1.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ... -0.111111   
348  0.0  0.0  0.0  0.0  0.0  0.0  0.833333  0.0  1.0   0.0  ...  1.000000   

     X_931     X_932  X_933      HOUR    MINUTE  DAY_OF_WEEK  LINE_AND_CODE  \
244    0.0 -0.739130   -0.1  0.666667 -0.172414     0.000000           -1.0   
245    0.0 -0.434783    0.0  0.333333 -0.517241    -1.000000            0.0   
246    1.0  1.437681    0.1  0.000000  0.758621    -0.666667           -1.0   
247    1.0  0.304348    0.1 -0.666667  0.379310     0.333333           -1.0   
248    0.0 -0.134783    0.0  0.166667  0.068966     0.000000           -1.0   
..     ...       ...    ...       ...       ...          ...            ...   
344    1.0  0.739130    0.0 -0.166667  0.827586    -0.666667           -1.0   
345    1.0  0.089855    0.0  0.833333  0.724138     0.666667            0.0   
346    0.0 -0.134783    0.0  0.166667  0.689655     0.333333           -1.0   
347    0.0 -0.608696    0.0 -0.166667 -0.103448     0.666667           -1.0   
348    0.0 -0.304348    0.0  0.916667  0.379310    -1.333333            0.0   

     Y_Quality  prediction_label  
244   0.531825          0.530498  
245   0.530560          0.530523  
246   0.532981          0.530197  
247   0.530986          0.530731  
248   0.545678          0.540110  
..         ...               ...  
344   0.526413          0.530259  
345   0.531676          0.530296  
346   0.529456          0.530668  
347   0.528094          0.530597  
348   0.531684          0.530543  

[105 rows x 671 columns]

X_1  X_2  X_3  X_4  X_5  X_6       X_7  X_8  X_9  X_10  ...     X_930  \
244  0.0 -0.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ... -0.111111   
245  0.0 -0.2  0.0  0.0  0.0  0.0  1.500000  0.0  1.0   0.0  ...  1.000000   
246  0.0  1.2  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...  0.000000   
247  0.0  1.0  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...  0.222222   
248  0.0  0.8  0.0  0.0  0.0  0.0  0.000000  0.0  0.0   0.0  ...  1.000000   
..   ...  ...  ...  ...  ...  ...       ...  ...  ...   ...  ...       ...   
344  0.0  0.8  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...  1.111111   
345  0.0 -0.4  0.0  0.0  0.0  0.0  1.000000  0.0  1.0   0.0  ... -1.000000   
346  0.0 -0.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...  0.000000   
347  0.0  1.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ... -0.111111   
348  0.0  0.0  0.0  0.0  0.0  0.0  0.833333  0.0  1.0   0.0  ...  1.000000   

     X_931     X_932  X_933      HOUR    MINUTE  DAY_OF_WEEK  LINE_AND_CODE  \
244    0.0 -0.739130   -0.1  0.666667 -0.172414     0.000000           -1.0   
245    0.0 -0.434783    0.0  0.333333 -0.517241    -1.000000            0.0   
246    1.0  1.437681    0.1  0.000000  0.758621    -0.666667           -1.0   
247    1.0  0.304348    0.1 -0.666667  0.379310     0.333333           -1.0   
248    0.0 -0.134783    0.0  0.166667  0.068966     0.000000           -1.0   
..     ...       ...    ...       ...       ...          ...            ...   
344    1.0  0.739130    0.0 -0.166667  0.827586    -0.666667           -1.0   
345    1.0  0.089855    0.0  0.833333  0.724138     0.666667            0.0   
346    0.0 -0.134783    0.0  0.166667  0.689655     0.333333           -1.0   
347    0.0 -0.608696    0.0 -0.166667 -0.103448     0.666667           -1.0   
348    0.0 -0.304348    0.0  0.916667  0.379310    -1.333333            0.0   

     Y_Quality  prediction_label  
244   0.531825          0.526468  
245   0.530560          0.531674  
246   0.532981          0.530081  
247   0.530986          0.533036  
248   0.545678          0.542315  
..         ...               ...  
344   0.526413          0.530968  
345   0.531676          0.530831  
346   0.529456          0.532183  
347   0.528094          0.525054  
348   0.531684          0.532458  

[105 rows x 671 columns]

X_1  X_2  X_3  X_4  X_5  X_6       X_7  X_8  X_9  X_10  ...     X_930  \
244  0.0 -0.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ... -0.111111   
245  0.0 -0.2  0.0  0.0  0.0  0.0  1.500000  0.0  1.0   0.0  ...  1.000000   
246  0.0  1.2  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...  0.000000   
247  0.0  1.0  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...  0.222222   
248  0.0  0.8  0.0  0.0  0.0  0.0  0.000000  0.0  0.0   0.0  ...  1.000000   
..   ...  ...  ...  ...  ...  ...       ...  ...  ...   ...  ...       ...   
344  0.0  0.8  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...  1.111111   
345  0.0 -0.4  0.0  0.0  0.0  0.0  1.000000  0.0  1.0   0.0  ... -1.000000   
346  0.0 -0.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...  0.000000   
347  0.0  1.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ... -0.111111   
348  0.0  0.0  0.0  0.0  0.0  0.0  0.833333  0.0  1.0   0.0  ...  1.000000   

     X_931     X_932  X_933      HOUR    MINUTE  DAY_OF_WEEK  LINE_AND_CODE  \
244    0.0 -0.739130   -0.1  0.666667 -0.172414     0.000000           -1.0   
245    0.0 -0.434783    0.0  0.333333 -0.517241    -1.000000            0.0   
246    1.0  1.437681    0.1  0.000000  0.758621    -0.666667           -1.0   
247    1.0  0.304348    0.1 -0.666667  0.379310     0.333333           -1.0   
248    0.0 -0.134783    0.0  0.166667  0.068966     0.000000           -1.0   
..     ...       ...    ...       ...       ...          ...            ...   
344    1.0  0.739130    0.0 -0.166667  0.827586    -0.666667           -1.0   
345    1.0  0.089855    0.0  0.833333  0.724138     0.666667            0.0   
346    0.0 -0.134783    0.0  0.166667  0.689655     0.333333           -1.0   
347    0.0 -0.608696    0.0 -0.166667 -0.103448     0.666667           -1.0   
348    0.0 -0.304348    0.0  0.916667  0.379310    -1.333333            0.0   

     Y_Quality  prediction_label  
244   0.531825          0.530455  
245   0.530560          0.530554  
246   0.532981          0.530489  
247   0.530986          0.530508  
248   0.545678          0.547267  
..         ...               ...  
344   0.526413          0.530511  
345   0.531676          0.530523  
346   0.529456          0.530519  
347   0.528094          0.530534  
348   0.531684          0.530478  

[105 rows x 671 columns]

X_1  X_2  X_3  X_4  X_5  X_6       X_7  X_8  X_9  X_10  ...     X_930  \
244  0.0 -0.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ... -0.111111   
245  0.0 -0.2  0.0  0.0  0.0  0.0  1.500000  0.0  1.0   0.0  ...  1.000000   
246  0.0  1.2  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...  0.000000   
247  0.0  1.0  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...  0.222222   
248  0.0  0.8  0.0  0.0  0.0  0.0  0.000000  0.0  0.0   0.0  ...  1.000000   
..   ...  ...  ...  ...  ...  ...       ...  ...  ...   ...  ...       ...   
344  0.0  0.8  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...  1.111111   
345  0.0 -0.4  0.0  0.0  0.0  0.0  1.000000  0.0  1.0   0.0  ... -1.000000   
346  0.0 -0.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...  0.000000   
347  0.0  1.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ... -0.111111   
348  0.0  0.0  0.0  0.0  0.0  0.0  0.833333  0.0  1.0   0.0  ...  1.000000   

     X_931     X_932  X_933      HOUR    MINUTE  DAY_OF_WEEK  LINE_AND_CODE  \
244    0.0 -0.739130   -0.1  0.666667 -0.172414     0.000000           -1.0   
245    0.0 -0.434783    0.0  0.333333 -0.517241    -1.000000            0.0   
246    1.0  1.437681    0.1  0.000000  0.758621    -0.666667           -1.0   
247    1.0  0.304348    0.1 -0.666667  0.379310     0.333333           -1.0   
248    0.0 -0.134783    0.0  0.166667  0.068966     0.000000           -1.0   
..     ...       ...    ...       ...       ...          ...            ...   
344    1.0  0.739130    0.0 -0.166667  0.827586    -0.666667           -1.0   
345    1.0  0.089855    0.0  0.833333  0.724138     0.666667            0.0   
346    0.0 -0.134783    0.0  0.166667  0.689655     0.333333           -1.0   
347    0.0 -0.608696    0.0 -0.166667 -0.103448     0.666667           -1.0   
348    0.0 -0.304348    0.0  0.916667  0.379310    -1.333333            0.0   

     Y_Quality  prediction_label  
244   0.531825          0.530411  
245   0.530560          0.530411  
246   0.532981          0.530411  
247   0.530986          0.530411  
248   0.545678          0.530411  
..         ...               ...  
344   0.526413          0.530411  
345   0.531676          0.530411  
346   0.529456          0.530411  
347   0.528094          0.530411  
348   0.531684          0.530411  

[105 rows x 671 columns]

In [176]:
T10_vote_regressor_models = [
    ('ada',  T10_model_ada),
    ('lightgbm', T10_model_lightgbm),
    ('rf', T10_model_rf),
    ('gbc', T10_model_gbr),
    ('et', T10_model_et),
    ('cat', T10_model_catboost),
    ('xgb', T10_model_xgb),
]

In [177]:
T10_vote_regressor = VotingRegressor(estimators = T10_vote_regressor_models)
#soft_vote_cv = cross_validate(soft_vote, T01_datas, T01_class, cv = KFold)
#soft_vote.fit(T05_datas, T05_class)

In [178]:
T10_vote_regressor.fit(T10_data, T10_target)
T10_pred = T10_vote_regressor.predict(T10_data)

[LightGBM] [Warning] feature_fraction is set=0.7, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.7
[LightGBM] [Warning] bagging_fraction is set=0.8, subsample=1.0 will be ignored. Current value: bagging_fraction=0.8
[LightGBM] [Warning] bagging_freq is set=2, subsample_freq=0 will be ignored. Current value: bagging_freq=2


In [179]:
T10_datas = pd.DataFrame(T10_pred, columns = ['Y_Quality'])
T10_datas

Y_Quality
0     0.522109
1     0.522585
2     0.530021
3     0.531225
4     0.531454
..         ...
344   0.530116
345   0.530183
346   0.529922
347   0.528703
348   0.531797

[349 rows x 1 columns]

In [138]:
T10_final_regression_model = finalize_model(T10_model_et)

In [139]:
T10_prediction = predict_model(T10_final_regression_model, data=T10_data)
#prediction.drop(['Y_Quality'], axis = 1, inplace = True)

In [140]:
T10_datas = T10_prediction['prediction_label']
T10_datas = pd.DataFrame(T10_datas.values, columns = ['Y_Quality'])
T10_datas

Y_Quality
0     0.517719
1     0.519090
2     0.529362
3     0.532405
4     0.533110
..         ...
344   0.529510
345   0.529948
346   0.529308
347   0.526546
348   0.533702

[349 rows x 1 columns]

In [180]:
T10_class

22     0
23     0
25     1
29     1
37     1
      ..
589    1
590    1
591    1
593    1
597    1
Name: Y_Class, Length: 349, dtype: int64

In [181]:
T10y_idx= T10_class.index
T10y_idx = pd.DataFrame(T10y_idx, columns = ['index'])
T10_datas = pd.concat([T10y_idx, T10_datas], axis = 1)
T10_datas = T10_datas.set_index('index')
T10_datas

Y_Quality
index           
22      0.522109
23      0.522585
25      0.530021
29      0.531225
37      0.531454
...          ...
589     0.530116
590     0.530183
591     0.529922
593     0.528703
597     0.531797

[349 rows x 1 columns]

In [182]:
from pycaret.classification import *
# 분류 패키지의 모든 모듈을 임포트한다.
exp_clf101 = setup(data=T10_datas, 
                   target=T10_class, 
                   fold=5,
                   session_id=414)
top5 = compare_models(sort='Accuracy', n_select=5)

Processing:   0%|          | 0/73 [00:00<?, ?it/s]

In [183]:
T10_total_models = []

T10_model_rf = create_model('rf', fold = 5)
T10_total_models.append(T10_model_rf)

T10_model_gbc = create_model('gbc', fold = 5)
T10_total_models.append(T10_model_gbc)

T10_model_et = create_model('et', fold = 5)
T10_total_models.append(T10_model_et)

T10_model_catboost = create_model('catboost', fold = 5)
T10_total_models.append(T10_model_catboost)

T10_model_xgb = create_model('xgboost', fold = 5)
T10_total_models.append(T10_model_xgb)

T10_model_ada = create_model('ada', fold = 5)
T10_total_models.append(T10_model_ada)

T10_model_lightgbm = create_model('lightgbm', fold = 5)
T10_total_models.append(T10_model_lightgbm)

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

In [184]:
T10_model_rf = tune_model(T10_model_rf, fold=5, choose_better = True)

T10_model_gbc = tune_model(T10_model_gbc, fold=5, choose_better = True)

T10_model_et = tune_model(T10_model_et, fold=5, choose_better = True)

T10_model_catboost = tune_model(T10_model_catboost, fold=5, choose_better = True)

T10_model_xgb = tune_model(T10_model_xgb, fold=5, choose_better = True)

T10_model_ada = tune_model(T10_model_ada, fold=5, choose_better = True)

T10_model_lightgbm = tune_model(T10_model_lightgbm, fold=5, choose_better = True)

Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

...

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


In [185]:
T10_tuned_models = [T10_model_rf, T10_model_gbc, T10_model_et, T10_model_catboost, T10_model_xgb, T10_model_ada, T10_model_lightgbm]
T10_tuned_models

[RandomForestClassifier(bootstrap=True, ccp_alpha=0.0, class_weight={},
                        criterion='entropy', max_depth=5, max_features='sqrt',
                        max_leaf_nodes=None, max_samples=None,
                        min_impurity_decrease=0.3, min_samples_leaf=3,
                        min_samples_split=10, min_weight_fraction_leaf=0.0,
                        n_estimators=170, n_jobs=-1, oob_score=False,
                        random_state=414, verbose=0, warm_start=False),
 GradientBoostingClassifier(ccp_alpha=0.0, criterion='friedman_mse', init=None,
                            learning_rate=0.05, loss='deviance', max_depth=7,
                            max_features='log2', max_leaf_nodes=None,
                            min_impurity_decrease=0, min_samples_leaf=1,
                            min_samples_split=10, min_weight_fraction_leaf=0.0,
                            n_estimators=60, n_iter_no_change=None,
                            random_state=414, su

In [186]:
for model in T10_tuned_models:
    display(predict_model(model))

Y_Quality  Y_Class  prediction_label  prediction_score
244   0.529268        1                 1            0.9892
245   0.528703        1                 1            0.9892
246   0.529929        1                 1            0.9892
247   0.531068        1                 1            0.9892
248   0.522584        0                 0            0.8328
..         ...      ...               ...               ...
344   0.531924        1                 1            0.9892
345   0.530183        1                 1            0.9892
346   0.527088        0                 0            0.8328
347   0.529881        1                 1            0.9892
348   0.531574        1                 1            0.9892

[105 rows x 4 columns]

Y_Quality  Y_Class  prediction_label  prediction_score
244   0.529268        1                 1            0.9967
245   0.528703        1                 1            0.9967
246   0.529929        1                 1            0.9967
247   0.531068        1                 1            0.9967
248   0.522584        0                 0            0.9709
..         ...      ...               ...               ...
344   0.531924        1                 1            0.9967
345   0.530183        1                 1            0.9967
346   0.527088        0                 0            0.9658
347   0.529881        1                 1            0.9967
348   0.531574        1                 1            0.9967

[105 rows x 4 columns]

Y_Quality  Y_Class  prediction_label  prediction_score
244   0.529268        1                 1               1.0
245   0.528703        1                 1               1.0
246   0.529929        1                 1               1.0
247   0.531068        1                 1               1.0
248   0.522584        0                 0               1.0
..         ...      ...               ...               ...
344   0.531924        1                 1               1.0
345   0.530183        1                 1               1.0
346   0.527088        0                 0               1.0
347   0.529881        1                 1               1.0
348   0.531574        1                 1               1.0

[105 rows x 4 columns]

Y_Quality  Y_Class  prediction_label  prediction_score
244   0.529268        1                 1            0.3392
245   0.528703        1                 1            0.3387
246   0.529929        1                 1            0.3395
247   0.531068        1                 1            0.3394
248   0.522584        0                 0            0.3367
..         ...      ...               ...               ...
344   0.531924        1                 1            0.3382
345   0.530183        1                 1            0.3395
346   0.527088        0                 0            0.3367
347   0.529881        1                 1            0.3395
348   0.531574        1                 1            0.3393

[105 rows x 4 columns]

Y_Quality  Y_Class  prediction_label  prediction_score
244   0.529268        1                 1            0.5163
245   0.528703        1                 1            0.5124
246   0.529929        1                 1            0.5163
247   0.531068        1                 1            0.5163
248   0.522584        0                 0            0.5021
..         ...      ...               ...               ...
344   0.531924        1                 1            0.5106
345   0.530183        1                 1            0.5163
346   0.527088        0                 0            0.5013
347   0.529881        1                 1            0.5163
348   0.531574        1                 1            0.5163

[105 rows x 4 columns]

Y_Quality  Y_Class  prediction_label  prediction_score
244   0.529268        1                 1            0.4089
245   0.528703        1                 1            0.4089
246   0.529929        1                 1            0.4089
247   0.531068        1                 1            0.4089
248   0.522584        0                 0            0.3767
..         ...      ...               ...               ...
344   0.531924        1                 1            0.4089
345   0.530183        1                 1            0.4089
346   0.527088        0                 0            0.3767
347   0.529881        1                 1            0.4089
348   0.531574        1                 1            0.4089

[105 rows x 4 columns]

Y_Quality  Y_Class  prediction_label  prediction_score
244   0.529268        1                 1            0.9997
245   0.528703        1                 1            0.9995
246   0.529929        1                 1            0.9997
247   0.531068        1                 1            0.9997
248   0.522584        0                 0            0.9989
..         ...      ...               ...               ...
344   0.531924        1                 1            0.9995
345   0.530183        1                 1            0.9997
346   0.527088        0                 0            0.9989
347   0.529881        1                 1            0.9997
348   0.531574        1                 1            0.9997

[105 rows x 4 columns]

In [187]:
T10_vote_classification_models = [
    ('ada',  T10_model_ada),
    ('lightgbm', T10_model_lightgbm),
    ('rf', T10_model_rf),
    ('gbc', T10_model_gbc),
    ('et', T10_model_et),
    ('cat', T10_model_catboost),
    ('xgb', T10_model_xgb),
]

In [188]:
T10_soft_vote = VotingClassifier(T10_vote_classification_models, voting = 'soft')
#soft_vote_cv = cross_validate(soft_vote, T01_datas, T01_class, cv = KFold)
T10_soft_vote.fit(T10_datas, T10_class)

VotingClassifier(estimators=[('ada',
                              AdaBoostClassifier(algorithm='SAMME',
                                                 base_estimator=None,
                                                 learning_rate=0.05,
                                                 n_estimators=190,
                                                 random_state=414)),
                             ('lightgbm',
                              LGBMClassifier(boosting_type='gbdt',
                                             class_weight=None,
                                             colsample_bytree=1.0,
                                             importance_type='split',
                                             learning_rate=0.1, max_depth=-1,
                                             min_child_samples=20,
                                             min_child_weight=0.001,
                                             min_split_gain=0...
                               

In [189]:
T10_prediction = pd.DataFrame(T10_soft_vote.predict(T10_datas), columns = ['prediction_label'])
T10_prediction

prediction_label
0                   0
1                   0
2                   1
3                   1
4                   1
..                ...
344                 1
345                 1
346                 1
347                 1
348                 1

[349 rows x 1 columns]

In [148]:
T10_final_classification_model = finalize_model(T10_model_xgb)

In [149]:
T10_prediction = predict_model(T10_final_classification_model, data=T10_datas)
#prediction.drop(['Y_Quality'], axis = 1, inplace = True)

In [190]:
T10_y_class = pd.DataFrame(T10_class, columns = ['Y_Class'])
T10_idx = T10_y_class.index
T10_y_class = T10_y_class.reset_index()
T10_prediction = pd.concat([T10_prediction, T10_y_class], axis = 1)
T10_prediction = T10_prediction.set_index('index')
T10_prediction.drop(['Y_Class'], axis = 1, inplace = True)

In [191]:
T10_prediction

prediction_label
index                  
22                    0
23                    0
25                    1
29                    1
37                    1
...                 ...
589                   1
590                   1
591                   1
593                   1
597                   1

[349 rows x 1 columns]

# Test

In [226]:
test_data = pd.read_csv("./test.csv")
test_data

PRODUCT_ID         TIMESTAMP     LINE PRODUCT_CODE  X_1   X_2  X_3   X_4  \
0     TEST_000   2022-09-09 2:01  T100306         T_31  2.0  94.0  0.0  45.0   
1     TEST_001   2022-09-09 2:09  T100304         T_31  2.0  93.0  0.0  45.0   
2     TEST_002   2022-09-09 8:42  T100304         T_31  2.0  95.0  0.0  45.0   
3     TEST_003  2022-09-09 10:56  T010305         A_31  NaN   NaN  NaN   NaN   
4     TEST_004  2022-09-09 11:04  T010306         A_31  NaN   NaN  NaN   NaN   
..         ...               ...      ...          ...  ...   ...  ...   ...   
305   TEST_305  2022-11-05 11:18  T100306         T_31  2.0  91.0  0.0  45.0   
306   TEST_306  2022-11-05 16:39  T100304         T_31  2.0  96.0  0.0  45.0   
307   TEST_307  2022-11-05 16:47  T100306         T_31  2.0  91.0  0.0  45.0   
308   TEST_308  2022-11-05 20:53  T100306         T_31  2.0  95.0  0.0  45.0   
309   TEST_309  2022-11-05 21:01  T100306         T_31  2.0  87.0  0.0  45.0   

      X_5  X_6  ...  X_2866  X_2867  X_2868  X_2869  X_2870  X_2871  X_2872  \
0    10.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
1    11.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
2    11.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
3     NaN  NaN  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
4     NaN  NaN  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
..    ...  ...  ...     ...     ...     ...     ...     ...     ...     ...   
305  10.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
306  11.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
307  10.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
308  10.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
309  10.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   

     X_2873  X_2874  X_2875  
0       NaN     NaN     NaN  
1       NaN     NaN     NaN  
2       NaN     NaN     NaN  
3       NaN     NaN     NaN  
4       NaN     NaN     NaN  
..      ...     ...     ...  
305     NaN     NaN     NaN  
306     NaN     NaN     NaN  
307     NaN     NaN     NaN  
308     NaN     NaN     NaN  
309     NaN     NaN     NaN  

[310 rows x 2879 columns]

In [227]:
test_data['YEAR'] =  pd.to_datetime(test_data['TIMESTAMP']).dt.year
test_data['MONTH'] =  pd.to_datetime(test_data['TIMESTAMP']).dt.month
test_data['DAY'] =  pd.to_datetime(test_data['TIMESTAMP']).dt.day
test_data['HOUR'] =  pd.to_datetime(test_data['TIMESTAMP']).dt.hour
test_data['MINUTE'] =  pd.to_datetime(test_data['TIMESTAMP']).dt.minute
test_data['DAY_OF_WEEK'] =  pd.to_datetime(test_data['TIMESTAMP']).dt.day_name()

In [228]:
test_data = test_data.drop(['MONTH', 'DAY', 'YEAR'], axis = 1)

In [229]:
test_data.drop(colls, inplace = True, axis = 1)

In [230]:
test_data.loc[(test_data.PRODUCT_CODE == 'A_31')&(test_data.LINE == 'T010305'),'LINE_AND_CODE'] = 0
test_data.loc[(test_data.PRODUCT_CODE == 'A_31')&(test_data.LINE == 'T010306'),'LINE_AND_CODE'] = 1
test_data.loc[(test_data.PRODUCT_CODE == 'A_31')&(test_data.LINE == 'T050304'),'LINE_AND_CODE'] = 2
test_data.loc[(test_data.PRODUCT_CODE == 'A_31')&(test_data.LINE == 'T050307'),'LINE_AND_CODE'] = 3
test_data.loc[(test_data.PRODUCT_CODE == 'A_31')&(test_data.LINE == 'T100304'),'LINE_AND_CODE'] = 4
test_data.loc[(test_data.PRODUCT_CODE == 'A_31')&(test_data.LINE == 'T100306'),'LINE_AND_CODE'] = 5

test_data.loc[(test_data.PRODUCT_CODE == 'T_31')&(test_data.LINE == 'T010305'),'LINE_AND_CODE'] = 6
test_data.loc[(test_data.PRODUCT_CODE == 'T_31')&(test_data.LINE == 'T010306'),'LINE_AND_CODE'] = 7
test_data.loc[(test_data.PRODUCT_CODE == 'T_31')&(test_data.LINE == 'T050304'),'LINE_AND_CODE'] = 8
test_data.loc[(test_data.PRODUCT_CODE == 'T_31')&(test_data.LINE == 'T050307'),'LINE_AND_CODE'] = 9
test_data.loc[(test_data.PRODUCT_CODE == 'T_31')&(test_data.LINE == 'T100304'),'LINE_AND_CODE'] = 10
test_data.loc[(test_data.PRODUCT_CODE == 'T_31')&(test_data.LINE == 'T100306'),'LINE_AND_CODE'] = 11

test_data.loc[(test_data.PRODUCT_CODE == 'O_31')&(test_data.LINE == 'T010305'),'LINE_AND_CODE'] = 12
test_data.loc[(test_data.PRODUCT_CODE == 'O_31')&(test_data.LINE == 'T010306'),'LINE_AND_CODE'] = 13
test_data.loc[(test_data.PRODUCT_CODE == 'O_31')&(test_data.LINE == 'T050304'),'LINE_AND_CODE'] = 14
test_data.loc[(test_data.PRODUCT_CODE == 'O_31')&(test_data.LINE == 'T050307'),'LINE_AND_CODE'] = 15
test_data.loc[(test_data.PRODUCT_CODE == 'O_31')&(test_data.LINE == 'T100304'),'LINE_AND_CODE'] = 16
test_data.loc[(test_data.PRODUCT_CODE == 'O_31')&(test_data.LINE == 'T100306'),'LINE_AND_CODE'] = 17
test_data

PRODUCT_ID         TIMESTAMP     LINE PRODUCT_CODE  X_1   X_2  X_3   X_4  \
0     TEST_000   2022-09-09 2:01  T100306         T_31  2.0  94.0  0.0  45.0   
1     TEST_001   2022-09-09 2:09  T100304         T_31  2.0  93.0  0.0  45.0   
2     TEST_002   2022-09-09 8:42  T100304         T_31  2.0  95.0  0.0  45.0   
3     TEST_003  2022-09-09 10:56  T010305         A_31  NaN   NaN  NaN   NaN   
4     TEST_004  2022-09-09 11:04  T010306         A_31  NaN   NaN  NaN   NaN   
..         ...               ...      ...          ...  ...   ...  ...   ...   
305   TEST_305  2022-11-05 11:18  T100306         T_31  2.0  91.0  0.0  45.0   
306   TEST_306  2022-11-05 16:39  T100304         T_31  2.0  96.0  0.0  45.0   
307   TEST_307  2022-11-05 16:47  T100306         T_31  2.0  91.0  0.0  45.0   
308   TEST_308  2022-11-05 20:53  T100306         T_31  2.0  95.0  0.0  45.0   
309   TEST_309  2022-11-05 21:01  T100306         T_31  2.0  87.0  0.0  45.0   

      X_5  X_6  ...  X_2866  X_2867  X_2868  X_2869  X_2870  X_2871  HOUR  \
0    10.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     2   
1    11.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     2   
2    11.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     8   
3     NaN  NaN  ...     NaN     NaN     NaN     NaN     NaN     NaN    10   
4     NaN  NaN  ...     NaN     NaN     NaN     NaN     NaN     NaN    11   
..    ...  ...  ...     ...     ...     ...     ...     ...     ...   ...   
305  10.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN    11   
306  11.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN    16   
307  10.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN    16   
308  10.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN    20   
309  10.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN    21   

     MINUTE  DAY_OF_WEEK  LINE_AND_CODE  
0         1       Friday           11.0  
1         9       Friday           10.0  
2        42       Friday           10.0  
3        56       Friday            0.0  
4         4       Friday            1.0  
..      ...          ...            ...  
305      18     Saturday           11.0  
306      39     Saturday           10.0  
307      47     Saturday           11.0  
308      53     Saturday           11.0  
309       1     Saturday           11.0  

[310 rows x 2801 columns]

In [231]:
test_data.loc[test_data.DAY_OF_WEEK == 'Monday','DAY_OF_WEEK'] = 1
test_data.loc[test_data.DAY_OF_WEEK == 'Tuesday','DAY_OF_WEEK'] = 2
test_data.loc[test_data.DAY_OF_WEEK == 'Wednesday','DAY_OF_WEEK'] = 3
test_data.loc[test_data.DAY_OF_WEEK == 'Thursday','DAY_OF_WEEK'] = 4
test_data.loc[test_data.DAY_OF_WEEK == 'Friday','DAY_OF_WEEK'] = 5
test_data.loc[test_data.DAY_OF_WEEK == 'Saturday','DAY_OF_WEEK'] = 6
test_data.loc[test_data.DAY_OF_WEEK == 'Sunday','DAY_OF_WEEK'] = 7

test_data.loc[test_data.PRODUCT_CODE == 'A_31','PRODUCT_CODE'] = 1
test_data.loc[test_data.PRODUCT_CODE == 'T_31','PRODUCT_CODE'] = 2
test_data.loc[test_data.PRODUCT_CODE == 'O_31','PRODUCT_CODE'] = 3

test_data.drop(['PRODUCT_ID', 'TIMESTAMP'], axis = 1, inplace = True)
test_data

LINE PRODUCT_CODE  X_1   X_2  X_3   X_4   X_5  X_6   X_7   X_8  ...  \
0    T100306            2  2.0  94.0  0.0  45.0  10.0  0.0  51.0  10.0  ...   
1    T100304            2  2.0  93.0  0.0  45.0  11.0  0.0  45.0  10.0  ...   
2    T100304            2  2.0  95.0  0.0  45.0  11.0  0.0  45.0  10.0  ...   
3    T010305            1  NaN   NaN  NaN   NaN   NaN  NaN   NaN   NaN  ...   
4    T010306            1  NaN   NaN  NaN   NaN   NaN  NaN   NaN   NaN  ...   
..       ...          ...  ...   ...  ...   ...   ...  ...   ...   ...  ...   
305  T100306            2  2.0  91.0  0.0  45.0  10.0  0.0  51.0  10.0  ...   
306  T100304            2  2.0  96.0  0.0  45.0  11.0  0.0  45.0  10.0  ...   
307  T100306            2  2.0  91.0  0.0  45.0  10.0  0.0  50.0  10.0  ...   
308  T100306            2  2.0  95.0  0.0  45.0  10.0  0.0  51.0  10.0  ...   
309  T100306            2  2.0  87.0  0.0  45.0  10.0  0.0  51.0  10.0  ...   

     X_2866  X_2867  X_2868  X_2869  X_2870  X_2871  HOUR  MINUTE  \
0       NaN     NaN     NaN     NaN     NaN     NaN     2       1   
1       NaN     NaN     NaN     NaN     NaN     NaN     2       9   
2       NaN     NaN     NaN     NaN     NaN     NaN     8      42   
3       NaN     NaN     NaN     NaN     NaN     NaN    10      56   
4       NaN     NaN     NaN     NaN     NaN     NaN    11       4   
..      ...     ...     ...     ...     ...     ...   ...     ...   
305     NaN     NaN     NaN     NaN     NaN     NaN    11      18   
306     NaN     NaN     NaN     NaN     NaN     NaN    16      39   
307     NaN     NaN     NaN     NaN     NaN     NaN    16      47   
308     NaN     NaN     NaN     NaN     NaN     NaN    20      53   
309     NaN     NaN     NaN     NaN     NaN     NaN    21       1   

     DAY_OF_WEEK  LINE_AND_CODE  
0              5           11.0  
1              5           10.0  
2              5           10.0  
3              5            0.0  
4              5            1.0  
..           ...            ...  
305            6           11.0  
306            6           10.0  
307            6           11.0  
308            6           11.0  
309            6           11.0  

[310 rows x 2799 columns]

In [232]:
TT050304 = test_data[test_data['LINE'] == 'T050304']
TT050307 = test_data[test_data['LINE'] == 'T050307']
TT010305 = test_data[test_data['LINE'] == 'T010305']
TT010306 = test_data[test_data['LINE'] == 'T010306']
TT100304 = test_data[test_data['LINE'] == 'T100304']
TT100306 = test_data[test_data['LINE'] == 'T100306']
TT050304

LINE PRODUCT_CODE  X_1  X_2  X_3  X_4  X_5  X_6  X_7  X_8  ...  X_2866  \
7   T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   57.74   
8   T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   53.18   
14  T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   49.77   
35  T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   55.22   
41  T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   49.67   
42  T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   51.30   
52  T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   54.06   
53  T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   54.04   
54  T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   55.72   
61  T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...     NaN   
64  T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...     NaN   
65  T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   51.55   
66  T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   51.37   

    X_2867  X_2868  X_2869  X_2870  X_2871  HOUR  MINUTE  DAY_OF_WEEK  \
7    52.51   54.45   57.99   63.16     1.0    12      27            6   
8    56.02   41.79   47.94   60.72     1.0    12      35            6   
14   54.93   49.85   48.62   63.18     1.0     6      10            6   
35   58.14   48.93   56.16   64.25     1.0     3      58            7   
41   45.00   49.81   55.19   67.17     1.0    23       2            1   
42   47.66   60.00   53.75   62.58     1.0    23      10            1   
52   51.18   52.17   57.75   63.94     1.0    17      47            3   
53   51.25   54.98   57.22   63.33     1.0    17      55            3   
54   57.57   42.08   55.19   66.06     1.0    18       3            3   
61     NaN     NaN     NaN     NaN     1.0    21      24            7   
64     NaN     NaN     NaN     NaN     1.0     0      35            1   
65   55.55   39.85   47.82   61.59     1.0     3      24            1   
66   55.70   52.49   48.34   62.12     1.0     8      26            1   

    LINE_AND_CODE  
7             2.0  
8             2.0  
14            2.0  
35            2.0  
41            2.0  
42            2.0  
52            2.0  
53            2.0  
54            2.0  
61            2.0  
64            2.0  
65            2.0  
66            2.0  

[13 rows x 2799 columns]

In [233]:
TT050304.drop(['LINE'], axis = 1, inplace = True)
TT050307.drop(['LINE'], axis = 1, inplace = True)
TT010305.drop(['LINE'], axis = 1, inplace = True)
TT010306.drop(['LINE'], axis = 1, inplace = True)
TT100304.drop(['LINE'], axis = 1, inplace = True)
TT100306.drop(['LINE'], axis = 1, inplace = True)

In [234]:
TT050304.drop(T050304_col, inplace = True, axis = 1)
TT050307.drop(T050307_col, inplace = True, axis = 1)
TT010305.drop(T010305_col, inplace = True, axis = 1)
TT010306.drop(T010306_col, inplace = True, axis = 1)
TT100304.drop(T100304_col, inplace = True, axis = 1)
TT100306.drop(T100306_col, inplace = True, axis = 1)
TT050304

PRODUCT_CODE    X_128    X_129  X_132  X_133  X_134  X_135  X_136  X_137  \
7             1  18031.0  18031.0   0.19   0.20   0.19    0.2  354.0  354.0   
8             1  18064.0  18064.0   0.19   0.20   0.19    0.2  355.0  354.0   
14            1    295.0    295.0   0.19   0.21   0.19    0.2   60.0   60.0   
35            1   8632.0   8632.0   0.20   0.21   0.20    0.2  249.0  249.0   
41            1  10712.0  10712.0   0.20   0.21   0.20    0.2  293.0  293.0   
42            1  10729.0  10729.0   0.20   0.21   0.19    0.2  293.0  293.0   
52            1  12261.0  12261.0   0.19   0.21   0.19    0.2  330.0  330.0   
53            1  12283.0  12283.0   0.20   0.21   0.20    0.2  330.0  330.0   
54            1  12305.0  12305.0   0.19   0.21   0.19    0.2  330.0  330.0   
61            1  17990.0  17990.0   0.20   0.21   0.20    0.2  436.0  436.0   
64            1  18026.0  18026.0   0.20   0.21   0.20    0.2  437.0  437.0   
65            1  18220.0  18220.0   0.20   0.21   0.20    0.2  441.0  441.0   
66            1  18514.0  18514.0   0.20   0.21   0.20    0.2  446.0  446.0   

    X_138  ...  X_2866  X_2867  X_2868  X_2869  X_2870  X_2871  HOUR  MINUTE  \
7   354.0  ...   57.74   52.51   54.45   57.99   63.16     1.0    12      27   
8   355.0  ...   53.18   56.02   41.79   47.94   60.72     1.0    12      35   
14   60.0  ...   49.77   54.93   49.85   48.62   63.18     1.0     6      10   
35  249.0  ...   55.22   58.14   48.93   56.16   64.25     1.0     3      58   
41  293.0  ...   49.67   45.00   49.81   55.19   67.17     1.0    23       2   
42  293.0  ...   51.30   47.66   60.00   53.75   62.58     1.0    23      10   
52  330.0  ...   54.06   51.18   52.17   57.75   63.94     1.0    17      47   
53  330.0  ...   54.04   51.25   54.98   57.22   63.33     1.0    17      55   
54  330.0  ...   55.72   57.57   42.08   55.19   66.06     1.0    18       3   
61  436.0  ...     NaN     NaN     NaN     NaN     NaN     1.0    21      24   
64  437.0  ...     NaN     NaN     NaN     NaN     NaN     1.0     0      35   
65  441.0  ...   51.55   55.55   39.85   47.82   61.59     1.0     3      24   
66  446.0  ...   51.37   55.70   52.49   48.34   62.12     1.0     8      26   

    DAY_OF_WEEK  LINE_AND_CODE  
7             6            2.0  
8             6            2.0  
14            6            2.0  
35            7            2.0  
41            1            2.0  
42            1            2.0  
52            3            2.0  
53            3            2.0  
54            3            2.0  
61            7            2.0  
64            1            2.0  
65            1            2.0  
66            1            2.0  

[13 rows x 1973 columns]

In [235]:
TT05 = pd.concat([TT050304, TT050307])
TT01 = pd.concat([TT010305, TT010306])
TT10 = pd.concat([TT100304, TT100306])

In [236]:
TT05.drop(T5drop, inplace = True, axis = 1)
TT01.drop(T0drop, inplace = True, axis = 1)
TT10.drop(T1drop, inplace = True, axis = 1)

In [237]:
TT05 = TT05.fillna(0)
TT01 = TT01.fillna(0)
TT10 = TT10.fillna(0)

In [238]:
TT05_idx = TT05['PRODUCT_CODE'].index
TT05_idx = pd.DataFrame(TT05_idx, columns = ['index'])
TT05_idx

index
0       7
1       8
2      14
3      35
4      41
5      42
6      52
7      53
8      54
9      61
10     64
11     65
12     66
13     13
14     36
15     62
16     63
17    130
18    131
19    132
20    248
21    249
22    250
23    251
24    252
25    253
26    254
27    255
28    260
29    263
30    280
31    281
32    282
33    283
34    284
35    285
36    286
37    292
38    293

In [239]:
TT05.drop(['PRODUCT_CODE'], axis = 1, inplace = True)

In [240]:
T_05c = T05_data.columns
T_05scaler = RobustScaler()
T_05scaled = T_05scaler.fit_transform(T05_data)
T05_data = pd.DataFrame(T_05scaled, columns = T_05c)
T05_data

X_132  X_133  X_134  X_135     X_136     X_137     X_138     X_139  \
0     -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864 -0.024793   
1     -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864  0.024793   
2     -1.0   -1.0   -2.0    0.0 -0.199797 -0.201826 -0.208864 -0.008264   
3     -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864  0.002755   
4     -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864 -0.002755   
..     ...    ...    ...    ...       ...       ...       ...       ...   
115   -1.0   -1.0   -1.0    0.0 -0.497972 -0.500000 -0.502292 -1.049587   
116   -1.0   -1.0   -1.0    0.0 -0.495943 -0.497972 -0.500255 -1.049587   
117   -1.0   -1.0   -1.0    0.0 -0.491886 -0.493915 -0.496179 -1.044077   
118   -1.0   -1.0   -1.0    0.0 -0.491886 -0.493915 -0.496179 -1.033058   
119   -1.0   -1.0   -1.0    0.0 -0.485801 -0.487830 -0.490066 -1.082645   

        X_140     X_141  ...    X_2866    X_2867    X_2868    X_2869  \
0   -0.052154  0.023438  ... -0.819981 -0.721628 -1.242857 -0.958879   
1   -0.029478  0.315104  ... -0.829261 -0.942865 -0.535000 -0.848622   
2   -0.043084 -0.049479  ... -0.859573 -0.669450 -0.216429 -1.004067   
3   -0.043084 -1.195312  ... -1.243118 -0.693973 -0.828571 -1.106191   
4   -0.047619  0.263021  ... -0.639963 -0.602661  0.402857 -0.996385   
..        ...       ...  ...       ...       ...       ...       ...   
115 -0.882086 -0.898437  ...  0.023198  0.080355  0.227143  0.044736   
116 -0.891156 -0.929687  ...  0.000928 -0.084529  0.524286  0.057840   
117 -0.886621 -0.695312  ... -0.019487  0.079311  0.322143 -0.214641   
118 -0.877551 -0.919271  ...  0.064646  0.218106 -0.007857  0.106191   
119 -0.877551 -1.263021  ... -3.253634 -2.855205 -3.568571 -2.499322   

        X_2870  X_2871      HOUR    MINUTE  DAY_OF_WEEK  LINE_AND_CODE  
0     3.252475    -1.0 -0.222222 -0.538462         -0.6            0.0  
1     3.396040    -1.0 -0.222222  0.076923         -0.6            0.0  
2     3.054455    -1.0 -0.222222  0.730769         -0.6            0.0  
3     3.044554    -1.0 -0.111111 -0.961538         -0.6            0.0  
4     3.433168    -1.0 -0.111111 -0.346154         -0.6            0.0  
..         ...     ...       ...       ...          ...            ...  
115   0.346535     0.0  0.111111 -0.384615          0.2            1.0  
116   0.544554     0.0  0.111111 -0.076923          0.2            1.0  
117  -0.519802     0.0  0.222222  0.384615          0.2            1.0  
118  -0.368812     0.0  0.777778  1.192308          0.2            1.0  
119 -15.997525     0.0  0.555556  0.346154          0.2            1.0  

[120 rows x 1960 columns]

In [241]:
TT05c = TT05.columns
TT05scaled = T_05scaler.transform(TT05)
TT05scaled
TT05 = pd.DataFrame(TT05scaled, columns = TT05c)
TT05

X_132  X_133  X_134  X_135     X_136     X_137     X_138     X_139  \
0    -1.0   -1.0   -1.0    0.0  0.055781  0.053753  0.053999  0.449036   
1    -1.0   -1.0   -1.0    0.0  0.057809  0.053753  0.056037  0.449036   
2    -1.0    0.0   -1.0    0.0 -0.540568 -0.542596 -0.545084 -1.374656   
3     0.0    0.0    0.0    0.0 -0.157201 -0.159229 -0.159959 -0.013774   
4     0.0    0.0    0.0    0.0 -0.067951 -0.069980 -0.070301 -0.134986   
5     0.0    0.0   -1.0    0.0 -0.067951 -0.069980 -0.070301 -0.129477   
6    -1.0    0.0   -1.0    0.0  0.007099  0.005071  0.005094 -0.024793   
7     0.0    0.0    0.0    0.0  0.007099  0.005071  0.005094  0.002755   
8    -1.0    0.0   -1.0    0.0  0.007099  0.005071  0.005094 -0.019284   
9     0.0    0.0    0.0    0.0  0.222110  0.220081  0.221090  0.482094   
10    0.0    0.0    0.0    0.0  0.224138  0.222110  0.223128  0.570248   
11    0.0    0.0    0.0    0.0  0.232252  0.230223  0.231279  0.575758   
12    0.0    0.0    0.0    0.0  0.242394  0.240365  0.241467  0.542700   
13    1.0    1.0    1.0    0.0 -0.195740 -0.197769 -0.196638 -0.151515   
14    1.0    1.0    1.0    0.0 -0.461460 -0.463489 -0.465614 -0.101928   
15    1.0    1.0    1.0    0.0 -0.560852 -0.564909 -0.585838 -0.261708   
16    1.0    1.0    1.0    0.0 -0.556795 -0.560852 -0.583800 -0.157025   
17    1.0    1.0    0.0    0.0  0.197769  0.193712  0.174223  0.129477   
18    1.0    0.0    1.0    0.0  0.197769  0.193712  0.176261  0.057851   
19    1.0    1.0    1.0    0.0  0.201826  0.197769  0.180336  0.046832   
20    1.0    1.0    1.0    0.0  0.822515  0.818458  0.803872  0.669421   
21    1.0    1.0    1.0    0.0  0.822515  0.818458  0.803872  0.630854   
22    1.0    1.0    1.0    0.0  0.824544  0.820487  0.803872  0.586777   
23    1.0    1.0    1.0    0.0  0.824544  0.820487  0.803872  0.592287   
24    1.0    1.0    1.0    0.0  0.824544  0.820487  0.803872  0.581267   
25    1.0    1.0    1.0    0.0  0.824544  0.820487  0.805909  0.586777   
26    1.0    1.0    1.0    0.0  0.832657  0.828600  0.814060  0.608815   
27    1.0    1.0    1.0    0.0  0.834686  0.830629  0.814060  0.619835   
28    1.0    1.0    0.0    0.0  0.834686  0.830629  0.816098  0.680441   
29    0.0    1.0    0.0    0.0  0.840771  0.836714  0.820173  0.752066   
30    1.0    1.0    1.0    0.0  0.938134  0.934077  0.920020  1.033058   
31    1.0    1.0    1.0    0.0  0.940162  0.936105  0.920020  0.955923   
32    1.0    1.0    1.0    0.0  0.960446  0.956389  0.940397  0.900826   
33    1.0    1.0    1.0    0.0  0.960446  0.956389  0.942435  0.884298   
34    1.0    1.0    1.0    0.0  0.972617  0.968560  0.954661  0.884298   
35    1.0    1.0    1.0    0.0  0.972617  0.968560  0.954661  0.895317   
36    1.0    1.0    1.0    0.0  0.974645  0.970588  0.954661  0.895317   
37    1.0    1.0    1.0    0.0  1.003043  0.998986  0.983189  1.000000   
38    1.0    1.0    1.0    0.0  1.003043  0.998986  0.985227  0.994490   

       X_140     X_141  ...    X_2866    X_2867    X_2868    X_2869  \
0   0.428571  0.455729  ...  0.318280 -0.115314  0.320714  0.121103   
1   0.428571  0.460938  ...  0.036189  0.067832 -0.583571 -0.333032   
2  -1.195011 -1.007812  ... -0.174760  0.010957 -0.007857 -0.302305   
3  -0.052154  0.158854  ...  0.162388  0.178450 -0.073571  0.038409   
4  -0.142857  0.184896  ... -0.180946 -0.507175 -0.010714 -0.005423   
5  -0.138322  0.106771  ... -0.080111 -0.368380  0.717143 -0.070493   
6  -0.015873 -1.273437  ...  0.090628 -0.184712  0.157857  0.110258   
7  -0.011338 -0.153646  ...  0.089391 -0.181059  0.358571  0.086308   
8  -0.020408  0.184896  ...  0.193319  0.148709 -0.562857 -0.005423   
9   0.437642  0.726563  ... -3.253634 -2.855205 -3.568571 -2.499322   
10  0.505669  0.690104  ... -3.253634 -2.855205 -3.568571 -2.499322   
11  0.519274  0.403646  ... -0.064646  0.043308 -0.722143 -0.338455   
12  0.487528  0.888021  ... -0.075781  0.051135  0.180714 -0.314957   
13 -0.188209 -0.252604  ... -0.043613  0.027655  

In [242]:
TT05 = pd.concat([TT05_idx, TT05], axis = 1)
TT05 = TT05.set_index('index')

In [243]:
TT01_idx = TT01['PRODUCT_CODE'].index
TT01_idx = pd.DataFrame(TT01_idx, columns = ['index'])
TT01_idx

index
0       3
1       6
2      10
3      11
4      38
5      40
6      71
7      86
8      88
9      89
10    116
11    117
12    141
13    142
14      4
15      5
16      9
17     12
18     37
19     39
20     72
21     79
22     87
23    109
24    114
25    115
26    128
27    129

In [244]:
TT01.drop(['PRODUCT_CODE'], axis = 1, inplace = True)

In [245]:
T_01c = T01_data.columns
T_01scaler = RobustScaler()
T_01scaled = T_01scaler.fit_transform(T01_data)
T01_data = pd.DataFrame(T_01scaled, columns = T_01c)
T01_data

X_246  X_247     X_248  X_249  X_250     X_251  X_252  X_253  X_254  \
0      0.0  -0.25 -0.054348    0.0    0.0  1.011236    0.0   -1.0   -1.0   
1      0.0   1.25 -0.054348    0.0    0.0  1.101124    0.0   -1.0   -1.0   
2      0.0   1.25 -0.054348    0.0    0.0  1.146067    0.0    0.0   -1.0   
3      0.0   1.25 -0.054348    0.0    0.0  1.179775    0.0   -1.0   -1.0   
4      0.0  -0.75 -0.054348    0.0    0.0  1.179775    0.0   -1.0   -1.0   
..     ...    ...       ...    ...    ...       ...    ...    ...    ...   
124    0.0   0.75  1.108696    0.0    0.0  0.000000    0.0    0.0    0.0   
125    1.0   1.25  1.293478    0.0    0.0  0.000000    0.0    0.0    0.0   
126    0.0  -0.25  1.423913    0.0    1.0  0.000000    0.0    0.0    0.0   
127    0.0   0.00  1.489130    0.0    0.0  0.000000    0.0    0.0    0.0   
128    0.0   0.75  0.630435    0.0    1.0  0.000000    0.0    0.0    0.0   

     X_255  ...    X_2860    X_2861    X_2862  X_2863    X_2864  X_2865  \
0      0.0  ... -0.053030  0.321839  0.041096    -1.9 -1.452964    -5.0   
1      0.0  ... -0.530303 -0.217241 -0.109589    -1.9 -1.500816    -5.0   
2      0.0  ...  0.106061  0.217816  0.404110    -1.8 -1.666123    -8.0   
3      0.0  ...  0.689394  0.663885  0.595890    -1.9 -1.604342    -5.0   
4      0.0  ... -0.022727 -0.040517  0.205479    -1.9 -1.524742    -8.5   
..     ...  ...       ...       ...       ...     ...       ...     ...   
124    0.0  ...  0.045455 -0.109329 -0.390411    -0.9 -0.482871    -5.0   
125    0.0  ...  0.371212  0.939778  1.041096     0.1  0.344334     1.0   
126    0.0  ...  0.492424  0.902874  0.876712     0.1  0.264525     0.0   
127    0.0  ...  0.750000  1.195135  0.910959     0.1  0.428577     2.0   
128    0.0  ...  0.719697  1.377586  1.150685     0.7  0.924415     4.5   

         HOUR    MINUTE  DAY_OF_WEEK  LINE_AND_CODE  
0    0.777778 -0.142857     0.666667           -1.0  
1   -0.666667 -0.571429    -1.000000           -1.0  
2   -1.000000  0.535714    -0.666667           -1.0  
3   -0.111111 -0.142857    -0.666667           -1.0  
4   -0.111111  0.142857    -0.666667           -1.0  
..        ...       ...          ...            ...  
124  0.222222 -0.071429    -1.000000            0.0  
125  0.222222  1.000000     0.000000            0.0  
126 -0.333333  0.321429     0.666667            0.0  
127  0.222222  0.285714    -1.333333            0.0  
128 -0.222222 -0.464286    -1.333333            0.0  

[129 rows x 882 columns]

In [246]:
TT01c = TT01.columns
TT01scaled = T_01scaler.transform(TT01)
TT01 = pd.DataFrame(TT01scaled, columns = TT01c)
TT01

X_246  X_247     X_248  X_249  X_250     X_251  X_252  X_253  X_254  \
0     0.0   0.75 -0.054348    0.0    0.0  0.415730    0.0   -1.0   -1.0   
1     0.0   0.75 -0.054348    0.0    0.0  0.449438    0.0   -1.0   -1.0   
2     0.0   0.00 -0.054348    0.0    0.0  0.516854    0.0   -1.0   -1.0   
3     0.0   1.25 -0.054348    0.0    0.0  0.595506    0.0   -1.0   -1.0   
4     1.0  -0.50 -0.054348    0.0    0.0  1.505618    0.0   -1.0   -1.0   
5     1.0   0.75 -0.054348    0.0    0.0  1.584270    0.0   -1.0   -1.0   
6     1.0  -0.25 -0.054348    0.0    0.0  0.067416    0.0   -1.0   -1.0   
7     0.0  -0.25 -0.054348    0.0    0.0  0.258427    0.0   -1.0   -1.0   
8    16.0   0.00 -0.054348    0.0    0.0  0.258427    0.0   -1.0   -1.0   
9     1.0  -0.25 -0.054348    0.0    0.0  0.258427    0.0   -1.0   -1.0   
10    1.0   0.00 -0.054348    0.0    0.0  0.483146    0.0   -1.0   -1.0   
11    0.0  -0.50 -0.054348    0.0    0.0  0.483146    0.0   -1.0   -1.0   
12    0.0  -0.50 -0.054348    0.0    0.0  0.775281    0.0   -1.0   -1.0   
13    1.0  -0.75 -0.054348    0.0    0.0  0.775281    0.0    0.0   -1.0   
14    1.0   1.25  0.913043    0.0    1.0  0.000000    0.0    0.0    0.0   
15    1.0   0.00  0.945652    0.0    1.0  0.000000    0.0    0.0    0.0   
16    0.0  -0.25  1.010870    0.0    0.0  0.000000    0.0    0.0    0.0   
17    1.0  -0.25  1.086957    0.0    0.0  0.000000    0.0    0.0    0.0   
18    0.0   1.00  0.097826    0.0    1.0  0.000000    0.0    0.0    0.0   
19    1.0   0.25  0.173913    0.0    1.0  0.000000    0.0    0.0    0.0   
20    1.0   1.75  0.902174    0.0    1.0  0.000000    0.0    0.0    0.0   
21    0.0   0.00  0.956522    0.0    1.0  0.000000    0.0    0.0    0.0   
22    0.0   0.50  1.152174    0.0    1.0  0.000000    0.0    0.0    0.0   
23    3.0   1.75  1.326087    0.0    1.0  0.000000    0.0    0.0    0.0   
24    0.0   1.25  1.358696    0.0    1.0  0.000000    0.0    0.0    0.0   
25    1.0   0.75  1.358696    0.0    1.0  0.000000    0.0    0.0    0.0   
26    0.0   1.25  1.500000    0.0    1.0  0.000000    0.0    0.0    0.0   
27    1.0   0.75  1.500000    0.0    1.0  0.000000    0.0    0.0    0.0   

    X_255  ...    X_2860    X_2861    X_2862  X_2863    X_2864  X_2865  \
0     0.0  ...  1.159091  1.715374  1.636986     0.2  0.215753     0.0   
1     0.0  ...  1.424242  1.957184  1.041096    -0.1  0.317564     0.0   
2     0.0  ...  1.204545  1.582338  0.993151     0.1  0.206885     0.0   
3     0.0  ...  1.090909  1.374600  1.109589     0.1  0.220187    -0.5   
4     0.0  ...  0.954545  1.398276  1.383562    -0.3  0.650353    -0.5   
5     0.0  ...  1.628788  2.220402  1.767123     0.1  0.957042     4.5   
6     0.0  ...  1.492424  2.167816  1.863014     0.0  0.284937     0.0   
7     0.0  ...  1.492424  2.143966  1.369863     0.1  0.711256     5.0   
8     0.0  ...  3.325758  3.852278  3.178082     0.1  0.018446     0.0   
9     0.0  ...  1.446970  2.243647  1.671233     0.0  0.390890     1.5   
10    0.0  ...  1.416667  1.918647  1.561644     0.1  0.519471     1.5   
11    0.0  ...  1.750000  2.069828  1.993151    -0.9 -0.176183    -0.5   
12    0.0  ...  1.727273  2.173563  2.089041     0.1  0.261011     0.0   
13    0.0  ...  2.484848  2.879659  2.452055     0.1  0.703476     0.0   
14    0.0  ...  2.083333  1.851385  1.356164     0.0  0.102690     0.0   
15    0.0  ...  1.560606  1.792529  1.493151     0.1 -0.056552    -0.5   
16    0.0  ...  1.083333  1.794540  1.684932    -0.9 -0.314092     0.0   
17    0.0  ...  1.090909  1.678161  1.801370     0.1  0.796085     4.5   
18    0.0  ...  1.106061  1.346921  0.883562     0.1  0.353202    -0.5   
19    0.0  ...  1.825758  2.331897  1.856164     1.0  1.452964     4.5   
20    0.0  ...  1.772727  2.225575  1.315068     0.1  0.102229     0.0   
21    0.0  ...  1.568182  2.054598  2.157534     0.0  0.352365     0.0   
22    0.0  ...  1.833333  2.227299  1.904110     0.1  0.123980     0.0   
23    0.0  ...  2.166667  2.789183  2.383562     0.1

In [247]:
TT01 = pd.concat([TT01_idx, TT01], axis = 1)
TT01 = TT01.set_index('index')
TT01

X_246  X_247     X_248  X_249  X_250     X_251  X_252  X_253  X_254  \
index                                                                        
3        0.0   0.75 -0.054348    0.0    0.0  0.415730    0.0   -1.0   -1.0   
6        0.0   0.75 -0.054348    0.0    0.0  0.449438    0.0   -1.0   -1.0   
10       0.0   0.00 -0.054348    0.0    0.0  0.516854    0.0   -1.0   -1.0   
11       0.0   1.25 -0.054348    0.0    0.0  0.595506    0.0   -1.0   -1.0   
38       1.0  -0.50 -0.054348    0.0    0.0  1.505618    0.0   -1.0   -1.0   
40       1.0   0.75 -0.054348    0.0    0.0  1.584270    0.0   -1.0   -1.0   
71       1.0  -0.25 -0.054348    0.0    0.0  0.067416    0.0   -1.0   -1.0   
86       0.0  -0.25 -0.054348    0.0    0.0  0.258427    0.0   -1.0   -1.0   
88      16.0   0.00 -0.054348    0.0    0.0  0.258427    0.0   -1.0   -1.0   
89       1.0  -0.25 -0.054348    0.0    0.0  0.258427    0.0   -1.0   -1.0   
116      1.0   0.00 -0.054348    0.0    0.0  0.483146    0.0   -1.0   -1.0   
117      0.0  -0.50 -0.054348    0.0    0.0  0.483146    0.0   -1.0   -1.0   
141      0.0  -0.50 -0.054348    0.0    0.0  0.775281    0.0   -1.0   -1.0   
142      1.0  -0.75 -0.054348    0.0    0.0  0.775281    0.0    0.0   -1.0   
4        1.0   1.25  0.913043    0.0    1.0  0.000000    0.0    0.0    0.0   
5        1.0   0.00  0.945652    0.0    1.0  0.000000    0.0    0.0    0.0   
9        0.0  -0.25  1.010870    0.0    0.0  0.000000    0.0    0.0    0.0   
12       1.0  -0.25  1.086957    0.0    0.0  0.000000    0.0    0.0    0.0   
37       0.0   1.00  0.097826    0.0    1.0  0.000000    0.0    0.0    0.0   
39       1.0   0.25  0.173913    0.0    1.0  0.000000    0.0    0.0    0.0   
72       1.0   1.75  0.902174    0.0    1.0  0.000000    0.0    0.0    0.0   
79       0.0   0.00  0.956522    0.0    1.0  0.000000    0.0    0.0    0.0   
87       0.0   0.50  1.152174    0.0    1.0  0.000000    0.0    0.0    0.0   
109      3.0   1.75  1.326087    0.0    1.0  0.000000    0.0    0.0    0.0   
114      0.0   1.25  1.358696    0.0    1.0  0.000000    0.0    0.0    0.0   
115      1.0   0.75  1.358696    0.0    1.0  0.000000    0.0    0.0    0.0   
128      0.0   1.25  1.500000    0.0    1.0  0.000000    0.0    0.0    0.0   
129      1.0   0.75  1.500000    0.0    1.0  0.000000    0.0    0.0    0.0   

       X_255  ...    X_2860    X_2861    X_2862  X_2863    X_2864  X_2865  \
index         ...                                                           
3        0.0  ...  1.159091  1.715374  1.636986     0.2  0.215753     0.0   
6        0.0  ...  1.424242  1.957184  1.041096    -0.1  0.317564     0.0   
10       0.0  ...  1.204545  1.582338  0.993151     0.1  0.206885     0.0   
11       0.0  ...  1.090909  1.374600  1.109589     0.1  0.220187    -0.5   
38       0.0  ...  0.954545  1.398276  1.383562    -0.3  0.650353    -0.5   
40       0.0  ...  1.628788  2.220402  1.767123     0.1  0.957042     4.5   
71       0.0  ...  1.492424  2.167816  1.863014     0.0  0.284937     0.0   
86       0.0  ...  1.492424  2.143966  1.369863     0.1  0.711256     5.0   
88       0.0  ...  3.325758  3.852278  3.178082     0.1  0.018446     0.0   
89       0.0  ...  1.446970  2.243647  1.671233     0.0  0.390890     1.5   
116      0.0  ...  1.416667  1.918647  1.561644     0.1  0.519471     1.5   
117      0.0  ...  1.750000  2.069828  1.993151    -0.9 -0.176183    -0.5   
141      0.0  ...  1.727273  2.173563  2.089041     0.1  0.261011     0.0   
142      0.0  ...  2.484848  2.879659  2.452055     0.1  0.703476     0.0   
4        0.0  ...  2.083333  1.851385  1.356164     0.0  0.102690     0.0   
5        0.0  ...  1.560606  1.792529  1.493151     0.1 -0.056552    -0.5   
9        0.0  ...  1.083333  1.794540  1.684932    -0.9 -0.314092     0.0   
12       0.0  ...  1.090909  1.678161  1.801370     0.1  0.796085     4.5   
37       0.0  ...  1.106061  1.346921  0.883562     0.1  0.353202    -0.5   
39       0.0  ...  1.825758  2.331897  1.856164  

In [248]:
TT10_idx = TT10['PRODUCT_CODE'].index
TT10_idx = pd.DataFrame(TT10_idx, columns = ['index'])
TT10_idx

index
0        1
1        2
2       15
3       17
4       20
..     ...
238    301
239    305
240    307
241    308
242    309

[243 rows x 1 columns]

In [249]:
TT10.drop(['PRODUCT_CODE'], axis = 1, inplace = True)

In [250]:
T_10c = T10_data.columns
T_10scaler = RobustScaler()
T_10scaled = T_10scaler.fit_transform(T10_data)
T10_data = pd.DataFrame(T_10scaled, columns = T_10c)
T10_data

X_1  X_2  X_3  X_4  X_5  X_6       X_7  X_8  X_9  X_10  ...  X_928  \
0     0.0  1.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...    0.0   
1     0.0  1.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...  -32.6   
2     0.0  0.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...    0.1   
3     0.0  1.0  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...    0.1   
4     0.0  1.0  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...    0.1   
..    ...  ...  ...  ...  ...  ...       ...  ...  ...   ...  ...    ...   
344  -1.0 -0.2  0.0  0.0  0.0  0.0  0.833333  0.0  1.0   0.0  ...    0.0   
345  -1.0 -1.2  0.0  0.0  0.0  0.0  0.833333  0.0  1.0   0.0  ...    0.1   
346  -1.0 -1.6  0.0  0.0  0.0  0.0  0.833333  0.0  1.0   0.0  ...    0.0   
347   0.0  0.0  0.0  0.0  0.0  0.0  0.833333  0.0  1.0   0.0  ...    0.1   
348  19.0 -1.6  0.0  0.0  0.0  0.0  2.666667  0.0  1.0   0.0  ...    0.0   

         X_929      X_930  X_931       X_932  X_933      HOUR    MINUTE  \
0     0.386364   0.111111    1.0    0.584058    0.0 -0.166667  0.793103   
1   -38.275000 -32.111111 -136.0 -180.608692  -13.2 -0.083333 -1.000000   
2     0.581818   1.000000    1.0    0.739130    0.0 -0.083333 -0.655172   
3     0.738636   1.000000    1.0    0.304348    0.0  1.083333  0.034483   
4     0.756818   1.000000    1.0    0.763768    0.1 -0.583333  0.586207   
..         ...        ...    ...         ...    ...       ...       ...   
344   0.634091   1.000000    1.0    1.130435    0.1  0.666667 -1.034483   
345   0.900000   1.111111    0.0   -0.086956    0.0 -0.750000 -1.000000   
346   0.909091   1.000000    0.0    0.000000    0.0 -0.750000 -0.724138   
347   0.895455   1.000000    0.0   -0.652174    0.0  0.333333  0.000000   
348  -0.172727   0.000000    0.0   -0.269565    0.0  0.333333  0.551724   

     DAY_OF_WEEK  LINE_AND_CODE  
0      -1.000000           -1.0  
1      -1.000000           -1.0  
2       0.666667           -1.0  
3       0.666667           -1.0  
4      -0.666667           -1.0  
..           ...            ...  
344    -1.000000            0.0  
345    -0.666667            0.0  
346    -0.666667            0.0  
347    -0.333333            0.0  
348    -0.333333            6.0  

[349 rows x 669 columns]

In [251]:
TT10c = TT10.columns
TT10scaled = T_10scaler.transform(TT10)
TT10 = pd.DataFrame(TT10scaled, columns = TT10c)
TT10

X_1  X_2  X_3  X_4  X_5  X_6       X_7  X_8  X_9  X_10  ...  X_928  \
0    0.0 -0.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...    0.1   
1    0.0  0.0  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...    0.0   
2    0.0  1.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   -0.9   
3    0.0  0.0  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...    0.0   
4    0.0 -0.2  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   -0.9   
..   ...  ...  ...  ...  ...  ...       ...  ...  ...   ...  ...    ...   
238  0.0 -0.2  0.0  0.0  0.0  0.0  1.000000  0.0  1.0   0.0  ...    0.1   
239  0.0 -0.8  0.0  0.0  0.0  0.0  1.000000  0.0  1.0   0.0  ...    0.0   
240  0.0 -0.8  0.0  0.0  0.0  0.0  0.833333  0.0  1.0   0.0  ...   -0.3   
241  0.0  0.0  0.0  0.0  0.0  0.0  1.000000  0.0  1.0   0.0  ...    0.0   
242  0.0 -1.6  0.0  0.0  0.0  0.0  1.000000  0.0  1.0   0.0  ...    0.1   

        X_929     X_930  X_931     X_932  X_933      HOUR    MINUTE  \
0    0.800000  1.000000    0.0  0.086956    0.0 -0.666667 -0.724138   
1    0.015909  0.000000    0.0 -0.391304    0.0 -0.166667  0.413793   
2   -0.343182  0.000000    0.0 -0.173913    0.0 -0.416667 -0.344828   
3    0.490909  0.000000    1.0  0.043478    0.0  1.083333  0.517241   
4   -0.293182  0.000000    0.0  0.044927    0.0 -0.750000  0.551724   
..        ...       ...    ...       ...    ...       ...       ...   
238  0.818182  1.000000    0.0 -0.260870    0.0  0.416667 -0.413793   
239  0.859091  0.555556    0.0 -0.782609    0.0  0.083333 -0.413793   
240 -0.222727  0.000000    0.0 -0.521739    0.0  0.500000  0.586207   
241  0.102273  0.111111    0.0 -0.869565    0.0  0.833333  0.793103   
242  0.245455  0.000000    0.0 -0.763768    0.0  0.916667 -1.000000   

     DAY_OF_WEEK  LINE_AND_CODE  
0       0.000000           -1.0  
1       0.000000           -1.0  
2      -1.000000           -1.0  
3      -0.333333           -1.0  
4       0.000000           -1.0  
..           ...            ...  
238     0.000000            0.0  
239     0.333333            0.0  
240     0.333333            0.0  
241     0.333333            0.0  
242     0.333333            0.0  

[243 rows x 669 columns]

In [252]:
TT10 = pd.concat([TT10_idx, TT10], axis = 1)
TT10 = TT10.set_index('index')
TT10

X_1  X_2  X_3  X_4  X_5  X_6       X_7  X_8  X_9  X_10  ...  X_928  \
index                                                          ...          
1      0.0 -0.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...    0.1   
2      0.0  0.0  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...    0.0   
15     0.0  1.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   -0.9   
17     0.0  0.0  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...    0.0   
20     0.0 -0.2  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   -0.9   
...    ...  ...  ...  ...  ...  ...       ...  ...  ...   ...  ...    ...   
301    0.0 -0.2  0.0  0.0  0.0  0.0  1.000000  0.0  1.0   0.0  ...    0.1   
305    0.0 -0.8  0.0  0.0  0.0  0.0  1.000000  0.0  1.0   0.0  ...    0.0   
307    0.0 -0.8  0.0  0.0  0.0  0.0  0.833333  0.0  1.0   0.0  ...   -0.3   
308    0.0  0.0  0.0  0.0  0.0  0.0  1.000000  0.0  1.0   0.0  ...    0.0   
309    0.0 -1.6  0.0  0.0  0.0  0.0  1.000000  0.0  1.0   0.0  ...    0.1   

          X_929     X_930  X_931     X_932  X_933      HOUR    MINUTE  \
index                                                                   
1      0.800000  1.000000    0.0  0.086956    0.0 -0.666667 -0.724138   
2      0.015909  0.000000    0.0 -0.391304    0.0 -0.166667  0.413793   
15    -0.343182  0.000000    0.0 -0.173913    0.0 -0.416667 -0.344828   
17     0.490909  0.000000    1.0  0.043478    0.0  1.083333  0.517241   
20    -0.293182  0.000000    0.0  0.044927    0.0 -0.750000  0.551724   
...         ...       ...    ...       ...    ...       ...       ...   
301    0.818182  1.000000    0.0 -0.260870    0.0  0.416667 -0.413793   
305    0.859091  0.555556    0.0 -0.782609    0.0  0.083333 -0.413793   
307   -0.222727  0.000000    0.0 -0.521739    0.0  0.500000  0.586207   
308    0.102273  0.111111    0.0 -0.869565    0.0  0.833333  0.793103   
309    0.245455  0.000000    0.0 -0.763768    0.0  0.916667 -1.000000   

       DAY_OF_WEEK  LINE_AND_CODE  
index                              
1         0.000000           -1.0  
2         0.000000           -1.0  
15       -1.000000           -1.0  
17       -0.333333           -1.0  
20        0.000000           -1.0  
...            ...            ...  
301       0.000000            0.0  
305       0.333333            0.0  
307       0.333333            0.0  
308       0.333333            0.0  
309       0.333333            0.0  

[243 rows x 669 columns]

In [253]:
from pycaret.regression import *
TT05_prediction = predict_model(T05_final_regression_model, data=TT05)
TT01_prediction = predict_model(T01_final_regression_model, data=TT01)
TT10_prediction = predict_model(T10_final_regression_model, data=TT10)

NameError: name 'T01_final_regression_model' is not defined

In [262]:
TT05_prediction = T05_vote_regressor.predict(TT05)
TT01_prediction = T01_vote_regressor.predict(TT01)
TT10_prediction = T10_vote_regressor.predict(TT10)
TT05_prediction

array([0.5259427 , 0.52541112, 0.52193754, 0.52209592, 0.52617994,
       0.52539321, 0.52505398, 0.52495162, 0.52514787, 0.52523937,
       0.5243389 , 0.52196038, 0.52375263, 0.52784045, 0.52902038,
       0.52724367, 0.5298083 , 0.52926914, 0.52952869, 0.52945538,
       0.53054315, 0.53063029, 0.5292762 , 0.52856895, 0.52960082,
       0.52930508, 0.52950084, 0.52976257, 0.5392391 , 0.53010458,
       0.53033794, 0.53299961, 0.52954166, 0.5327926 , 0.52810506,
       0.5291241 , 0.52909553, 0.52755728, 0.52925375])

In [264]:
TT05_prediction = pd.DataFrame(TT05_prediction, columns = ['prediction_label'])
TT01_prediction = pd.DataFrame(TT01_prediction, columns = ['prediction_label'])
TT10_prediction = pd.DataFrame(TT10_prediction, columns = ['prediction_label'])
TT05_prediction

prediction_label
0           0.525943
1           0.525411
2           0.521938
3           0.522096
4           0.526180
5           0.525393
6           0.525054
7           0.524952
8           0.525148
9           0.525239
10          0.524339
11          0.521960
12          0.523753
13          0.527840
14          0.529020
15          0.527244
16          0.529808
17          0.529269
18          0.529529
19          0.529455
20          0.530543
21          0.530630
22          0.529276
23          0.528569
24          0.529601
25          0.529305
26          0.529501
27          0.529763
28          0.539239
29          0.530105
30          0.530338
31          0.533000
32          0.529542
33          0.532793
34          0.528105
35          0.529124
36          0.529096
37          0.527557
38          0.529254

In [265]:
TT05_y_class = pd.DataFrame(TT05, columns = ['PRODUCT_CODE'])
TT05_idx = TT05_y_class.index
TT05_y_class = TT05_y_class.reset_index()
TT05_prediction = pd.concat([TT05_prediction, TT05_y_class], axis = 1)
TT05_prediction = TT05_prediction.set_index('index')
TT05_prediction.drop(['PRODUCT_CODE'], axis = 1, inplace = True)
TT05_prediction

prediction_label
index                  
7              0.525943
8              0.525411
14             0.521938
35             0.522096
41             0.526180
42             0.525393
52             0.525054
53             0.524952
54             0.525148
61             0.525239
64             0.524339
65             0.521960
66             0.523753
13             0.527840
36             0.529020
62             0.527244
63             0.529808
130            0.529269
131            0.529529
132            0.529455
248            0.530543
249            0.530630
250            0.529276
251            0.528569
252            0.529601
253            0.529305
254            0.529501
255            0.529763
260            0.539239
263            0.530105
280            0.530338
281            0.533000
282            0.529542
283            0.532793
284            0.528105
285            0.529124
286            0.529096
292            0.527557
293            0.529254

In [266]:
TT01_y_class = pd.DataFrame(TT01, columns = ['PRODUCT_CODE'])
TT01_idx = TT01_y_class.index
TT01_y_class = TT01_y_class.reset_index()
TT01_prediction = pd.concat([TT01_prediction, TT01_y_class], axis = 1)
TT01_prediction = TT01_prediction.set_index('index')
TT01_prediction.drop(['PRODUCT_CODE'], axis = 1, inplace = True)

In [267]:
TT10_y_class = pd.DataFrame(TT10, columns = ['PRODUCT_CODE'])
TT10_idx = TT10_y_class.index
TT10_y_class = TT10_y_class.reset_index()
TT10_prediction = pd.concat([TT10_prediction, TT10_y_class], axis = 1)
TT10_prediction = TT10_prediction.set_index('index')
TT10_prediction.drop(['PRODUCT_CODE'], axis = 1, inplace = True)

In [247]:
from pycaret.classification import *

In [268]:
TT05_datas = TT05_prediction['prediction_label']
TT05_datas = pd.DataFrame(TT05_datas.values, columns = ['Y_Quality'])
TT05_datas

Y_Quality
0    0.525943
1    0.525411
2    0.521938
3    0.522096
4    0.526180
5    0.525393
6    0.525054
7    0.524952
8    0.525148
9    0.525239
10   0.524339
11   0.521960
12   0.523753
13   0.527840
14   0.529020
15   0.527244
16   0.529808
17   0.529269
18   0.529529
19   0.529455
20   0.530543
21   0.530630
22   0.529276
23   0.528569
24   0.529601
25   0.529305
26   0.529501
27   0.529763
28   0.539239
29   0.530105
30   0.530338
31   0.533000
32   0.529542
33   0.532793
34   0.528105
35   0.529124
36   0.529096
37   0.527557
38   0.529254

In [269]:
TT05y_idx= TT05_prediction.index
TT05y_idx = pd.DataFrame(TT05y_idx, columns = ['index'])
TT05_datas = pd.concat([TT05y_idx, TT05_datas], axis = 1)
TT05_datas = TT05_datas.set_index('index')
TT05_datas

Y_Quality
index           
7       0.525943
8       0.525411
14      0.521938
35      0.522096
41      0.526180
42      0.525393
52      0.525054
53      0.524952
54      0.525148
61      0.525239
64      0.524339
65      0.521960
66      0.523753
13      0.527840
36      0.529020
62      0.527244
63      0.529808
130     0.529269
131     0.529529
132     0.529455
248     0.530543
249     0.530630
250     0.529276
251     0.528569
252     0.529601
253     0.529305
254     0.529501
255     0.529763
260     0.539239
263     0.530105
280     0.530338
281     0.533000
282     0.529542
283     0.532793
284     0.528105
285     0.529124
286     0.529096
292     0.527557
293     0.529254

In [270]:
TT01_datas = TT01_prediction['prediction_label']
TT01_datas = pd.DataFrame(TT01_datas.values, columns = ['Y_Quality'])
TT01_datas

Y_Quality
0    0.524870
1    0.534387
2    0.533758
3    0.535029
4    0.546324
5    0.530239
6    0.516551
7    0.518399
8    0.518638
9    0.526151
10   0.526962
11   0.526794
12   0.524985
13   0.525460
14   0.530151
15   0.533284
16   0.532810
17   0.534897
18   0.519203
19   0.524432
20   0.530650
21   0.531134
22   0.531469
23   0.531514
24   0.532891
25   0.532567
26   0.529605
27   0.529951

In [271]:
TT01y_idx= TT01_prediction.index
TT01y_idx = pd.DataFrame(TT01y_idx, columns = ['index'])
TT01_datas = pd.concat([TT01y_idx, TT01_datas], axis = 1)
TT01_datas = TT01_datas.set_index('index')
TT01_datas

Y_Quality
index           
3       0.524870
6       0.534387
10      0.533758
11      0.535029
38      0.546324
40      0.530239
71      0.516551
86      0.518399
88      0.518638
89      0.526151
116     0.526962
117     0.526794
141     0.524985
142     0.525460
4       0.530151
5       0.533284
9       0.532810
12      0.534897
37      0.519203
39      0.524432
72      0.530650
79      0.531134
87      0.531469
109     0.531514
114     0.532891
115     0.532567
128     0.529605
129     0.529951

In [272]:
TT10_datas = TT10_prediction['prediction_label']
TT10_datas = pd.DataFrame(TT10_datas.values, columns = ['Y_Quality'])
TT10_datas

Y_Quality
0     0.532379
1     0.531925
2     0.527565
3     0.529364
4     0.529030
..         ...
238   0.529531
239   0.529191
240   0.529382
241   0.529476
242   0.529718

[243 rows x 1 columns]

In [273]:
TT10y_idx= TT10_prediction.index
TT10y_idx = pd.DataFrame(TT10y_idx, columns = ['index'])
TT10_datas = pd.concat([TT10y_idx, TT10_datas], axis = 1)
TT10_datas = TT10_datas.set_index('index')
TT10_datas

Y_Quality
index           
1       0.532379
2       0.531925
15      0.527565
17      0.529364
20      0.529030
...          ...
301     0.529531
305     0.529191
307     0.529382
308     0.529476
309     0.529718

[243 rows x 1 columns]

In [254]:
TT05_predictions = predict_model(T05_final_classification_model, data=TT05_datas)
TT01_predictions = predict_model(T01_final_classification_model, data=TT01_datas)
TT10_predictions = predict_model(T10_final_classification_model, data=TT10_datas)

In [278]:
TT05_predictions = T05_soft_vote.predict(TT05_datas)
TT01_predictions = T01_soft_vote.predict(TT01_datas)
TT10_predictions = T10_soft_vote.predict(TT10_datas)
TT05_predictions = pd.DataFrame(TT05_predictions, columns = ['prediction_label'])
TT01_predictions = pd.DataFrame(TT01_predictions, columns = ['prediction_label'])
TT10_predictions = pd.DataFrame(TT10_predictions, columns = ['prediction_label'])

In [279]:
TT05_idxf = TT05_datas.index
TT05_p = pd.DataFrame(TT05_idxf, columns = ['index'])
TT05_predictions = pd.concat([TT05_p, TT05_predictions], axis = 1)
TT05_predictions = TT05_predictions.set_index('index')
TT05_predictions

prediction_label
index                  
7                     1
8                     1
14                    0
35                    0
41                    1
42                    0
52                    0
53                    0
54                    0
61                    0
64                    0
65                    0
66                    0
13                    1
36                    1
62                    1
63                    1
130                   1
131                   1
132                   1
248                   1
249                   1
250                   1
251                   1
252                   1
253                   1
254                   1
255                   1
260                   2
263                   1
280                   1
281                   1
282                   1
283                   1
284                   1
285                   1
286                   1
292                   1
293                   1

In [280]:
TT01_idxf = TT01_datas.index
TT01_p = pd.DataFrame(TT01_idxf, columns = ['index'])
TT01_predictions = pd.concat([TT01_p, TT01_predictions], axis = 1)
TT01_predictions = TT01_predictions.set_index('index')
TT01_predictions

prediction_label
index                  
3                     0
6                     1
10                    1
11                    2
38                    2
40                    1
71                    0
86                    0
88                    0
89                    1
116                   1
117                   1
141                   0
142                   0
4                     1
5                     1
9                     1
12                    2
37                    0
39                    0
72                    1
79                    1
87                    1
109                   1
114                   1
115                   1
128                   1
129                   1

In [281]:
TT10_idxf = TT10_datas.index
TT10_p = pd.DataFrame(TT10_idxf, columns = ['index'])
TT10_predictions = pd.concat([TT10_p, TT10_predictions], axis = 1)
TT10_predictions = TT10_predictions.set_index('index')
TT10_predictions

prediction_label
index                  
1                     2
2                     1
15                    0
17                    1
20                    1
...                 ...
301                   1
305                   1
307                   1
308                   1
309                   1

[243 rows x 1 columns]

In [282]:
final_test = pd.concat([TT05_predictions, TT01_predictions, TT10_predictions])
final_test

prediction_label
index                  
7                     1
8                     1
14                    0
35                    0
41                    1
...                 ...
301                   1
305                   1
307                   1
308                   1
309                   1

[310 rows x 1 columns]

In [283]:
final_test = final_test.sort_index(ascending=True)
final_test['prediction_label']

index
0      1
1      2
2      1
3      0
4      1
      ..
305    1
306    1
307    1
308    1
309    1
Name: prediction_label, Length: 310, dtype: int64

In [287]:
#52
sample_submission = pd.read_csv('sample_submission.csv')
sample_submission['Y_Class'] = final_test['prediction_label']
display(sample_submission.head())
sample_submission.to_csv('line3_otherdrop_robust_regpyc_classpyc_fill0_voting_submission.csv',index=False)

PRODUCT_ID  Y_Class
0   TEST_000        1
1   TEST_001        2
2   TEST_002        1
3   TEST_003        0
4   TEST_004        1

In [288]:
final_test['prediction_label'].value_counts()

1    251
0     35
2     24
Name: prediction_label, dtype: int64

In [289]:
np.array(final_test['prediction_label'])

array([1, 2, 1, 0, 1, 1, 1, 1, 1, 1, 1, 2, 2, 1, 0, 0, 1, 1, 1, 1, 1, 1,
       0, 1, 1, 1, 1, 0, 0, 1, 0, 1, 1, 1, 1, 0, 1, 0, 2, 0, 1, 1, 0, 0,
       1, 1, 1, 0, 1, 0, 1, 0, 0, 0, 0, 0, 1, 1, 0, 0, 0, 0, 1, 1, 0, 0,
       0, 1, 1, 1, 1, 0, 1, 1, 1, 1, 1, 1, 2, 1, 1, 1, 1, 1, 1, 1, 0, 1,
       0, 1, 2, 1, 2, 2, 1, 2, 1, 1, 1, 1, 1, 2, 1, 1, 1, 1, 1, 1, 2, 1,
       1, 1, 1, 2, 1, 1, 1, 1, 1, 2, 1, 1, 1, 1, 1, 1, 2, 1, 1, 1, 1, 1,
       1, 1, 2, 2, 1, 2, 1, 1, 1, 0, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 2, 2, 1, 2, 1, 1, 1, 1, 1, 1, 1, 1, 2, 1, 1, 1,
       1, 1, 1, 2, 1, 1, 1, 2, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 1, 1, 1, 1, 0, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 2, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 0, 1, 1, 1, 1, 1, 1, 0, 1, 1, 1, 1, 1, 1,